In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.cm
import seaborn as sns
from IPython.display import display
import datetime
import numpy as np
from statsmodels import robust

In [2]:
# Percentage of nulls per column
def null_ratio(df):
        null_count = df.isnull().sum()
        null_percent = 100 * df.isnull().sum()/len(df)
        null_table = pd.concat([null_count, null_percent], axis=1)
        null_table = null_table.rename(columns = {0 : 'Null Count', 1 : 'Null Percent'})
        return null_table.sort_values('Null Percent', ascending=0)

In [3]:
def return_all_rows(x):
    pd.set_option('display.max_rows', len(x))
    return x
    pd.reset_option('display.max_rows')
    
def return_all_columns(x):
    pd.set_option('display.max_columns', len(x))
    return x.head(5)
    pd.reset_option('display.max_columns')

In [4]:
def overview(df):
    print("Number of columns:", len(df.columns))
    print("Number of rows:", len(df.index))
    df.head(5)

In [5]:
def drop_dups(df):
    # list comprehension of the cols that end with '_y'
    y_drop = [x for x in df if x.endswith('_y')]
    df.drop(y_drop, axis=1, inplace=True)

In [6]:
def floatToString(inputValue):
    result = ('%.15f' % inputValue).rstrip('0').rstrip('.')
    return '0' if result == '-0' else result

In [7]:
def mad(arr):
    """ 
    Get Median Absolute Deviation and multiple by 1.486 to mimic standard deviation
        https://www.ibm.com/support/knowledgecenter/SSWLVY_1.0.0/com.ibm.spss.analyticcatalyst.help/analytic_catalyst/modified_z.html
    Median Absolute Deviation: a "Robust" version of standard deviation.
        Indices variabililty of the sample.
        https://en.wikipedia.org/wiki/Median_absolute_deviation
    """
    arr = np.ma.array(arr).compressed() # should be faster to not use masked arrays.
    med = np.nanmedian(arr)
    mad = np.nanmedian(np.abs(arr - med))
    # Multiply coefficient by 1.486 to mimic Standard Deviation (source: IBM)
    return 1.486 * mad

In [8]:
def meanad(arr):
    """ 
    Get Mean Absolute Deviation and multiple by 1.253314 to mimic standard deviation
        https://www.ibm.com/support/knowledgecenter/SSWLVY_1.0.0/com.ibm.spss.analyticcatalyst.help/analytic_catalyst/modified_z.html
    Mean Absolute Deviation: a "Robust" version of standard deviation.
        Indices variabililty of the sample.
        https://en.wikipedia.org/wiki/Mean_absolute_deviation
    """
    arr = np.ma.array(arr).compressed() # should be faster to not use masked arrays.
    med = np.nanmedian(arr)
    mad = np.nanmean(np.abs(arr - med))
    # Multiply coefficient by 1.253314 to mimic Standard Deviation (source: IBM)
    return 1.253314 * mad

In [9]:
# Load financial suite from Wharton
df = pd.read_csv('c:/users/shane/Desktop/W205_Final/sample_data/Sample_Financial_Ratios_Firm_Level.csv')

In [10]:
# Import link table
link_table = pd.read_csv('c:/users/shane/Desktop/W205_Final/sample_data/Sample_CRSP_Compustat_Merged_Linking_Table.csv')

In [11]:
link_table['LINKENDDT'] = link_table['LINKENDDT'].str.replace('E','20200101').astype(int)

In [12]:
link_table['LPERMNO'] = link_table['LPERMNO'].astype(object)

In [13]:
# Add additional time based columns
link_table['LINKDT'] = pd.to_datetime(link_table['LINKDT'], format='%Y%m%d')
link_table['LINKENDDT'] = pd.to_datetime(link_table['LINKENDDT'], format='%Y%m%d')

In [14]:
df = pd.merge(df, link_table, on='gvkey', how='left', suffixes=('', '_y'))

In [15]:
# Add additional time based columns
df['public_date'] = pd.to_datetime(df['public_date'])

# Create year
df['year'] = df['public_date'].dt.year

# Create month
df['month'] = df['public_date'].dt.month

df["year-month"] = df['public_date'].apply(lambda x: x.strftime('%Y-%m'))

In [16]:
# Create Unique Identifier for links from other databases for specific date-time
df["GVKEY-year-month"] = df["gvkey"].map(str) + "-" + df["year-month"]
df["CUSIP-year-month"] = df["cusip"].map(str) + "-" + df["year-month"]
df["TIC-year-month"] = df["tic"].map(str) + "-" + df["year-month"]
df["PERMNO-year-month"] = df["LPERMNO"].map(str) + "-" + df["year-month"]

In [17]:
df = df[(df.public_date >= df.LINKDT) & (df.public_date <= df.LINKENDDT)]

In [18]:
# Load CRSP/Compustat Merged Database - Security Monthly from Wharton
CRSP_comp_merge = pd.read_csv('c:/users/shane/desktop/W205_Final/sample_data/Sample_CRSP_Compustat_Merged_Security_Monthly.csv', low_memory=False)

In [19]:
# Convert time
CRSP_comp_merge['datadate'] = pd.to_datetime(CRSP_comp_merge['datadate'])

# Create year
CRSP_comp_merge['year'] = CRSP_comp_merge['datadate'].dt.year

# Create month
CRSP_comp_merge['month'] = CRSP_comp_merge['datadate'].dt.month

# Create year-month for indexing
CRSP_comp_merge["year-month"] = CRSP_comp_merge['datadate'].apply(lambda x: x.strftime('%Y-%m'))

In [20]:
# Sort by date and GVKEY
CRSP_comp_merge = CRSP_comp_merge.sort_values(by=['GVKEY','datadate'], ascending=[True,True])

In [21]:
# Forward (PRCCM -- Price - Close - Monthly) 1 – 36 months
CRSP_comp_merge['forward_one_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-1)

CRSP_comp_merge['forward_two_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-2)

CRSP_comp_merge['forward_three_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-3)

CRSP_comp_merge['forward_four_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-4)

CRSP_comp_merge['forward_five_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-5)

CRSP_comp_merge['forward_six_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-6)

CRSP_comp_merge['forward_seven_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-7)

CRSP_comp_merge['forward_eight_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-8)

CRSP_comp_merge['forward_nine_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-9)

CRSP_comp_merge['forward_ten_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-10)

CRSP_comp_merge['forward_eleven_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-11)

CRSP_comp_merge['forward_twelve_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-12)

CRSP_comp_merge['forward_thirteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-13)

CRSP_comp_merge['forward_fourteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-14)

CRSP_comp_merge['forward_fifteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-15)

CRSP_comp_merge['forward_sixteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-16)

CRSP_comp_merge['forward_seventeen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-17)

CRSP_comp_merge['forward_eighteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-18)

CRSP_comp_merge['forward_nineteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-19)

CRSP_comp_merge['forward_twenty_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-20)

CRSP_comp_merge['forward_twentyone_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-21)

CRSP_comp_merge['forward_twentytwo_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-22)

CRSP_comp_merge['forward_twentythree_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-23)

CRSP_comp_merge['forward_twentyfour_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-24)

CRSP_comp_merge['forward_twentyfive_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-25)

CRSP_comp_merge['forward_twentysix_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-26)

CRSP_comp_merge['forward_twentyseven_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-27)

CRSP_comp_merge['forward_twentyeight_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-28)

CRSP_comp_merge['forward_twentynine_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-29)

CRSP_comp_merge['forward_thirty_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-30)

CRSP_comp_merge['forward_thirtyone_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-31)

CRSP_comp_merge['forward_thirtytwo_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-32)

CRSP_comp_merge['forward_thirtythree_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-33)

CRSP_comp_merge['forward_thirtyfour_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-34)

CRSP_comp_merge['forward_thirtyfive_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-35)

CRSP_comp_merge['forward_thirtysix_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(-36)


# Forward (AJEXM -- Cumulative Adjustment Factor - Ex Date -Monthly) 1 – 36 months
CRSP_comp_merge['forward_one_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-1)

CRSP_comp_merge['forward_two_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-2)

CRSP_comp_merge['forward_three_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-3)

CRSP_comp_merge['forward_four_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-4)

CRSP_comp_merge['forward_five_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-5)

CRSP_comp_merge['forward_six_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-6)

CRSP_comp_merge['forward_seven_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-7)

CRSP_comp_merge['forward_eight_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-8)

CRSP_comp_merge['forward_nine_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-9)

CRSP_comp_merge['forward_ten_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-10)

CRSP_comp_merge['forward_eleven_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-11)

CRSP_comp_merge['forward_twelve_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-12)

CRSP_comp_merge['forward_thirteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-13)

CRSP_comp_merge['forward_fourteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-14)

CRSP_comp_merge['forward_fifteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-15)

CRSP_comp_merge['forward_sixteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-16)

CRSP_comp_merge['forward_seventeen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-17)

CRSP_comp_merge['forward_eighteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-18)

CRSP_comp_merge['forward_nineteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-19)

CRSP_comp_merge['forward_twenty_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-20)

CRSP_comp_merge['forward_twentyone_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-21)

CRSP_comp_merge['forward_twentytwo_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-22)

CRSP_comp_merge['forward_twentythree_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-23)

CRSP_comp_merge['forward_twentyfour_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-24)

CRSP_comp_merge['forward_twentyfive_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-25)

CRSP_comp_merge['forward_twentysix_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-26)

CRSP_comp_merge['forward_twentyseven_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-27)

CRSP_comp_merge['forward_twentyeight_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-28)

CRSP_comp_merge['forward_twentynine_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-29)

CRSP_comp_merge['forward_thirty_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-30)

CRSP_comp_merge['forward_thirtyone_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-31)

CRSP_comp_merge['forward_thirtytwo_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-32)

CRSP_comp_merge['forward_thirtythree_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-33)

CRSP_comp_merge['forward_thirtyfour_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-34)

CRSP_comp_merge['forward_thirtyfive_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-35)

CRSP_comp_merge['forward_thirtysix_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(-36)


# Forward (TRFM -- Monthly Total Return Factor) 1 – 36 months
CRSP_comp_merge['forward_one_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-1)

CRSP_comp_merge['forward_two_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-2)

CRSP_comp_merge['forward_three_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-3)

CRSP_comp_merge['forward_four_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-4)

CRSP_comp_merge['forward_five_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-5)

CRSP_comp_merge['forward_six_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-6)

CRSP_comp_merge['forward_seven_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-7)

CRSP_comp_merge['forward_eight_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-8)

CRSP_comp_merge['forward_nine_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-9)

CRSP_comp_merge['forward_ten_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-10)

CRSP_comp_merge['forward_eleven_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-11)

CRSP_comp_merge['forward_twelve_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-12)

CRSP_comp_merge['forward_thirteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-13)

CRSP_comp_merge['forward_fourteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-14)

CRSP_comp_merge['forward_fifteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-15)

CRSP_comp_merge['forward_sixteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-16)

CRSP_comp_merge['forward_seventeen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-17)

CRSP_comp_merge['forward_eighteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-18)

CRSP_comp_merge['forward_nineteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-19)

CRSP_comp_merge['forward_twenty_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-20)

CRSP_comp_merge['forward_twentyone_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-21)

CRSP_comp_merge['forward_twentytwo_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-22)

CRSP_comp_merge['forward_twentythree_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-23)

CRSP_comp_merge['forward_twentyfour_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-24)

CRSP_comp_merge['forward_twentyfive_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-25)

CRSP_comp_merge['forward_twentysix_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-26)

CRSP_comp_merge['forward_twentyseven_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-27)

CRSP_comp_merge['forward_twentyeight_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-28)

CRSP_comp_merge['forward_twentynine_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-29)

CRSP_comp_merge['forward_thirty_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-30)

CRSP_comp_merge['forward_thirtyone_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-31)

CRSP_comp_merge['forward_thirtytwo_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-32)

CRSP_comp_merge['forward_thirtythree_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-33)

CRSP_comp_merge['forward_thirtyfour_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-34)

CRSP_comp_merge['forward_thirtyfive_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-35)

CRSP_comp_merge['forward_thirtysix_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(-36)


# Forward Return over x number of months (1 - 36)
CRSP_comp_merge['forward_one_month_return'] = ((((CRSP_comp_merge['forward_one_month_prccm']/CRSP_comp_merge['forward_one_month_ajexm'])*CRSP_comp_merge['forward_one_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_two_month_return'] = ((((CRSP_comp_merge['forward_two_month_prccm']/CRSP_comp_merge['forward_two_month_ajexm'])*CRSP_comp_merge['forward_two_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_three_month_return'] = ((((CRSP_comp_merge['forward_three_month_prccm']/CRSP_comp_merge['forward_three_month_ajexm'])*CRSP_comp_merge['forward_three_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_four_month_return'] = ((((CRSP_comp_merge['forward_four_month_prccm']/CRSP_comp_merge['forward_four_month_ajexm'])*CRSP_comp_merge['forward_four_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_five_month_return'] = ((((CRSP_comp_merge['forward_five_month_prccm']/CRSP_comp_merge['forward_five_month_ajexm'])*CRSP_comp_merge['forward_five_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_six_month_return'] = ((((CRSP_comp_merge['forward_six_month_prccm']/CRSP_comp_merge['forward_six_month_ajexm'])*CRSP_comp_merge['forward_six_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_seven_month_return'] = ((((CRSP_comp_merge['forward_seven_month_prccm']/CRSP_comp_merge['forward_seven_month_ajexm'])*CRSP_comp_merge['forward_seven_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_eight_month_return'] = ((((CRSP_comp_merge['forward_eight_month_prccm']/CRSP_comp_merge['forward_eight_month_ajexm'])*CRSP_comp_merge['forward_eight_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_nine_month_return'] = ((((CRSP_comp_merge['forward_nine_month_prccm']/CRSP_comp_merge['forward_nine_month_ajexm'])*CRSP_comp_merge['forward_nine_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_ten_month_return'] = ((((CRSP_comp_merge['forward_ten_month_prccm']/CRSP_comp_merge['forward_ten_month_ajexm'])*CRSP_comp_merge['forward_ten_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_eleven_month_return'] = ((((CRSP_comp_merge['forward_eleven_month_prccm']/CRSP_comp_merge['forward_eleven_month_ajexm'])*CRSP_comp_merge['forward_eleven_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twelve_month_return'] = ((((CRSP_comp_merge['forward_twelve_month_prccm']/CRSP_comp_merge['forward_twelve_month_ajexm'])*CRSP_comp_merge['forward_twelve_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_thirteen_month_return'] = ((((CRSP_comp_merge['forward_thirteen_month_prccm']/CRSP_comp_merge['forward_thirteen_month_ajexm'])*CRSP_comp_merge['forward_thirteen_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_fourteen_month_return'] = ((((CRSP_comp_merge['forward_fourteen_month_prccm']/CRSP_comp_merge['forward_fourteen_month_ajexm'])*CRSP_comp_merge['forward_fourteen_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_fifteen_month_return'] = ((((CRSP_comp_merge['forward_fifteen_month_prccm']/CRSP_comp_merge['forward_fifteen_month_ajexm'])*CRSP_comp_merge['forward_fifteen_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_sixteen_month_return'] = ((((CRSP_comp_merge['forward_sixteen_month_prccm']/CRSP_comp_merge['forward_sixteen_month_ajexm'])*CRSP_comp_merge['forward_sixteen_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_seventeen_month_return'] = ((((CRSP_comp_merge['forward_seventeen_month_prccm']/CRSP_comp_merge['forward_seventeen_month_ajexm'])*CRSP_comp_merge['forward_seventeen_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_eighteen_month_return'] = ((((CRSP_comp_merge['forward_eighteen_month_prccm']/CRSP_comp_merge['forward_eighteen_month_ajexm'])*CRSP_comp_merge['forward_eighteen_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_nineteen_month_return'] = ((((CRSP_comp_merge['forward_nineteen_month_prccm']/CRSP_comp_merge['forward_nineteen_month_ajexm'])*CRSP_comp_merge['forward_nineteen_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twenty_month_return'] = ((((CRSP_comp_merge['forward_twenty_month_prccm']/CRSP_comp_merge['forward_twenty_month_ajexm'])*CRSP_comp_merge['forward_twenty_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twentyone_month_return'] = ((((CRSP_comp_merge['forward_twentyone_month_prccm']/CRSP_comp_merge['forward_twentyone_month_ajexm'])*CRSP_comp_merge['forward_twentyone_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twentytwo_month_return'] = ((((CRSP_comp_merge['forward_twentytwo_month_prccm']/CRSP_comp_merge['forward_twentytwo_month_ajexm'])*CRSP_comp_merge['forward_twentytwo_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twentythree_month_return'] = ((((CRSP_comp_merge['forward_twentythree_month_prccm']/CRSP_comp_merge['forward_twentythree_month_ajexm'])*CRSP_comp_merge['forward_twentythree_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twentyfour_month_return'] = ((((CRSP_comp_merge['forward_twentyfour_month_prccm']/CRSP_comp_merge['forward_twentyfour_month_ajexm'])*CRSP_comp_merge['forward_twentyfour_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twentyfive_month_return'] = ((((CRSP_comp_merge['forward_twentyfive_month_prccm']/CRSP_comp_merge['forward_twentyfive_month_ajexm'])*CRSP_comp_merge['forward_twentyfive_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twentysix_month_return'] = ((((CRSP_comp_merge['forward_twentysix_month_prccm']/CRSP_comp_merge['forward_twentysix_month_ajexm'])*CRSP_comp_merge['forward_twentysix_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twentyseven_month_return'] = ((((CRSP_comp_merge['forward_twentyseven_month_prccm']/CRSP_comp_merge['forward_twentyseven_month_ajexm'])*CRSP_comp_merge['forward_twentyseven_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twentyeight_month_return'] = ((((CRSP_comp_merge['forward_twentyeight_month_prccm']/CRSP_comp_merge['forward_twentyeight_month_ajexm'])*CRSP_comp_merge['forward_twentyeight_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_twentynine_month_return'] = ((((CRSP_comp_merge['forward_twentynine_month_prccm']/CRSP_comp_merge['forward_twentynine_month_ajexm'])*CRSP_comp_merge['forward_twentynine_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_thirty_month_return'] = ((((CRSP_comp_merge['forward_thirty_month_prccm']/CRSP_comp_merge['forward_thirty_month_ajexm'])*CRSP_comp_merge['forward_thirty_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_thirtyone_month_return'] = ((((CRSP_comp_merge['forward_thirtyone_month_prccm']/CRSP_comp_merge['forward_thirtyone_month_ajexm'])*CRSP_comp_merge['forward_thirtyone_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_thirtytwo_month_return'] = ((((CRSP_comp_merge['forward_thirtytwo_month_prccm']/CRSP_comp_merge['forward_thirtytwo_month_ajexm'])*CRSP_comp_merge['forward_thirtytwo_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_thirtythree_month_return'] = ((((CRSP_comp_merge['forward_thirtythree_month_prccm']/CRSP_comp_merge['forward_thirtythree_month_ajexm'])*CRSP_comp_merge['forward_thirtythree_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_thirtyfour_month_return'] = ((((CRSP_comp_merge['forward_thirtyfour_month_prccm']/CRSP_comp_merge['forward_thirtyfour_month_ajexm'])*CRSP_comp_merge['forward_thirtyfour_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_thirtyfive_month_return'] = ((((CRSP_comp_merge['forward_thirtyfive_month_prccm']/CRSP_comp_merge['forward_thirtyfive_month_ajexm'])*CRSP_comp_merge['forward_thirtyfive_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

CRSP_comp_merge['forward_thirtysix_month_return'] = ((((CRSP_comp_merge['forward_thirtysix_month_prccm']/CRSP_comp_merge['forward_thirtysix_month_ajexm'])*CRSP_comp_merge['forward_thirtysix_month_trfm'])/((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['trfm']))-1)*100

In [22]:
# Past (PRCCM -- Price - Close - Monthly) 1 – 36 months
CRSP_comp_merge['past_one_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(1)

CRSP_comp_merge['past_two_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(2)

CRSP_comp_merge['past_three_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(3)

CRSP_comp_merge['past_four_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(4)

CRSP_comp_merge['past_five_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(5)

CRSP_comp_merge['past_six_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(6)

CRSP_comp_merge['past_seven_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(7)

CRSP_comp_merge['past_eight_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(8)

CRSP_comp_merge['past_nine_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(9)

CRSP_comp_merge['past_ten_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(10)

CRSP_comp_merge['past_eleven_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(11)

CRSP_comp_merge['past_twelve_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(12)

CRSP_comp_merge['past_thirteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(13)

CRSP_comp_merge['past_fourteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(14)

CRSP_comp_merge['past_fifteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(15)

CRSP_comp_merge['past_sixteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(16)

CRSP_comp_merge['past_seventeen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(17)

CRSP_comp_merge['past_eighteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(18)

CRSP_comp_merge['past_nineteen_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(19)

CRSP_comp_merge['past_twenty_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(20)

CRSP_comp_merge['past_twentyone_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(21)

CRSP_comp_merge['past_twentytwo_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(22)

CRSP_comp_merge['past_twentythree_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(23)

CRSP_comp_merge['past_twentyfour_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(24)

CRSP_comp_merge['past_twentyfive_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(25)

CRSP_comp_merge['past_twentysix_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(26)

CRSP_comp_merge['past_twentyseven_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(27)

CRSP_comp_merge['past_twentyeight_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(28)

CRSP_comp_merge['past_twentynine_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(29)

CRSP_comp_merge['past_thirty_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(30)

CRSP_comp_merge['past_thirtyone_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(31)

CRSP_comp_merge['past_thirtytwo_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(32)

CRSP_comp_merge['past_thirtythree_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(33)

CRSP_comp_merge['past_thirtyfour_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(34)

CRSP_comp_merge['past_thirtyfive_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(35)

CRSP_comp_merge['past_thirtysix_month_prccm'] = CRSP_comp_merge.groupby('GVKEY')['prccm'].shift(36)


# Past (AJEXM -- Cumulative Adjustment Factor - Ex Date -Monthly) 1 – 36 months
CRSP_comp_merge['past_one_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(1)

CRSP_comp_merge['past_two_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(2)

CRSP_comp_merge['past_three_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(3)

CRSP_comp_merge['past_four_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(4)

CRSP_comp_merge['past_five_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(5)

CRSP_comp_merge['past_six_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(6)

CRSP_comp_merge['past_seven_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(7)

CRSP_comp_merge['past_eight_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(8)

CRSP_comp_merge['past_nine_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(9)

CRSP_comp_merge['past_ten_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(10)

CRSP_comp_merge['past_eleven_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(11)

CRSP_comp_merge['past_twelve_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(12)

CRSP_comp_merge['past_thirteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(13)

CRSP_comp_merge['past_fourteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(14)

CRSP_comp_merge['past_fifteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(15)

CRSP_comp_merge['past_sixteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(16)

CRSP_comp_merge['past_seventeen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(17)

CRSP_comp_merge['past_eighteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(18)

CRSP_comp_merge['past_nineteen_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(19)

CRSP_comp_merge['past_twenty_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(20)

CRSP_comp_merge['past_twentyone_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(21)

CRSP_comp_merge['past_twentytwo_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(22)

CRSP_comp_merge['past_twentythree_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(23)

CRSP_comp_merge['past_twentyfour_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(24)

CRSP_comp_merge['past_twentyfive_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(25)

CRSP_comp_merge['past_twentysix_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(26)

CRSP_comp_merge['past_twentyseven_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(27)

CRSP_comp_merge['past_twentyeight_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(28)

CRSP_comp_merge['past_twentynine_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(29)

CRSP_comp_merge['past_thirty_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(30)

CRSP_comp_merge['past_thirtyone_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(31)

CRSP_comp_merge['past_thirtytwo_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(32)

CRSP_comp_merge['past_thirtythree_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(33)

CRSP_comp_merge['past_thirtyfour_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(34)

CRSP_comp_merge['past_thirtyfive_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(35)

CRSP_comp_merge['past_thirtysix_month_ajexm'] = CRSP_comp_merge.groupby('GVKEY')['ajexm'].shift(36)


# Past (TRFM -- Monthly Total Return Factor) 1 – 36 months
CRSP_comp_merge['past_one_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(1)

CRSP_comp_merge['past_two_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(2)

CRSP_comp_merge['past_three_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(3)

CRSP_comp_merge['past_four_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(4)

CRSP_comp_merge['past_five_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(5)

CRSP_comp_merge['past_six_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(6)

CRSP_comp_merge['past_seven_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(7)

CRSP_comp_merge['past_eight_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(8)

CRSP_comp_merge['past_nine_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(9)

CRSP_comp_merge['past_ten_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(10)

CRSP_comp_merge['past_eleven_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(11)

CRSP_comp_merge['past_twelve_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(12)

CRSP_comp_merge['past_thirteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(13)

CRSP_comp_merge['past_fourteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(14)

CRSP_comp_merge['past_fifteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(15)

CRSP_comp_merge['past_sixteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(16)

CRSP_comp_merge['past_seventeen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(17)

CRSP_comp_merge['past_eighteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(18)

CRSP_comp_merge['past_nineteen_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(19)

CRSP_comp_merge['past_twenty_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(20)

CRSP_comp_merge['past_twentyone_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(21)

CRSP_comp_merge['past_twentytwo_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(22)

CRSP_comp_merge['past_twentythree_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(23)

CRSP_comp_merge['past_twentyfour_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(24)

CRSP_comp_merge['past_twentyfive_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(25)

CRSP_comp_merge['past_twentysix_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(26)

CRSP_comp_merge['past_twentyseven_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(27)

CRSP_comp_merge['past_twentyeight_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(28)

CRSP_comp_merge['past_twentynine_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(29)

CRSP_comp_merge['past_thirty_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(30)

CRSP_comp_merge['past_thirtyone_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(31)

CRSP_comp_merge['past_thirtytwo_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(32)

CRSP_comp_merge['past_thirtythree_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(33)

CRSP_comp_merge['past_thirtyfour_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(34)

CRSP_comp_merge['past_thirtyfive_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(35)

CRSP_comp_merge['past_thirtysix_month_trfm'] = CRSP_comp_merge.groupby('GVKEY')['trfm'].shift(36)


# Past Return over x number of months (1 - 36)
CRSP_comp_merge['past_one_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_one_month_trfm'])/((CRSP_comp_merge['past_one_month_prccm']/CRSP_comp_merge['past_one_month_ajexm'])*CRSP_comp_merge['past_one_month_trfm']))-1)*100

CRSP_comp_merge['past_two_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_two_month_trfm'])/((CRSP_comp_merge['past_two_month_prccm']/CRSP_comp_merge['past_two_month_ajexm'])*CRSP_comp_merge['past_two_month_trfm']))-1)*100

CRSP_comp_merge['past_three_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_three_month_trfm'])/((CRSP_comp_merge['past_three_month_prccm']/CRSP_comp_merge['past_three_month_ajexm'])*CRSP_comp_merge['past_three_month_trfm']))-1)*100

CRSP_comp_merge['past_four_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_four_month_trfm'])/((CRSP_comp_merge['past_four_month_prccm']/CRSP_comp_merge['past_four_month_ajexm'])*CRSP_comp_merge['past_four_month_trfm']))-1)*100

CRSP_comp_merge['past_five_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_five_month_trfm'])/((CRSP_comp_merge['past_five_month_prccm']/CRSP_comp_merge['past_five_month_ajexm'])*CRSP_comp_merge['past_five_month_trfm']))-1)*100

CRSP_comp_merge['past_six_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_six_month_trfm'])/((CRSP_comp_merge['past_six_month_prccm']/CRSP_comp_merge['past_six_month_ajexm'])*CRSP_comp_merge['past_six_month_trfm']))-1)*100

CRSP_comp_merge['past_seven_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_seven_month_trfm'])/((CRSP_comp_merge['past_seven_month_prccm']/CRSP_comp_merge['past_seven_month_ajexm'])*CRSP_comp_merge['past_seven_month_trfm']))-1)*100

CRSP_comp_merge['past_eight_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_eight_month_trfm'])/((CRSP_comp_merge['past_eight_month_prccm']/CRSP_comp_merge['past_eight_month_ajexm'])*CRSP_comp_merge['past_eight_month_trfm']))-1)*100

CRSP_comp_merge['past_nine_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_nine_month_trfm'])/((CRSP_comp_merge['past_nine_month_prccm']/CRSP_comp_merge['past_nine_month_ajexm'])*CRSP_comp_merge['past_nine_month_trfm']))-1)*100

CRSP_comp_merge['past_ten_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_ten_month_trfm'])/((CRSP_comp_merge['past_ten_month_prccm']/CRSP_comp_merge['past_ten_month_ajexm'])*CRSP_comp_merge['past_ten_month_trfm']))-1)*100

CRSP_comp_merge['past_eleven_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_eleven_month_trfm'])/((CRSP_comp_merge['past_eleven_month_prccm']/CRSP_comp_merge['past_eleven_month_ajexm'])*CRSP_comp_merge['past_eleven_month_trfm']))-1)*100

CRSP_comp_merge['past_twelve_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twelve_month_trfm'])/((CRSP_comp_merge['past_twelve_month_prccm']/CRSP_comp_merge['past_twelve_month_ajexm'])*CRSP_comp_merge['past_twelve_month_trfm']))-1)*100

CRSP_comp_merge['past_thirteen_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_thirteen_month_trfm'])/((CRSP_comp_merge['past_thirteen_month_prccm']/CRSP_comp_merge['past_thirteen_month_ajexm'])*CRSP_comp_merge['past_thirteen_month_trfm']))-1)*100

CRSP_comp_merge['past_fourteen_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_fourteen_month_trfm'])/((CRSP_comp_merge['past_fourteen_month_prccm']/CRSP_comp_merge['past_fourteen_month_ajexm'])*CRSP_comp_merge['past_fourteen_month_trfm']))-1)*100

CRSP_comp_merge['past_fifteen_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_fifteen_month_trfm'])/((CRSP_comp_merge['past_fifteen_month_prccm']/CRSP_comp_merge['past_fifteen_month_ajexm'])*CRSP_comp_merge['past_fifteen_month_trfm']))-1)*100

CRSP_comp_merge['past_sixteen_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_sixteen_month_trfm'])/((CRSP_comp_merge['past_sixteen_month_prccm']/CRSP_comp_merge['past_sixteen_month_ajexm'])*CRSP_comp_merge['past_sixteen_month_trfm']))-1)*100

CRSP_comp_merge['past_seventeen_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_seventeen_month_trfm'])/((CRSP_comp_merge['past_seventeen_month_prccm']/CRSP_comp_merge['past_seventeen_month_ajexm'])*CRSP_comp_merge['past_seventeen_month_trfm']))-1)*100

CRSP_comp_merge['past_eighteen_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_eighteen_month_trfm'])/((CRSP_comp_merge['past_eighteen_month_prccm']/CRSP_comp_merge['past_eighteen_month_ajexm'])*CRSP_comp_merge['past_eighteen_month_trfm']))-1)*100

CRSP_comp_merge['past_nineteen_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_nineteen_month_trfm'])/((CRSP_comp_merge['past_nineteen_month_prccm']/CRSP_comp_merge['past_nineteen_month_ajexm'])*CRSP_comp_merge['past_nineteen_month_trfm']))-1)*100

CRSP_comp_merge['past_twenty_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twenty_month_trfm'])/((CRSP_comp_merge['past_twenty_month_prccm']/CRSP_comp_merge['past_twenty_month_ajexm'])*CRSP_comp_merge['past_twenty_month_trfm']))-1)*100

CRSP_comp_merge['past_twentyone_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twentyone_month_trfm'])/((CRSP_comp_merge['past_twentyone_month_prccm']/CRSP_comp_merge['past_twentyone_month_ajexm'])*CRSP_comp_merge['past_twentyone_month_trfm']))-1)*100

CRSP_comp_merge['past_twentytwo_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twentytwo_month_trfm'])/((CRSP_comp_merge['past_twentytwo_month_prccm']/CRSP_comp_merge['past_twentytwo_month_ajexm'])*CRSP_comp_merge['past_twentytwo_month_trfm']))-1)*100

CRSP_comp_merge['past_twentythree_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twentythree_month_trfm'])/((CRSP_comp_merge['past_twentythree_month_prccm']/CRSP_comp_merge['past_twentythree_month_ajexm'])*CRSP_comp_merge['past_twentythree_month_trfm']))-1)*100

CRSP_comp_merge['past_twentyfour_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twentyfour_month_trfm'])/((CRSP_comp_merge['past_twentyfour_month_prccm']/CRSP_comp_merge['past_twentyfour_month_ajexm'])*CRSP_comp_merge['past_twentyfour_month_trfm']))-1)*100

CRSP_comp_merge['past_twentyfive_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twentyfive_month_trfm'])/((CRSP_comp_merge['past_twentyfive_month_prccm']/CRSP_comp_merge['past_twentyfive_month_ajexm'])*CRSP_comp_merge['past_twentyfive_month_trfm']))-1)*100

CRSP_comp_merge['past_twentysix_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twentysix_month_trfm'])/((CRSP_comp_merge['past_twentysix_month_prccm']/CRSP_comp_merge['past_twentysix_month_ajexm'])*CRSP_comp_merge['past_twentysix_month_trfm']))-1)*100

CRSP_comp_merge['past_twentyseven_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twentyseven_month_trfm'])/((CRSP_comp_merge['past_twentyseven_month_prccm']/CRSP_comp_merge['past_twentyseven_month_ajexm'])*CRSP_comp_merge['past_twentyseven_month_trfm']))-1)*100

CRSP_comp_merge['past_twentyeight_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twentyeight_month_trfm'])/((CRSP_comp_merge['past_twentyeight_month_prccm']/CRSP_comp_merge['past_twentyeight_month_ajexm'])*CRSP_comp_merge['past_twentyeight_month_trfm']))-1)*100

CRSP_comp_merge['past_twentynine_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_twentynine_month_trfm'])/((CRSP_comp_merge['past_twentynine_month_prccm']/CRSP_comp_merge['past_twentynine_month_ajexm'])*CRSP_comp_merge['past_twentynine_month_trfm']))-1)*100

CRSP_comp_merge['past_thirty_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_thirty_month_trfm'])/((CRSP_comp_merge['past_thirty_month_prccm']/CRSP_comp_merge['past_thirty_month_ajexm'])*CRSP_comp_merge['past_thirty_month_trfm']))-1)*100

CRSP_comp_merge['past_thirtyone_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_thirtyone_month_trfm'])/((CRSP_comp_merge['past_thirtyone_month_prccm']/CRSP_comp_merge['past_thirtyone_month_ajexm'])*CRSP_comp_merge['past_thirtyone_month_trfm']))-1)*100

CRSP_comp_merge['past_thirtytwo_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_thirtytwo_month_trfm'])/((CRSP_comp_merge['past_thirtytwo_month_prccm']/CRSP_comp_merge['past_thirtytwo_month_ajexm'])*CRSP_comp_merge['past_thirtytwo_month_trfm']))-1)*100

CRSP_comp_merge['past_thirtythree_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_thirtythree_month_trfm'])/((CRSP_comp_merge['past_thirtythree_month_prccm']/CRSP_comp_merge['past_thirtythree_month_ajexm'])*CRSP_comp_merge['past_thirtythree_month_trfm']))-1)*100

CRSP_comp_merge['past_thirtyfour_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_thirtyfour_month_trfm'])/((CRSP_comp_merge['past_thirtyfour_month_prccm']/CRSP_comp_merge['past_thirtyfour_month_ajexm'])*CRSP_comp_merge['past_thirtyfour_month_trfm']))-1)*100

CRSP_comp_merge['past_thirtyfive_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_thirtyfive_month_trfm'])/((CRSP_comp_merge['past_thirtyfive_month_prccm']/CRSP_comp_merge['past_thirtyfive_month_ajexm'])*CRSP_comp_merge['past_thirtyfive_month_trfm']))-1)*100

CRSP_comp_merge['past_thirtysix_month_return'] = ((((CRSP_comp_merge['prccm']/CRSP_comp_merge['ajexm'])*CRSP_comp_merge['past_thirtysix_month_trfm'])/((CRSP_comp_merge['past_thirtysix_month_prccm']/CRSP_comp_merge['past_thirtysix_month_ajexm'])*CRSP_comp_merge['past_thirtysix_month_trfm']))-1)*100

In [23]:
CRSP_comp_merge["GVKEY-year-month"] = CRSP_comp_merge["GVKEY"].map(str) + "-" + CRSP_comp_merge["year-month"]

In [24]:
df = df.merge(CRSP_comp_merge, on='GVKEY-year-month', how='left', suffixes=('', '_y'))

In [25]:
drop_dups(df)

In [26]:
# Load Recommendations - Summary Statistics (Consensus Recommendations) from Wharton
recommendations = pd.read_csv('c:/users/shane/Desktop/W205_Final/sample_data/Sample_Recommendations_Summary_Statistics.csv', low_memory=False)

In [27]:
# Add additional time based columns
recommendations['STATPERS'] = pd.to_datetime(recommendations['STATPERS'])

# Create year
recommendations['year'] = recommendations['STATPERS'].dt.year

# Create month
recommendations['month'] = recommendations['STATPERS'].dt.month

recommendations["year-month"] = recommendations['STATPERS'].apply(lambda x: x.strftime('%Y-%m'))

In [28]:
recommendations["TIC-year-month"] = recommendations["OFTIC"].map(str) + "-" + recommendations["year-month"]

In [29]:
df = df.merge(recommendations, on='TIC-year-month', how='left', suffixes=('', '_y'))

In [30]:
drop_dups(df)

In [31]:
# Load Beta Suite from Wharton
beta_suite = pd.read_csv('c:/users/shane/Desktop/W205_Final/sample_data/Sample_Beta_Suite.csv', low_memory=False)

In [32]:
# Add additional time based columns
beta_suite['DATE'] = pd.to_datetime(beta_suite['DATE'])

# Create year
beta_suite['year'] = beta_suite['DATE'].dt.year

# Create month
beta_suite['month'] = beta_suite['DATE'].dt.month

beta_suite["year-month"] = beta_suite['DATE'].apply(lambda x: x.strftime('%Y-%m'))

beta_suite["PERMNO-year-month"] = beta_suite["PERMNO"].map(str) + "-" + beta_suite["year-month"]

In [33]:
df = df.merge(beta_suite, on='PERMNO-year-month', how='left', suffixes=('', '_y'))

In [34]:
# Overview of merged dataset
print("Number of columns:", len(df.columns))
print("Number of rows:", len(df.index))
df.head(5)

Number of columns: 516
Number of rows: 47539


gvkey       adate      qdate public_date   CAPEI     bm     evm  \
0   1045  12/31/2013  9/30/2014  2015-01-31 -28.361  0.195   6.783   
1   1050  12/31/2013  9/30/2014  2015-01-31  96.478  0.602  12.999   
2   1075  12/31/2013  9/30/2014  2015-01-31  22.099  1.189   7.706   
3   1076  12/31/2013  9/30/2014  2015-01-31  18.284  0.786   2.385   
4   1078  12/31/2013  9/30/2014  2015-01-31  20.978  0.365  16.133   

   pe_op_basic  pe_op_dil  pe_exi      ...        b_smb   b_hml   b_umd  \
0       16.751     17.282  -8.827      ...       0.5515  1.3562 -0.7802   
1       21.438     21.778  25.407      ...       0.9943 -0.3774 -0.1815   
2       18.615     18.715  18.715      ...      -0.0262  0.5299 -0.1109   
3       22.454     22.614  29.589      ...       0.7789  0.4319 -0.0340   
4       34.431     34.698  43.882      ...      -0.4996  0.0523  0.0932   

       ivol      tvol        R2     exret  year_y  month_y  year-month_y  
0  16.8533%  20.0013%  29.0013%   4.8844%  2015.0      1.0       2015-01  
1  14.6365%  16.2668%  19.0399%  -8.4346%  2015.0      1.0       2015-01  
2   5.4796%   6.0076%  16.8061%   7.0960%  2015.0      1.0       2015-01  
3   8.2736%   9.1728%  18.6448%   7.5446%  2015.0      1.0       2015-01  
4   5.0409%   5.5657%  17.9691%   1.0404%  2015.0      1.0       2015-01  

[5 rows x 516 columns]

In [35]:
drop_dups(df)

In [36]:
# Create formal vocabulary of industries
# https://en.wikipedia.org/wiki/Global_Industry_Classification_Standard

industry = pd.DataFrame()

industry['GSECTOR'] = [10.0, 
                       15.0, 
                       20.0, 
                       25.0, 
                       30.0, 
                       35.0, 
                       40.0, 
                       45.0, 
                       50.0, 
                       55.0, 
                       60.0]

industry['industry'] = ['Energy', 
                        'Materials', 
                        'Industrials', 
                        'Consumer Discretionary', 
                        'Consumer Staples', 
                        'Health Care', 
                        'Financials', 
                        'Information Technology', 
                        'Telecommunication Services', 
                        'Utilities', 
                        'Real Estate']

In [37]:
industry

GSECTOR                    industry
0      10.0                      Energy
1      15.0                   Materials
2      20.0                 Industrials
3      25.0      Consumer Discretionary
4      30.0            Consumer Staples
5      35.0                 Health Care
6      40.0                  Financials
7      45.0      Information Technology
8      50.0  Telecommunication Services
9      55.0                   Utilities
10     60.0                 Real Estate

In [38]:
df = df.merge(industry, on='GSECTOR', how='left', suffixes=('', '_y'))

In [39]:
drop_dups(df)

In [40]:
# Overview of merged dataset
print("Number of columns:", len(df.columns))
print("Number of rows:", len(df.index))
df.head(5)

Number of columns: 514
Number of rows: 47539


gvkey       adate      qdate public_date   CAPEI     bm     evm  \
0   1045  12/31/2013  9/30/2014  2015-01-31 -28.361  0.195   6.783   
1   1050  12/31/2013  9/30/2014  2015-01-31  96.478  0.602  12.999   
2   1075  12/31/2013  9/30/2014  2015-01-31  22.099  1.189   7.706   
3   1076  12/31/2013  9/30/2014  2015-01-31  18.284  0.786   2.385   
4   1078  12/31/2013  9/30/2014  2015-01-31  20.978  0.365  16.133   

   pe_op_basic  pe_op_dil  pe_exi           ...             alpha   b_mkt  \
0       16.751     17.282  -8.827           ...           -0.0015  1.7369   
1       21.438     21.778  25.407           ...            0.0085  1.0891   
2       18.615     18.715  18.715           ...            0.0049  0.3827   
3       22.454     22.614  29.589           ...            0.0073  0.5894   
4       34.431     34.698  43.882           ...            0.0062  0.4869   

    b_smb   b_hml   b_umd      ivol      tvol        R2     exret  \
0  0.5515  1.3562 -0.7802  16.8533%  20.0013%  29.0013%   4.8844%   
1  0.9943 -0.3774 -0.1815  14.6365%  16.2668%  19.0399%  -8.4346%   
2 -0.0262  0.5299 -0.1109   5.4796%   6.0076%  16.8061%   7.0960%   
3  0.7789  0.4319 -0.0340   8.2736%   9.1728%  18.6448%   7.5446%   
4 -0.4996  0.0523  0.0932   5.0409%   5.5657%  17.9691%   1.0404%   

                 industry  
0             Industrials  
1             Industrials  
2               Utilities  
3  Consumer Discretionary  
4             Health Care  

[5 rows x 514 columns]

In [41]:
# Load Zack Surprises from Wharton
zacks_eps_surprises = pd.read_csv('c:/users/shane/Desktop/W205_Final/sample_data/Sample_Zacks_EPS_Surprises.csv', low_memory=False)

In [42]:
# Add additional time based columns
zacks_eps_surprises['REPORT_DATE'] = pd.to_datetime(zacks_eps_surprises['REPORT_DATE'], format='%Y%m%d')

# Create year
zacks_eps_surprises['year'] = zacks_eps_surprises['REPORT_DATE'].dt.year

# Create month
zacks_eps_surprises['month'] = zacks_eps_surprises['REPORT_DATE'].dt.month

zacks_eps_surprises['year-month'] = zacks_eps_surprises['REPORT_DATE'].apply(lambda x: x.strftime('%Y-%m'))

zacks_eps_surprises["TIC-year-month"] = zacks_eps_surprises["TICKER"].map(str) + "-" + zacks_eps_surprises["year-month"]

In [43]:
# Merge new dataset to df
df = df.merge(zacks_eps_surprises, on='TIC-year-month', how='left', suffixes=('', '_y'))

# Drop duplicate columns from second dataset
drop_dups(df)

# Overview of merged dataset
print("Number of columns:", len(df.columns))
print("Number of rows:", len(df.index))
df.head(5)

Number of columns: 528
Number of rows: 47539


gvkey       adate      qdate public_date   CAPEI     bm     evm  \
0   1045  12/31/2013  9/30/2014  2015-01-31 -28.361  0.195   6.783   
1   1050  12/31/2013  9/30/2014  2015-01-31  96.478  0.602  12.999   
2   1075  12/31/2013  9/30/2014  2015-01-31  22.099  1.189   7.706   
3   1076  12/31/2013  9/30/2014  2015-01-31  18.284  0.786   2.385   
4   1078  12/31/2013  9/30/2014  2015-01-31  20.978  0.365  16.133   

   pe_op_basic  pe_op_dil  pe_exi  ...   ACTUAL_EPS  CONSENSUS_EPS  \
0       16.751     17.282  -8.827  ...          NaN            NaN   
1       21.438     21.778  25.407  ...          NaN            NaN   
2       18.615     18.715  18.715  ...          NaN            NaN   
3       22.454     22.614  29.589  ...          NaN            NaN   
4       34.431     34.698  43.882  ...          NaN            NaN   

   SURPRISE_PCT  CONSENSUS_STD  NUMBER_OF_EST  ADJUSTMENT  INTERNAL_CODE  \
0           NaN            NaN            NaN         NaN            NaN   
1           NaN            NaN            NaN         NaN            NaN   
2           NaN            NaN            NaN         NaN            NaN   
3           NaN            NaN            NaN         NaN            NaN   
4           NaN            NaN            NaN         NaN            NaN   

   CURRENT_INACTIVE_CODE  FISCAL_MONTH  NAME  
0                    NaN           NaN   NaN  
1                    NaN           NaN   NaN  
2                    NaN           NaN   NaN  
3                    NaN           NaN   NaN  
4                    NaN           NaN   NaN  

[5 rows x 528 columns]

In [44]:
# Seperate feature for each month
df['january'] = np.where(df['month'] == 1, int(1), int(0))
df['february'] = np.where(df['month'] == 2, int(1), int(0))
df['march'] = np.where(df['month'] == 3, int(1), int(0))
df['april'] = np.where(df['month'] == 4, int(1), int(0))
df['may'] = np.where(df['month'] == 5, int(1), int(0))
df['june'] = np.where(df['month'] == 6, int(1), int(0))
df['july'] = np.where(df['month'] == 7, int(1), int(0))
df['august'] = np.where(df['month'] == 8, int(1), int(0))
df['september'] = np.where(df['month'] == 9, int(1), int(0))
df['october'] = np.where(df['month'] == 10, int(1), int(0))
df['november'] = np.where(df['month'] == 11, int(1), int(0))
df['december'] = np.where(df['month'] == 12, int(1), int(0))

In [45]:
# Grab final feature list, remove non relevant to analysis
return_all_rows(null_ratio(df))

Null Count  Null Percent
forward_thirtysix_month_return         47539    100.000000
FISCAL_MONTH                           47539    100.000000
INTERNAL_CODE                          47539    100.000000
ADJUSTMENT                             47539    100.000000
NUMBER_OF_EST                          47539    100.000000
CONSENSUS_STD                          47539    100.000000
past_thirtysix_month_trfm              47539    100.000000
SURPRISE_PCT                           47539    100.000000
CONSENSUS_EPS                          47539    100.000000
ACTUAL_EPS                             47539    100.000000
REFERENCE_PERIOD                       47539    100.000000
ZID                                    47539    100.000000
REPORT_DATE                            47539    100.000000
ENTRY_DATE                             47539    100.000000
past_thirtysix_month_ajexm             47539    100.000000
forward_thirtysix_month_ajexm          47539    100.000000
csfsm                                  47539    100.000000
sph100                                 47539    100.000000
sphcusip                               47539    100.000000
sphiid                                 47539    100.000000
sphmid                                 47539    100.000000
sphname                                47539    100.000000
sphsec                                 47539    100.000000
sphtic                                 47539    100.000000
sphvg                                  47539    100.000000
forward_thirtysix_month_trfm           47539    100.000000
NAME                                   47539    100.000000
past_thirtysix_month_return            47539    100.000000
past_thirtysix_month_prccm             47539    100.000000
forward_thirtysix_month_prccm          47539    100.000000
CURRENT_INACTIVE_CODE                  47539    100.000000
past_thirtyfive_month_prccm            47533     99.987379
forward_thirtyfive_month_return        47533     99.987379
forward_thirtyfive_month_trfm          47533     99.987379
past_thirtyfive_month_return           47533     99.987379
forward_thirtyfive_month_prccm         47533     99.987379
past_thirtyfive_month_ajexm            47533     99.987379
forward_thirtyfive_month_ajexm         47533     99.987379
past_thirtyfive_month_trfm             47533     99.987379
past_thirtyfour_month_prccm            47527     99.974758
past_thirtyfour_month_return           47527     99.974758
navm                                   47527     99.974758
county                                 47527     99.974758
forward_thirtyfour_month_trfm          47527     99.974758
COUNTY                                 47527     99.974758
past_thirtyfour_month_trfm             47527     99.974758
forward_thirtyfour_month_prccm         47527     99.974758
past_thirtyfour_month_ajexm            47527     99.974758
forward_thirtyfour_month_return        47527     99.974758
forward_thirtyfour_month_ajexm         47527     99.974758
past_thirtythree_month_return          47521     99.962136
forward_thirtythree_month_return       47521     99.962136
past_thirtythree_month_prccm           47521     99.962136
past_thirtythree_month_trfm            47521     99.962136
past_thirtythree_month_ajexm           47521     99.962136
forward_thirtythree_month_prccm        47521     99.962136
forward_thirtythree_month_trfm         47521     99.962136
forward_thirtythree_month_ajexm        47521     99.962136
past_thirtytwo_month_trfm              47515     99.949515
past_thirtytwo_month_prccm             47515     99.949515
forward_thirtytwo_month_trfm           47515     99.949515
forward_thirtytwo_month_ajexm          47515     99.949515
forward_thirtytwo_month_prccm          47515     99.949515
past_thirtytwo_month_return            47515     99.949515
past_thirtytwo_month_ajexm             47515     99.949515
forward_thirtytwo_month_return         47515     99.949515
isalrt                                 47512     99.943205
past_thirtyone_month_p

In [46]:
df = df[[
        'GVKEY', 
        'tic', 
        'conm', 
        'industry', 
        'GVKEY-year-month', 
        'year-month', 
        'forward_one_month_return', 
        'forward_two_month_return', 
        'forward_three_month_return', 
        'forward_four_month_return', 
        'forward_five_month_return', 
        'forward_six_month_return', 
        'forward_seven_month_return', 
        'forward_eight_month_return', 
        'forward_nine_month_return', 
        'forward_ten_month_return', 
        'forward_eleven_month_return', 
        'forward_twelve_month_return', 
        'forward_thirteen_month_return', 
        'forward_fourteen_month_return', 
        'forward_fifteen_month_return', 
        'forward_sixteen_month_return', 
        'forward_seventeen_month_return', 
        'forward_eighteen_month_return', 
        'forward_nineteen_month_return', 
        'forward_twenty_month_return', 
        'forward_twentyone_month_return', 
        'forward_twentytwo_month_return', 
        'forward_twentythree_month_return', 
        'forward_twentyfour_month_return', 
        'forward_twentyfive_month_return', 
        'forward_twentysix_month_return', 
        'forward_twentyseven_month_return', 
        'forward_twentyeight_month_return', 
        'forward_twentynine_month_return', 
        'forward_thirty_month_return', 
        'forward_thirtyone_month_return', 
        'forward_thirtytwo_month_return', 
        'forward_thirtythree_month_return', 
        'forward_thirtyfour_month_return', 
        'forward_thirtyfive_month_return', 
        'forward_thirtysix_month_return', 
        'past_one_month_return', 
        'past_two_month_return', 
        'past_three_month_return', 
        'past_four_month_return', 
        'past_five_month_return', 
        'past_six_month_return', 
        'past_seven_month_return', 
        'past_eight_month_return', 
        'past_nine_month_return', 
        'past_ten_month_return', 
        'past_eleven_month_return', 
        'past_twelve_month_return', 
        'past_thirteen_month_return', 
        'past_fourteen_month_return', 
        'past_fifteen_month_return', 
        'past_sixteen_month_return', 
        'past_seventeen_month_return', 
        'past_eighteen_month_return', 
        'past_nineteen_month_return', 
        'past_twenty_month_return', 
        'past_twentyone_month_return', 
        'past_twentytwo_month_return', 
        'past_twentythree_month_return', 
        'past_twentyfour_month_return', 
        'past_twentyfive_month_return', 
        'past_twentysix_month_return', 
        'past_twentyseven_month_return', 
        'past_twentyeight_month_return', 
        'past_twentynine_month_return', 
        'past_thirty_month_return', 
        'past_thirtyone_month_return', 
        'past_thirtytwo_month_return', 
        'past_thirtythree_month_return', 
        'past_thirtyfour_month_return', 
        'past_thirtyfive_month_return', 
        'past_thirtysix_month_return', 
        'accrual', 
        'adv_sale', 
        'aftret_eq', 
        'aftret_equity', 
        'aftret_invcapx', 
        'at_turn', 
        'bm', 
        'CAPEI', 
        'capital_ratio', 
        'cash_conversion', 
        'cash_debt', 
        'cash_lt', 
        'cash_ratio', 
        'cfm', 
        'curr_debt', 
        'curr_ratio', 
        'de_ratio', 
        'debt_assets', 
        'debt_at', 
        'debt_capital', 
        'debt_ebitda', 
        'debt_invcap', 
        'DIVYIELD', 
        'dltt_be', 
        'dpr', 
        'efftax', 
        'equity_invcap', 
        'evm', 
        'fcf_ocf', 
        'gpm', 
        'GProf', 
        'int_debt', 
        'int_totdebt', 
        'intcov', 
        'intcov_ratio', 
        'inv_turn', 
        'invt_act', 
        'lt_debt', 
        'lt_ppent', 
        'npm', 
        'ocf_lct', 
        'opmad', 
        'opmbd', 
        'pay_turn', 
        'pcf', 
        'pe_exi', 
        'pe_inc', 
        'pe_op_basic', 
        'pe_op_dil', 
        'PEG_1yrforward', 
        'PEG_ltgforward', 
        'PEG_trailing', 
        'pretret_earnat', 
        'pretret_noa', 
        'profit_lct', 
        'ps', 
        'ptb', 
        'ptpm', 
        'quick_ratio', 
        'rd_sale', 
        'rect_act', 
        'rect_turn', 
        'roa', 
        'roce', 
        'roe', 
        'sale_equity', 
        'sale_invcap', 
        'sale_nwc', 
        'short_debt', 
        'staff_sale', 
        'totdebt_invcap', 
        'dvpspm', 
        'dvpsxm', 
        'dvrate', 
        'sic', 
        'spcsrc', 
        'alpha', 
        'b_hml', 
        'b_mkt', 
        'b_smb', 
        'b_umd', 
        'exret', 
        'ivol', 
        'n', 
        'R2', 
        'tvol', 
        'january', 
        'february', 
        'march', 
        'april', 
        'may', 
        'june', 
        'july', 
        'august', 
        'september', 
        'october', 
        'november', 
        'december', 
        'BUYPCT', 
        'HOLDPCT', 
        'MEANREC', 
        'MEDREC', 
        'NUMDOWN', 
        'NUMREC', 
        'NUMUP', 
        'SELLPCT', 
        'STDEV', 
        'USFIRM', 
        'ACTUAL_EPS', 
        'CONSENSUS_EPS', 
        'CONSENSUS_STD', 
        'NUMBER_OF_EST', 
        'SURPRISE_PCT'
        ]]

In [47]:
# Companies who do not report dividends are unlikely to have paid dividends, the majority of companies do not pay as well.
df['DIVYIELD'] = df['DIVYIELD'].replace('%','',regex=True).astype('float')/100
df['DIVYIELD'] = df['DIVYIELD'].fillna(0)
df['DIVYIELD'] = pd.to_numeric(df['DIVYIELD'])

In [48]:
df['dvpspm'] = df['dvpspm'].fillna(0)
df['dvpsxm'] = df['dvpsxm'].fillna(0)
df['dvrate'] = df['dvrate'].fillna(0)

In [49]:
df['spcsrc'].value_counts()

B-    8110
C     7825
B     7753
B+    6368
A-    2265
A     1167
D     1070
A+     405
Name: spcsrc, dtype: int64

In [50]:
# Per S&P Quality Rankings information; 
# A+ - 98-100 percentile (Highest, 2%)
# A - 92-98 percentile (High, 6%) 
# A- - 86-92 percentile (Above Average, 6%) 
# B+ - 70-86 percentile (Average, 16%) 
# B - 51-70 percentile (Below Average, 19%)
# B- - 25-51 percentile (Lower, 26%)
# C - 1-25 percentile (Lowest, 24%)
# D - 0-1 percentile (In Reorganization, 1%) 

# Using the average of percentile ranges above

df['spcsrc'] = df['spcsrc'].map({
                                'A+': 99,
                                'A': 95,
                                'A-': 89,
                                'B+': 79.5,
                                'B': 60.5,
                                'B-': 38,
                                'C': 13,
                                'D': 0.5,
                                })

df['spcsrc'] = pd.to_numeric(df['spcsrc'])

In [51]:
df['exret'] = df['exret'].replace('%','',regex=True).astype('float')/100
df['exret'] = pd.to_numeric(df['exret'])

In [52]:
df['ivol'] = df['ivol'].replace('%','',regex=True).astype('float')/100
df['ivol'] = pd.to_numeric(df['ivol'])

In [53]:
df['R2'] = df['R2'].replace('%','',regex=True).astype('float')/100
df['R2'] = pd.to_numeric(df['R2'])

In [54]:
df['tvol'] = df['tvol'].replace('%','',regex=True).astype('float')/100
df['tvol'] = pd.to_numeric(df['tvol'])

In [55]:
df['CONSENSUS_EPS'] = pd.to_numeric(df['CONSENSUS_EPS'])
df['CONSENSUS_STD'] = pd.to_numeric(df['CONSENSUS_STD'])
df['SURPRISE_PCT'] = pd.to_numeric(df['SURPRISE_PCT'])

In [56]:
return_all_rows(df.dtypes)

GVKEY                                 int64
tic                                  object
conm                                 object
industry                             object
GVKEY-year-month                     object
year-month                           object
forward_one_month_return            float64
forward_two_month_return            float64
forward_three_month_return          float64
forward_four_month_return           float64
forward_five_month_return           float64
forward_six_month_return            float64
forward_seven_month_return          float64
forward_eight_month_return          float64
forward_nine_month_return           float64
forward_ten_month_return            float64
forward_eleven_month_return         float64
forward_twelve_month_return         float64
forward_thirteen_month_return       float64
forward_fourteen_month_return       float64
forward_fifteen_month_return        float64
forward_sixteen_month_return        float64
forward_seventeen_month_return  

In [57]:
return_all_columns(df)

GVKEY   tic                         conm                industry  \
0   1045   AAL  AMERICAN AIRLINES GROUP INC             Industrials   
1   1050  CECE      CECO ENVIRONMENTAL CORP             Industrials   
2   1075   PNW   PINNACLE WEST CAPITAL CORP               Utilities   
3   1076   AAN                  AARON'S INC  Consumer Discretionary   
4   1078   ABT          ABBOTT LABORATORIES             Health Care   

  GVKEY-year-month year-month  forward_one_month_return  \
0     1045-2015-01    2015-01                 -2.200307   
1     1050-2015-01    2015-01                  3.717201   
2     1075-2015-01    2015-01                 -8.691935   
3     1076-2015-01    2015-01                 -5.843335   
4     1078-2015-01    2015-01                  5.831099   

   forward_two_month_return  forward_three_month_return  \
0                  7.763420                   -1.208663   
1                -22.185362                  -13.531142   
2                 -9.162154                  -11.947686   
3                -10.510038                    7.476464   
4                  3.507596                    4.245988   

   forward_four_month_return  forward_five_month_return  \
0                 -13.310781                 -18.292802   
1                 -16.758139                 -16.421029   
2                 -12.350540                 -18.148756   
3                  10.732369                  14.533202   
4                   9.141642                  10.219585   

   forward_six_month_return  forward_seven_month_return  \
0                -17.955212                  -20.041269   
1                -33.608937                  -28.592724   
2                -10.358036                  -13.524775   
3                 16.968733                   19.087961   
4                 14.373570                    2.189366   

   forward_eight_month_return  forward_nine_month_return  \
0                  -20.348960                  -5.190032   
1                  -39.099046                 -33.670756   
2                   -6.828139                  -6.835474   
3                   14.287472                 -21.919913   
4                   -9.250247                   1.625125   

   forward_ten_month_return  forward_eleven_month_return  \
0                -15.163603                   -12.922409   
1                -35.381039                   -42.399508   
2                 -7.055513                    -5.412555   
3                -23.104592                   -29.061055   
4                  1.897335                     1.874651   

   forward_twelve_month_return  forward_thirteen_month_return  \
0                          NaN                            NaN   
1                          NaN                            NaN   
2                          NaN                            NaN   
3                          NaN                            NaN   
4                          NaN                            NaN   

   forward_fourteen_month_return  forward_fifteen_month_return  \
0                            NaN                           NaN   
1                            NaN                           NaN   
2                            NaN                           NaN   
3                            NaN                           NaN   
4                            NaN                           NaN   

   forward_sixteen_month_return  forward_seventeen_month_return  \
0                           NaN                             NaN   
1                           NaN                             NaN   
2                           NaN                             NaN   
3                           NaN                             NaN   
4                           NaN                             NaN   

   forward_eighteen_month_return  forward_nineteen_month_return  \
0                            NaN                            NaN   
1                            NaN                            NaN   
2                            NaN          

In [58]:
from scipy import stats

In [59]:
overview(df)

Number of columns: 191
Number of rows: 47539


In [60]:
df = df[np.abs(df.forward_one_month_return-df.forward_one_month_return.apply(np.nanmean))<=(3*df.forward_one_month_return.apply(np.nanstd))] 

C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\s

In [61]:
overview(df)

Number of columns: 191
Number of rows: 43526


In [62]:
# Get median across all stocks per each month
forward_one_month_return_median = df.groupby(['year-month'])[['forward_one_month_return']].apply(np.nanmedian)
forward_one_month_return_median.name = 'forward_one_month_return_median'
df = df.join(forward_one_month_return_median, on=['year-month'])

forward_two_month_return_median = df.groupby(['year-month'])[['forward_two_month_return']].apply(np.nanmedian)
forward_two_month_return_median.name = 'forward_two_month_return_median'
df = df.join(forward_two_month_return_median, on=['year-month'])

forward_three_month_return_median = df.groupby(['year-month'])[['forward_three_month_return']].apply(np.nanmedian)
forward_three_month_return_median.name = 'forward_three_month_return_median'
df = df.join(forward_three_month_return_median, on=['year-month'])

forward_four_month_return_median = df.groupby(['year-month'])[['forward_four_month_return']].apply(np.nanmedian)
forward_four_month_return_median.name = 'forward_four_month_return_median'
df = df.join(forward_four_month_return_median, on=['year-month'])

forward_five_month_return_median = df.groupby(['year-month'])[['forward_five_month_return']].apply(np.nanmedian)
forward_five_month_return_median.name = 'forward_five_month_return_median'
df = df.join(forward_five_month_return_median, on=['year-month'])

forward_six_month_return_median = df.groupby(['year-month'])[['forward_six_month_return']].apply(np.nanmedian)
forward_six_month_return_median.name = 'forward_six_month_return_median'
df = df.join(forward_six_month_return_median, on=['year-month'])

forward_seven_month_return_median = df.groupby(['year-month'])[['forward_seven_month_return']].apply(np.nanmedian)
forward_seven_month_return_median.name = 'forward_seven_month_return_median'
df = df.join(forward_seven_month_return_median, on=['year-month'])

forward_eight_month_return_median = df.groupby(['year-month'])[['forward_eight_month_return']].apply(np.nanmedian)
forward_eight_month_return_median.name = 'forward_eight_month_return_median'
df = df.join(forward_eight_month_return_median, on=['year-month'])

forward_nine_month_return_median = df.groupby(['year-month'])[['forward_nine_month_return']].apply(np.nanmedian)
forward_nine_month_return_median.name = 'forward_nine_month_return_median'
df = df.join(forward_nine_month_return_median, on=['year-month'])

forward_ten_month_return_median = df.groupby(['year-month'])[['forward_ten_month_return']].apply(np.nanmedian)
forward_ten_month_return_median.name = 'forward_ten_month_return_median'
df = df.join(forward_ten_month_return_median, on=['year-month'])

forward_eleven_month_return_median = df.groupby(['year-month'])[['forward_eleven_month_return']].apply(np.nanmedian)
forward_eleven_month_return_median.name = 'forward_eleven_month_return_median'
df = df.join(forward_eleven_month_return_median, on=['year-month'])

forward_twelve_month_return_median = df.groupby(['year-month'])[['forward_twelve_month_return']].apply(np.nanmedian)
forward_twelve_month_return_median.name = 'forward_twelve_month_return_median'
df = df.join(forward_twelve_month_return_median, on=['year-month'])

forward_thirteen_month_return_median = df.groupby(['year-month'])[['forward_thirteen_month_return']].apply(np.nanmedian)
forward_thirteen_month_return_median.name = 'forward_thirteen_month_return_median'
df = df.join(forward_thirteen_month_return_median, on=['year-month'])

forward_fourteen_month_return_median = df.groupby(['year-month'])[['forward_fourteen_month_return']].apply(np.nanmedian)
forward_fourteen_month_return_median.name = 'forward_fourteen_month_return_median'
df = df.join(forward_fourteen_month_return_median, on=['year-month'])

forward_fifteen_month_return_median = df.groupby(['year-month'])[['forward_fifteen_month_return']].apply(np.nanmedian)
forward_fifteen_month_return_median.name = 'forward_fifteen_month_return_median'
df = df.join(forward_fifteen_month_return_median, on=['year-month'])

forward_sixteen_month_return_median = df.groupby(['year-month'])[['forward_sixteen_month_return']].apply(np.nanmedian)
forward_sixteen_month_return_median.name = 'forward_sixteen_month_return_median'
df = df.join(forward_sixteen_month_return_median, on=['year-month'])

forward_seventeen_month_return_median = df.groupby(['year-month'])[['forward_seventeen_month_return']].apply(np.nanmedian)
forward_seventeen_month_return_median.name = 'forward_seventeen_month_return_median'
df = df.join(forward_seventeen_month_return_median, on=['year-month'])

forward_eighteen_month_return_median = df.groupby(['year-month'])[['forward_eighteen_month_return']].apply(np.nanmedian)
forward_eighteen_month_return_median.name = 'forward_eighteen_month_return_median'
df = df.join(forward_eighteen_month_return_median, on=['year-month'])

forward_nineteen_month_return_median = df.groupby(['year-month'])[['forward_nineteen_month_return']].apply(np.nanmedian)
forward_nineteen_month_return_median.name = 'forward_nineteen_month_return_median'
df = df.join(forward_nineteen_month_return_median, on=['year-month'])

forward_twenty_month_return_median = df.groupby(['year-month'])[['forward_twenty_month_return']].apply(np.nanmedian)
forward_twenty_month_return_median.name = 'forward_twenty_month_return_median'
df = df.join(forward_twenty_month_return_median, on=['year-month'])

forward_twentyone_month_return_median = df.groupby(['year-month'])[['forward_twentyone_month_return']].apply(np.nanmedian)
forward_twentyone_month_return_median.name = 'forward_twentyone_month_return_median'
df = df.join(forward_twentyone_month_return_median, on=['year-month'])

forward_twentytwo_month_return_median = df.groupby(['year-month'])[['forward_twentytwo_month_return']].apply(np.nanmedian)
forward_twentytwo_month_return_median.name = 'forward_twentytwo_month_return_median'
df = df.join(forward_twentytwo_month_return_median, on=['year-month'])

forward_twentythree_month_return_median = df.groupby(['year-month'])[['forward_twentythree_month_return']].apply(np.nanmedian)
forward_twentythree_month_return_median.name = 'forward_twentythree_month_return_median'
df = df.join(forward_twentythree_month_return_median, on=['year-month'])

forward_twentyfour_month_return_median = df.groupby(['year-month'])[['forward_twentyfour_month_return']].apply(np.nanmedian)
forward_twentyfour_month_return_median.name = 'forward_twentyfour_month_return_median'
df = df.join(forward_twentyfour_month_return_median, on=['year-month'])

forward_twentyfive_month_return_median = df.groupby(['year-month'])[['forward_twentyfive_month_return']].apply(np.nanmedian)
forward_twentyfive_month_return_median.name = 'forward_twentyfive_month_return_median'
df = df.join(forward_twentyfive_month_return_median, on=['year-month'])

forward_twentysix_month_return_median = df.groupby(['year-month'])[['forward_twentysix_month_return']].apply(np.nanmedian)
forward_twentysix_month_return_median.name = 'forward_twentysix_month_return_median'
df = df.join(forward_twentysix_month_return_median, on=['year-month'])

forward_twentyseven_month_return_median = df.groupby(['year-month'])[['forward_twentyseven_month_return']].apply(np.nanmedian)
forward_twentyseven_month_return_median.name = 'forward_twentyseven_month_return_median'
df = df.join(forward_twentyseven_month_return_median, on=['year-month'])

forward_twentyeight_month_return_median = df.groupby(['year-month'])[['forward_twentyeight_month_return']].apply(np.nanmedian)
forward_twentyeight_month_return_median.name = 'forward_twentyeight_month_return_median'
df = df.join(forward_twentyeight_month_return_median, on=['year-month'])

forward_twentynine_month_return_median = df.groupby(['year-month'])[['forward_twentynine_month_return']].apply(np.nanmedian)
forward_twentynine_month_return_median.name = 'forward_twentynine_month_return_median'
df = df.join(forward_twentynine_month_return_median, on=['year-month'])

forward_thirty_month_return_median = df.groupby(['year-month'])[['forward_thirty_month_return']].apply(np.nanmedian)
forward_thirty_month_return_median.name = 'forward_thirty_month_return_median'
df = df.join(forward_thirty_month_return_median, on=['year-month'])

forward_thirtyone_month_return_median = df.groupby(['year-month'])[['forward_thirtyone_month_return']].apply(np.nanmedian)
forward_thirtyone_month_return_median.name = 'forward_thirtyone_month_return_median'
df = df.join(forward_thirtyone_month_return_median, on=['year-month'])

forward_thirtytwo_month_return_median = df.groupby(['year-month'])[['forward_thirtytwo_month_return']].apply(np.nanmedian)
forward_thirtytwo_month_return_median.name = 'forward_thirtytwo_month_return_median'
df = df.join(forward_thirtytwo_month_return_median, on=['year-month'])

forward_thirtythree_month_return_median = df.groupby(['year-month'])[['forward_thirtythree_month_return']].apply(np.nanmedian)
forward_thirtythree_month_return_median.name = 'forward_thirtythree_month_return_median'
df = df.join(forward_thirtythree_month_return_median, on=['year-month'])

forward_thirtyfour_month_return_median = df.groupby(['year-month'])[['forward_thirtyfour_month_return']].apply(np.nanmedian)
forward_thirtyfour_month_return_median.name = 'forward_thirtyfour_month_return_median'
df = df.join(forward_thirtyfour_month_return_median, on=['year-month'])

forward_thirtyfive_month_return_median = df.groupby(['year-month'])[['forward_thirtyfive_month_return']].apply(np.nanmedian)
forward_thirtyfive_month_return_median.name = 'forward_thirtyfive_month_return_median'
df = df.join(forward_thirtyfive_month_return_median, on=['year-month'])

forward_thirtysix_month_return_median = df.groupby(['year-month'])[['forward_thirtysix_month_return']].apply(np.nanmedian)
forward_thirtysix_month_return_median.name = 'forward_thirtysix_month_return_median'
df = df.join(forward_thirtysix_month_return_median, on=['year-month'])

past_one_month_return_median = df.groupby(['year-month'])[['past_one_month_return']].apply(np.nanmedian)
past_one_month_return_median.name = 'past_one_month_return_median'
df = df.join(past_one_month_return_median, on=['year-month'])

past_two_month_return_median = df.groupby(['year-month'])[['past_two_month_return']].apply(np.nanmedian)
past_two_month_return_median.name = 'past_two_month_return_median'
df = df.join(past_two_month_return_median, on=['year-month'])

past_three_month_return_median = df.groupby(['year-month'])[['past_three_month_return']].apply(np.nanmedian)
past_three_month_return_median.name = 'past_three_month_return_median'
df = df.join(past_three_month_return_median, on=['year-month'])

past_four_month_return_median = df.groupby(['year-month'])[['past_four_month_return']].apply(np.nanmedian)
past_four_month_return_median.name = 'past_four_month_return_median'
df = df.join(past_four_month_return_median, on=['year-month'])

past_five_month_return_median = df.groupby(['year-month'])[['past_five_month_return']].apply(np.nanmedian)
past_five_month_return_median.name = 'past_five_month_return_median'
df = df.join(past_five_month_return_median, on=['year-month'])

past_six_month_return_median = df.groupby(['year-month'])[['past_six_month_return']].apply(np.nanmedian)
past_six_month_return_median.name = 'past_six_month_return_median'
df = df.join(past_six_month_return_median, on=['year-month'])

past_seven_month_return_median = df.groupby(['year-month'])[['past_seven_month_return']].apply(np.nanmedian)
past_seven_month_return_median.name = 'past_seven_month_return_median'
df = df.join(past_seven_month_return_median, on=['year-month'])

past_eight_month_return_median = df.groupby(['year-month'])[['past_eight_month_return']].apply(np.nanmedian)
past_eight_month_return_median.name = 'past_eight_month_return_median'
df = df.join(past_eight_month_return_median, on=['year-month'])

past_nine_month_return_median = df.groupby(['year-month'])[['past_nine_month_return']].apply(np.nanmedian)
past_nine_month_return_median.name = 'past_nine_month_return_median'
df = df.join(past_nine_month_return_median, on=['year-month'])

past_ten_month_return_median = df.groupby(['year-month'])[['past_ten_month_return']].apply(np.nanmedian)
past_ten_month_return_median.name = 'past_ten_month_return_median'
df = df.join(past_ten_month_return_median, on=['year-month'])

past_eleven_month_return_median = df.groupby(['year-month'])[['past_eleven_month_return']].apply(np.nanmedian)
past_eleven_month_return_median.name = 'past_eleven_month_return_median'
df = df.join(past_eleven_month_return_median, on=['year-month'])

past_twelve_month_return_median = df.groupby(['year-month'])[['past_twelve_month_return']].apply(np.nanmedian)
past_twelve_month_return_median.name = 'past_twelve_month_return_median'
df = df.join(past_twelve_month_return_median, on=['year-month'])

past_thirteen_month_return_median = df.groupby(['year-month'])[['past_thirteen_month_return']].apply(np.nanmedian)
past_thirteen_month_return_median.name = 'past_thirteen_month_return_median'
df = df.join(past_thirteen_month_return_median, on=['year-month'])

past_fourteen_month_return_median = df.groupby(['year-month'])[['past_fourteen_month_return']].apply(np.nanmedian)
past_fourteen_month_return_median.name = 'past_fourteen_month_return_median'
df = df.join(past_fourteen_month_return_median, on=['year-month'])

past_fifteen_month_return_median = df.groupby(['year-month'])[['past_fifteen_month_return']].apply(np.nanmedian)
past_fifteen_month_return_median.name = 'past_fifteen_month_return_median'
df = df.join(past_fifteen_month_return_median, on=['year-month'])

past_sixteen_month_return_median = df.groupby(['year-month'])[['past_sixteen_month_return']].apply(np.nanmedian)
past_sixteen_month_return_median.name = 'past_sixteen_month_return_median'
df = df.join(past_sixteen_month_return_median, on=['year-month'])

past_seventeen_month_return_median = df.groupby(['year-month'])[['past_seventeen_month_return']].apply(np.nanmedian)
past_seventeen_month_return_median.name = 'past_seventeen_month_return_median'
df = df.join(past_seventeen_month_return_median, on=['year-month'])

past_eighteen_month_return_median = df.groupby(['year-month'])[['past_eighteen_month_return']].apply(np.nanmedian)
past_eighteen_month_return_median.name = 'past_eighteen_month_return_median'
df = df.join(past_eighteen_month_return_median, on=['year-month'])

past_nineteen_month_return_median = df.groupby(['year-month'])[['past_nineteen_month_return']].apply(np.nanmedian)
past_nineteen_month_return_median.name = 'past_nineteen_month_return_median'
df = df.join(past_nineteen_month_return_median, on=['year-month'])

past_twenty_month_return_median = df.groupby(['year-month'])[['past_twenty_month_return']].apply(np.nanmedian)
past_twenty_month_return_median.name = 'past_twenty_month_return_median'
df = df.join(past_twenty_month_return_median, on=['year-month'])

past_twentyone_month_return_median = df.groupby(['year-month'])[['past_twentyone_month_return']].apply(np.nanmedian)
past_twentyone_month_return_median.name = 'past_twentyone_month_return_median'
df = df.join(past_twentyone_month_return_median, on=['year-month'])

past_twentytwo_month_return_median = df.groupby(['year-month'])[['past_twentytwo_month_return']].apply(np.nanmedian)
past_twentytwo_month_return_median.name = 'past_twentytwo_month_return_median'
df = df.join(past_twentytwo_month_return_median, on=['year-month'])

past_twentythree_month_return_median = df.groupby(['year-month'])[['past_twentythree_month_return']].apply(np.nanmedian)
past_twentythree_month_return_median.name = 'past_twentythree_month_return_median'
df = df.join(past_twentythree_month_return_median, on=['year-month'])

past_twentyfour_month_return_median = df.groupby(['year-month'])[['past_twentyfour_month_return']].apply(np.nanmedian)
past_twentyfour_month_return_median.name = 'past_twentyfour_month_return_median'
df = df.join(past_twentyfour_month_return_median, on=['year-month'])

past_twentyfive_month_return_median = df.groupby(['year-month'])[['past_twentyfive_month_return']].apply(np.nanmedian)
past_twentyfive_month_return_median.name = 'past_twentyfive_month_return_median'
df = df.join(past_twentyfive_month_return_median, on=['year-month'])

past_twentysix_month_return_median = df.groupby(['year-month'])[['past_twentysix_month_return']].apply(np.nanmedian)
past_twentysix_month_return_median.name = 'past_twentysix_month_return_median'
df = df.join(past_twentysix_month_return_median, on=['year-month'])

past_twentyseven_month_return_median = df.groupby(['year-month'])[['past_twentyseven_month_return']].apply(np.nanmedian)
past_twentyseven_month_return_median.name = 'past_twentyseven_month_return_median'
df = df.join(past_twentyseven_month_return_median, on=['year-month'])

past_twentyeight_month_return_median = df.groupby(['year-month'])[['past_twentyeight_month_return']].apply(np.nanmedian)
past_twentyeight_month_return_median.name = 'past_twentyeight_month_return_median'
df = df.join(past_twentyeight_month_return_median, on=['year-month'])

past_twentynine_month_return_median = df.groupby(['year-month'])[['past_twentynine_month_return']].apply(np.nanmedian)
past_twentynine_month_return_median.name = 'past_twentynine_month_return_median'
df = df.join(past_twentynine_month_return_median, on=['year-month'])

past_thirty_month_return_median = df.groupby(['year-month'])[['past_thirty_month_return']].apply(np.nanmedian)
past_thirty_month_return_median.name = 'past_thirty_month_return_median'
df = df.join(past_thirty_month_return_median, on=['year-month'])

past_thirtyone_month_return_median = df.groupby(['year-month'])[['past_thirtyone_month_return']].apply(np.nanmedian)
past_thirtyone_month_return_median.name = 'past_thirtyone_month_return_median'
df = df.join(past_thirtyone_month_return_median, on=['year-month'])

past_thirtytwo_month_return_median = df.groupby(['year-month'])[['past_thirtytwo_month_return']].apply(np.nanmedian)
past_thirtytwo_month_return_median.name = 'past_thirtytwo_month_return_median'
df = df.join(past_thirtytwo_month_return_median, on=['year-month'])

past_thirtythree_month_return_median = df.groupby(['year-month'])[['past_thirtythree_month_return']].apply(np.nanmedian)
past_thirtythree_month_return_median.name = 'past_thirtythree_month_return_median'
df = df.join(past_thirtythree_month_return_median, on=['year-month'])

past_thirtyfour_month_return_median = df.groupby(['year-month'])[['past_thirtyfour_month_return']].apply(np.nanmedian)
past_thirtyfour_month_return_median.name = 'past_thirtyfour_month_return_median'
df = df.join(past_thirtyfour_month_return_median, on=['year-month'])

past_thirtyfive_month_return_median = df.groupby(['year-month'])[['past_thirtyfive_month_return']].apply(np.nanmedian)
past_thirtyfive_month_return_median.name = 'past_thirtyfive_month_return_median'
df = df.join(past_thirtyfive_month_return_median, on=['year-month'])

past_thirtysix_month_return_median = df.groupby(['year-month'])[['past_thirtysix_month_return']].apply(np.nanmedian)
past_thirtysix_month_return_median.name = 'past_thirtysix_month_return_median'
df = df.join(past_thirtysix_month_return_median, on=['year-month'])

accrual_median = df.groupby(['year-month'])[['accrual']].apply(np.nanmedian)
accrual_median.name = 'accrual_median'
df = df.join(accrual_median, on=['year-month'])

adv_sale_median = df.groupby(['year-month'])[['adv_sale']].apply(np.nanmedian)
adv_sale_median.name = 'adv_sale_median'
df = df.join(adv_sale_median, on=['year-month'])

aftret_eq_median = df.groupby(['year-month'])[['aftret_eq']].apply(np.nanmedian)
aftret_eq_median.name = 'aftret_eq_median'
df = df.join(aftret_eq_median, on=['year-month'])

aftret_equity_median = df.groupby(['year-month'])[['aftret_equity']].apply(np.nanmedian)
aftret_equity_median.name = 'aftret_equity_median'
df = df.join(aftret_equity_median, on=['year-month'])

aftret_invcapx_median = df.groupby(['year-month'])[['aftret_invcapx']].apply(np.nanmedian)
aftret_invcapx_median.name = 'aftret_invcapx_median'
df = df.join(aftret_invcapx_median, on=['year-month'])

at_turn_median = df.groupby(['year-month'])[['at_turn']].apply(np.nanmedian)
at_turn_median.name = 'at_turn_median'
df = df.join(at_turn_median, on=['year-month'])

bm_median = df.groupby(['year-month'])[['bm']].apply(np.nanmedian)
bm_median.name = 'bm_median'
df = df.join(bm_median, on=['year-month'])

CAPEI_median = df.groupby(['year-month'])[['CAPEI']].apply(np.nanmedian)
CAPEI_median.name = 'CAPEI_median'
df = df.join(CAPEI_median, on=['year-month'])

capital_ratio_median = df.groupby(['year-month'])[['capital_ratio']].apply(np.nanmedian)
capital_ratio_median.name = 'capital_ratio_median'
df = df.join(capital_ratio_median, on=['year-month'])

cash_conversion_median = df.groupby(['year-month'])[['cash_conversion']].apply(np.nanmedian)
cash_conversion_median.name = 'cash_conversion_median'
df = df.join(cash_conversion_median, on=['year-month'])

cash_debt_median = df.groupby(['year-month'])[['cash_debt']].apply(np.nanmedian)
cash_debt_median.name = 'cash_debt_median'
df = df.join(cash_debt_median, on=['year-month'])

cash_lt_median = df.groupby(['year-month'])[['cash_lt']].apply(np.nanmedian)
cash_lt_median.name = 'cash_lt_median'
df = df.join(cash_lt_median, on=['year-month'])

cash_ratio_median = df.groupby(['year-month'])[['cash_ratio']].apply(np.nanmedian)
cash_ratio_median.name = 'cash_ratio_median'
df = df.join(cash_ratio_median, on=['year-month'])

cfm_median = df.groupby(['year-month'])[['cfm']].apply(np.nanmedian)
cfm_median.name = 'cfm_median'
df = df.join(cfm_median, on=['year-month'])

curr_debt_median = df.groupby(['year-month'])[['curr_debt']].apply(np.nanmedian)
curr_debt_median.name = 'curr_debt_median'
df = df.join(curr_debt_median, on=['year-month'])

curr_ratio_median = df.groupby(['year-month'])[['curr_ratio']].apply(np.nanmedian)
curr_ratio_median.name = 'curr_ratio_median'
df = df.join(curr_ratio_median, on=['year-month'])

de_ratio_median = df.groupby(['year-month'])[['de_ratio']].apply(np.nanmedian)
de_ratio_median.name = 'de_ratio_median'
df = df.join(de_ratio_median, on=['year-month'])

debt_assets_median = df.groupby(['year-month'])[['debt_assets']].apply(np.nanmedian)
debt_assets_median.name = 'debt_assets_median'
df = df.join(debt_assets_median, on=['year-month'])

debt_at_median = df.groupby(['year-month'])[['debt_at']].apply(np.nanmedian)
debt_at_median.name = 'debt_at_median'
df = df.join(debt_at_median, on=['year-month'])

debt_capital_median = df.groupby(['year-month'])[['debt_capital']].apply(np.nanmedian)
debt_capital_median.name = 'debt_capital_median'
df = df.join(debt_capital_median, on=['year-month'])

debt_ebitda_median = df.groupby(['year-month'])[['debt_ebitda']].apply(np.nanmedian)
debt_ebitda_median.name = 'debt_ebitda_median'
df = df.join(debt_ebitda_median, on=['year-month'])

debt_invcap_median = df.groupby(['year-month'])[['debt_invcap']].apply(np.nanmedian)
debt_invcap_median.name = 'debt_invcap_median'
df = df.join(debt_invcap_median, on=['year-month'])

DIVYIELD_median = df.groupby(['year-month'])[['DIVYIELD']].apply(np.nanmedian)
DIVYIELD_median.name = 'DIVYIELD_median'
df = df.join(DIVYIELD_median, on=['year-month'])

dltt_be_median = df.groupby(['year-month'])[['dltt_be']].apply(np.nanmedian)
dltt_be_median.name = 'dltt_be_median'
df = df.join(dltt_be_median, on=['year-month'])

dpr_median = df.groupby(['year-month'])[['dpr']].apply(np.nanmedian)
dpr_median.name = 'dpr_median'
df = df.join(dpr_median, on=['year-month'])

efftax_median = df.groupby(['year-month'])[['efftax']].apply(np.nanmedian)
efftax_median.name = 'efftax_median'
df = df.join(efftax_median, on=['year-month'])

equity_invcap_median = df.groupby(['year-month'])[['equity_invcap']].apply(np.nanmedian)
equity_invcap_median.name = 'equity_invcap_median'
df = df.join(equity_invcap_median, on=['year-month'])

evm_median = df.groupby(['year-month'])[['evm']].apply(np.nanmedian)
evm_median.name = 'evm_median'
df = df.join(evm_median, on=['year-month'])

fcf_ocf_median = df.groupby(['year-month'])[['fcf_ocf']].apply(np.nanmedian)
fcf_ocf_median.name = 'fcf_ocf_median'
df = df.join(fcf_ocf_median, on=['year-month'])

gpm_median = df.groupby(['year-month'])[['gpm']].apply(np.nanmedian)
gpm_median.name = 'gpm_median'
df = df.join(gpm_median, on=['year-month'])

GProf_median = df.groupby(['year-month'])[['GProf']].apply(np.nanmedian)
GProf_median.name = 'GProf_median'
df = df.join(GProf_median, on=['year-month'])

int_debt_median = df.groupby(['year-month'])[['int_debt']].apply(np.nanmedian)
int_debt_median.name = 'int_debt_median'
df = df.join(int_debt_median, on=['year-month'])

int_totdebt_median = df.groupby(['year-month'])[['int_totdebt']].apply(np.nanmedian)
int_totdebt_median.name = 'int_totdebt_median'
df = df.join(int_totdebt_median, on=['year-month'])

intcov_median = df.groupby(['year-month'])[['intcov']].apply(np.nanmedian)
intcov_median.name = 'intcov_median'
df = df.join(intcov_median, on=['year-month'])

intcov_ratio_median = df.groupby(['year-month'])[['intcov_ratio']].apply(np.nanmedian)
intcov_ratio_median.name = 'intcov_ratio_median'
df = df.join(intcov_ratio_median, on=['year-month'])

inv_turn_median = df.groupby(['year-month'])[['inv_turn']].apply(np.nanmedian)
inv_turn_median.name = 'inv_turn_median'
df = df.join(inv_turn_median, on=['year-month'])

invt_act_median = df.groupby(['year-month'])[['invt_act']].apply(np.nanmedian)
invt_act_median.name = 'invt_act_median'
df = df.join(invt_act_median, on=['year-month'])

lt_debt_median = df.groupby(['year-month'])[['lt_debt']].apply(np.nanmedian)
lt_debt_median.name = 'lt_debt_median'
df = df.join(lt_debt_median, on=['year-month'])

lt_ppent_median = df.groupby(['year-month'])[['lt_ppent']].apply(np.nanmedian)
lt_ppent_median.name = 'lt_ppent_median'
df = df.join(lt_ppent_median, on=['year-month'])

npm_median = df.groupby(['year-month'])[['npm']].apply(np.nanmedian)
npm_median.name = 'npm_median'
df = df.join(npm_median, on=['year-month'])

ocf_lct_median = df.groupby(['year-month'])[['ocf_lct']].apply(np.nanmedian)
ocf_lct_median.name = 'ocf_lct_median'
df = df.join(ocf_lct_median, on=['year-month'])

opmad_median = df.groupby(['year-month'])[['opmad']].apply(np.nanmedian)
opmad_median.name = 'opmad_median'
df = df.join(opmad_median, on=['year-month'])

opmbd_median = df.groupby(['year-month'])[['opmbd']].apply(np.nanmedian)
opmbd_median.name = 'opmbd_median'
df = df.join(opmbd_median, on=['year-month'])

pay_turn_median = df.groupby(['year-month'])[['pay_turn']].apply(np.nanmedian)
pay_turn_median.name = 'pay_turn_median'
df = df.join(pay_turn_median, on=['year-month'])

pcf_median = df.groupby(['year-month'])[['pcf']].apply(np.nanmedian)
pcf_median.name = 'pcf_median'
df = df.join(pcf_median, on=['year-month'])

pe_exi_median = df.groupby(['year-month'])[['pe_exi']].apply(np.nanmedian)
pe_exi_median.name = 'pe_exi_median'
df = df.join(pe_exi_median, on=['year-month'])

pe_inc_median = df.groupby(['year-month'])[['pe_inc']].apply(np.nanmedian)
pe_inc_median.name = 'pe_inc_median'
df = df.join(pe_inc_median, on=['year-month'])

pe_op_basic_median = df.groupby(['year-month'])[['pe_op_basic']].apply(np.nanmedian)
pe_op_basic_median.name = 'pe_op_basic_median'
df = df.join(pe_op_basic_median, on=['year-month'])

pe_op_dil_median = df.groupby(['year-month'])[['pe_op_dil']].apply(np.nanmedian)
pe_op_dil_median.name = 'pe_op_dil_median'
df = df.join(pe_op_dil_median, on=['year-month'])

PEG_1yrforward_median = df.groupby(['year-month'])[['PEG_1yrforward']].apply(np.nanmedian)
PEG_1yrforward_median.name = 'PEG_1yrforward_median'
df = df.join(PEG_1yrforward_median, on=['year-month'])

PEG_ltgforward_median = df.groupby(['year-month'])[['PEG_ltgforward']].apply(np.nanmedian)
PEG_ltgforward_median.name = 'PEG_ltgforward_median'
df = df.join(PEG_ltgforward_median, on=['year-month'])

PEG_trailing_median = df.groupby(['year-month'])[['PEG_trailing']].apply(np.nanmedian)
PEG_trailing_median.name = 'PEG_trailing_median'
df = df.join(PEG_trailing_median, on=['year-month'])

pretret_earnat_median = df.groupby(['year-month'])[['pretret_earnat']].apply(np.nanmedian)
pretret_earnat_median.name = 'pretret_earnat_median'
df = df.join(pretret_earnat_median, on=['year-month'])

pretret_noa_median = df.groupby(['year-month'])[['pretret_noa']].apply(np.nanmedian)
pretret_noa_median.name = 'pretret_noa_median'
df = df.join(pretret_noa_median, on=['year-month'])

profit_lct_median = df.groupby(['year-month'])[['profit_lct']].apply(np.nanmedian)
profit_lct_median.name = 'profit_lct_median'
df = df.join(profit_lct_median, on=['year-month'])

ps_median = df.groupby(['year-month'])[['ps']].apply(np.nanmedian)
ps_median.name = 'ps_median'
df = df.join(ps_median, on=['year-month'])

ptb_median = df.groupby(['year-month'])[['ptb']].apply(np.nanmedian)
ptb_median.name = 'ptb_median'
df = df.join(ptb_median, on=['year-month'])

ptpm_median = df.groupby(['year-month'])[['ptpm']].apply(np.nanmedian)
ptpm_median.name = 'ptpm_median'
df = df.join(ptpm_median, on=['year-month'])

quick_ratio_median = df.groupby(['year-month'])[['quick_ratio']].apply(np.nanmedian)
quick_ratio_median.name = 'quick_ratio_median'
df = df.join(quick_ratio_median, on=['year-month'])

rd_sale_median = df.groupby(['year-month'])[['rd_sale']].apply(np.nanmedian)
rd_sale_median.name = 'rd_sale_median'
df = df.join(rd_sale_median, on=['year-month'])

rect_act_median = df.groupby(['year-month'])[['rect_act']].apply(np.nanmedian)
rect_act_median.name = 'rect_act_median'
df = df.join(rect_act_median, on=['year-month'])

rect_turn_median = df.groupby(['year-month'])[['rect_turn']].apply(np.nanmedian)
rect_turn_median.name = 'rect_turn_median'
df = df.join(rect_turn_median, on=['year-month'])

roa_median = df.groupby(['year-month'])[['roa']].apply(np.nanmedian)
roa_median.name = 'roa_median'
df = df.join(roa_median, on=['year-month'])

roce_median = df.groupby(['year-month'])[['roce']].apply(np.nanmedian)
roce_median.name = 'roce_median'
df = df.join(roce_median, on=['year-month'])

roe_median = df.groupby(['year-month'])[['roe']].apply(np.nanmedian)
roe_median.name = 'roe_median'
df = df.join(roe_median, on=['year-month'])

sale_equity_median = df.groupby(['year-month'])[['sale_equity']].apply(np.nanmedian)
sale_equity_median.name = 'sale_equity_median'
df = df.join(sale_equity_median, on=['year-month'])

sale_invcap_median = df.groupby(['year-month'])[['sale_invcap']].apply(np.nanmedian)
sale_invcap_median.name = 'sale_invcap_median'
df = df.join(sale_invcap_median, on=['year-month'])

sale_nwc_median = df.groupby(['year-month'])[['sale_nwc']].apply(np.nanmedian)
sale_nwc_median.name = 'sale_nwc_median'
df = df.join(sale_nwc_median, on=['year-month'])

short_debt_median = df.groupby(['year-month'])[['short_debt']].apply(np.nanmedian)
short_debt_median.name = 'short_debt_median'
df = df.join(short_debt_median, on=['year-month'])

staff_sale_median = df.groupby(['year-month'])[['staff_sale']].apply(np.nanmedian)
staff_sale_median.name = 'staff_sale_median'
df = df.join(staff_sale_median, on=['year-month'])

totdebt_invcap_median = df.groupby(['year-month'])[['totdebt_invcap']].apply(np.nanmedian)
totdebt_invcap_median.name = 'totdebt_invcap_median'
df = df.join(totdebt_invcap_median, on=['year-month'])

dvpspm_median = df.groupby(['year-month'])[['dvpspm']].apply(np.nanmedian)
dvpspm_median.name = 'dvpspm_median'
df = df.join(dvpspm_median, on=['year-month'])

dvpsxm_median = df.groupby(['year-month'])[['dvpsxm']].apply(np.nanmedian)
dvpsxm_median.name = 'dvpsxm_median'
df = df.join(dvpsxm_median, on=['year-month'])

dvrate_median = df.groupby(['year-month'])[['dvrate']].apply(np.nanmedian)
dvrate_median.name = 'dvrate_median'
df = df.join(dvrate_median, on=['year-month'])

spcsrc_median = df.groupby(['year-month'])[['spcsrc']].apply(np.nanmedian)
spcsrc_median.name = 'spcsrc_median'
df = df.join(spcsrc_median, on=['year-month'])

alpha_median = df.groupby(['year-month'])[['alpha']].apply(np.nanmedian)
alpha_median.name = 'alpha_median'
df = df.join(alpha_median, on=['year-month'])

b_hml_median = df.groupby(['year-month'])[['b_hml']].apply(np.nanmedian)
b_hml_median.name = 'b_hml_median'
df = df.join(b_hml_median, on=['year-month'])

b_mkt_median = df.groupby(['year-month'])[['b_mkt']].apply(np.nanmedian)
b_mkt_median.name = 'b_mkt_median'
df = df.join(b_mkt_median, on=['year-month'])

b_smb_median = df.groupby(['year-month'])[['b_smb']].apply(np.nanmedian)
b_smb_median.name = 'b_smb_median'
df = df.join(b_smb_median, on=['year-month'])

b_umd_median = df.groupby(['year-month'])[['b_umd']].apply(np.nanmedian)
b_umd_median.name = 'b_umd_median'
df = df.join(b_umd_median, on=['year-month'])

exret_median = df.groupby(['year-month'])[['exret']].apply(np.nanmedian)
exret_median.name = 'exret_median'
df = df.join(exret_median, on=['year-month'])

ivol_median = df.groupby(['year-month'])[['ivol']].apply(np.nanmedian)
ivol_median.name = 'ivol_median'
df = df.join(ivol_median, on=['year-month'])

n_median = df.groupby(['year-month'])[['n']].apply(np.nanmedian)
n_median.name = 'n_median'
df = df.join(n_median, on=['year-month'])

R2_median = df.groupby(['year-month'])[['R2']].apply(np.nanmedian)
R2_median.name = 'R2_median'
df = df.join(R2_median, on=['year-month'])

tvol_median = df.groupby(['year-month'])[['tvol']].apply(np.nanmedian)
tvol_median.name = 'tvol_median'
df = df.join(tvol_median, on=['year-month'])

BUYPCT_median = df.groupby(['year-month'])[['BUYPCT']].apply(np.nanmedian)
BUYPCT_median.name = 'BUYPCT_median'
df = df.join(BUYPCT_median, on=['year-month'])

HOLDPCT_median = df.groupby(['year-month'])[['HOLDPCT']].apply(np.nanmedian)
HOLDPCT_median.name = 'HOLDPCT_median'
df = df.join(HOLDPCT_median, on=['year-month'])

MEANREC_median = df.groupby(['year-month'])[['MEANREC']].apply(np.nanmedian)
MEANREC_median.name = 'MEANREC_median'
df = df.join(MEANREC_median, on=['year-month'])

MEDREC_median = df.groupby(['year-month'])[['MEDREC']].apply(np.nanmedian)
MEDREC_median.name = 'MEDREC_median'
df = df.join(MEDREC_median, on=['year-month'])

NUMDOWN_median = df.groupby(['year-month'])[['NUMDOWN']].apply(np.nanmedian)
NUMDOWN_median.name = 'NUMDOWN_median'
df = df.join(NUMDOWN_median, on=['year-month'])

NUMREC_median = df.groupby(['year-month'])[['NUMREC']].apply(np.nanmedian)
NUMREC_median.name = 'NUMREC_median'
df = df.join(NUMREC_median, on=['year-month'])

NUMUP_median = df.groupby(['year-month'])[['NUMUP']].apply(np.nanmedian)
NUMUP_median.name = 'NUMUP_median'
df = df.join(NUMUP_median, on=['year-month'])

SELLPCT_median = df.groupby(['year-month'])[['SELLPCT']].apply(np.nanmedian)
SELLPCT_median.name = 'SELLPCT_median'
df = df.join(SELLPCT_median, on=['year-month'])

STDEV_median = df.groupby(['year-month'])[['STDEV']].apply(np.nanmedian)
STDEV_median.name = 'STDEV_median'
df = df.join(STDEV_median, on=['year-month'])

ACTUAL_EPS_median = df.groupby(['year-month'])[['ACTUAL_EPS']].apply(np.nanmedian)
ACTUAL_EPS_median.name = 'ACTUAL_EPS_median'
df.join(ACTUAL_EPS_median, on=['year-month'])

CONSENSUS_EPS_median = df.groupby(['year-month'])[['CONSENSUS_EPS']].apply(np.nanmedian)
CONSENSUS_EPS_median.name = 'CONSENSUS_EPS_median'
df.join(CONSENSUS_EPS_median, on=['year-month'])

CONSENSUS_STD_median = df.groupby(['year-month'])[['CONSENSUS_STD']].apply(np.nanmedian)
CONSENSUS_STD_median.name = 'CONSENSUS_STD_median'
df.join(CONSENSUS_STD_median, on=['year-month'])

NUMBER_OF_EST_median = df.groupby(['year-month'])[['NUMBER_OF_EST']].apply(np.nanmedian)
NUMBER_OF_EST_median.name = 'NUMBER_OF_EST_median'
df.join(NUMBER_OF_EST_median, on=['year-month'])

SURPRISE_PCT_median = df.groupby(['year-month'])[['SURPRISE_PCT']].apply(np.nanmedian)
SURPRISE_PCT_median.name = 'SURPRISE_PCT_median'
df.join(SURPRISE_PCT_median, on=['year-month'])

C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:717: RuntimeWarning: All-NaN slice encountered
  warnings.warn("All-NaN slice encountered", RuntimeWarning)


GVKEY    tic                          conm  \
0        1045    AAL   AMERICAN AIRLINES GROUP INC   
1        1050   CECE       CECO ENVIRONMENTAL CORP   
2        1075    PNW    PINNACLE WEST CAPITAL CORP   
3        1076    AAN                   AARON'S INC   
4        1078    ABT           ABBOTT LABORATORIES   
5        1078    ABT           ABBOTT LABORATORIES   
6        1104    ACU              ACME UNITED CORP   
7        1117    RWC            RELM WIRELESS CORP   
8        1121     AE  ADAMS RESOURCES & ENERGY INC   
9        1161    AMD        ADVANCED MICRO DEVICES   
10       1177    AET                     AETNA INC   
11       1230    ALK          ALASKA AIR GROUP INC   
12       1234   ATRI                   ATRION CORP   
13       1254   MATX                    MATSON INC   
14       1257    ALX               ALEXANDER'S INC   
15       1274      Y                ALLEGHANY CORP   
16       1274      Y                ALLEGHANY CORP   
17       1300    HON   HONEYWELL INTERNATIONAL INC   
18       1356   AA.3                     ALCOA INC   
19       1380    HES                     HESS CORP   
20       1414    PRI                 PRIMERICA INC   
21       1439   ECOL                US ECOLOGY INC   
22       1440    AEP    AMERICAN ELECTRIC POWER CO   
23       1447    AXP           AMERICAN EXPRESS CO   
24       1449    AFL                     AFLAC INC   
25       1487    AIG  AMERICAN INTERNATIONAL GROUP   
26       1526   ANAT   AMERICAN NATIONAL INSURANCE   
27       1545    ARL     AMERICAN REALTY INVESTORS   
28       1559    AMS    AMERICAN SHARED HSPTL SERV   
29       1585    AVD        AMERICAN VANGUARD CORP   
30       1598    AME                    AMETEK INC   
31       1602   AMGN                     AMGEN INC   
32       1613     AP         AMPCO-PITTSBURGH CORP   
33       1659   ANDE                 ANDERSONS INC   
34       1678    APA                   APACHE CORP   
35       1712   TREC             TRECORA RESOURCES   
36       1722    ADM     ARCHER-DANIELS-MIDLAND CO   
37       1743   ARCB                  ARCBEST CORP   
38       1773    ARW         ARROW ELECTRONICS INC   
39       1823   ATRO                ASTRONICS CORP   
40       1837    SO7               SOUTHERN GAS CO   
41       1906   AVHI                 A V HOMES INC   
42       1913    AVY           AVERY DENNISON CORP   
43       1920    AVP                 AVON PRODUCTS   
44       1968    BMI              BADGER METER INC   
45       1976    BHI              BAKER HUGHES INC   
46       1979   BCPC           BALCHEM CORP  -CL B   
47       1982  BWINB        BALDWIN & LYONS  -CL B   
48       1982  BWINB        BALDWIN & LYONS  -CL B   
49       1982  BWINB        BALDWIN & LYONS  -CL B   
50       1982  BWINB        BALDWIN & LYONS  -CL B   
51       1988    BLL                     BALL CORP   
52       2002   BPOP                   POPULAR INC   
53       2005    BOH           BANK OF HAWAII CORP   
54       2019     BK  BANK OF NEW YORK MELLON CORP   
55       2044    BCR               BARD (C.R.) INC   
56       2049      B              BARNES GROUP INC   
57       2086    BAX      BAXTER INTERNATIONAL INC   
58       2124  BELFB                  BEL FUSE INC   
59       2124  BELFB                  BEL FUSE INC   
60       2124  BELFB                  BEL FUSE INC   
61       2124  BELFB                  BEL FUSE INC   
62       2136     VZ    VERIZON COMMUNICATIONS INC   
63       2154    BMS                  BEMIS CO INC   
64       2176  BRK.B            BERKSHIRE HATHAWAY   
65       2176  BRK.B            BERKSHIRE HATHAWAY   
66       2176  BRK.B            BERKSHIRE HATHAWAY   
67       2176  BRK.B            BERKSHIRE HATHAWAY   
68       2220    BIO      BIO-RAD LABORATORIES INC   
69       2220    BIO      BIO-RAD LABORATORIES INC   
70       2220    BIO      BIO-RAD LABORATORIES INC   
71       2220    BIO      BIO-RAD LABORATORIES INC   
72       2259    BKH              BLACK HILLS CORP   
73       227

In [63]:
forward_one_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_one_month_return']].apply(np.nanmedian)
forward_one_month_return_sector_median.name = 'forward_one_month_return_sector_median'
df = df.join(forward_one_month_return_sector_median, on=['year-month', 'industry'])

forward_two_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_two_month_return']].apply(np.nanmedian)
forward_two_month_return_sector_median.name = 'forward_two_month_return_sector_median'
df = df.join(forward_two_month_return_sector_median, on=['year-month', 'industry'])

forward_three_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_three_month_return']].apply(np.nanmedian)
forward_three_month_return_sector_median.name = 'forward_three_month_return_sector_median'
df = df.join(forward_three_month_return_sector_median, on=['year-month', 'industry'])

forward_four_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_four_month_return']].apply(np.nanmedian)
forward_four_month_return_sector_median.name = 'forward_four_month_return_sector_median'
df = df.join(forward_four_month_return_sector_median, on=['year-month', 'industry'])

forward_five_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_five_month_return']].apply(np.nanmedian)
forward_five_month_return_sector_median.name = 'forward_five_month_return_sector_median'
df = df.join(forward_five_month_return_sector_median, on=['year-month', 'industry'])

forward_six_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_six_month_return']].apply(np.nanmedian)
forward_six_month_return_sector_median.name = 'forward_six_month_return_sector_median'
df = df.join(forward_six_month_return_sector_median, on=['year-month', 'industry'])

forward_seven_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_seven_month_return']].apply(np.nanmedian)
forward_seven_month_return_sector_median.name = 'forward_seven_month_return_sector_median'
df = df.join(forward_seven_month_return_sector_median, on=['year-month', 'industry'])

forward_eight_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_eight_month_return']].apply(np.nanmedian)
forward_eight_month_return_sector_median.name = 'forward_eight_month_return_sector_median'
df = df.join(forward_eight_month_return_sector_median, on=['year-month', 'industry'])

forward_nine_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_nine_month_return']].apply(np.nanmedian)
forward_nine_month_return_sector_median.name = 'forward_nine_month_return_sector_median'
df = df.join(forward_nine_month_return_sector_median, on=['year-month', 'industry'])

forward_ten_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_ten_month_return']].apply(np.nanmedian)
forward_ten_month_return_sector_median.name = 'forward_ten_month_return_sector_median'
df = df.join(forward_ten_month_return_sector_median, on=['year-month', 'industry'])

forward_eleven_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_eleven_month_return']].apply(np.nanmedian)
forward_eleven_month_return_sector_median.name = 'forward_eleven_month_return_sector_median'
df = df.join(forward_eleven_month_return_sector_median, on=['year-month', 'industry'])

forward_twelve_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twelve_month_return']].apply(np.nanmedian)
forward_twelve_month_return_sector_median.name = 'forward_twelve_month_return_sector_median'
df = df.join(forward_twelve_month_return_sector_median, on=['year-month', 'industry'])

forward_thirteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_thirteen_month_return']].apply(np.nanmedian)
forward_thirteen_month_return_sector_median.name = 'forward_thirteen_month_return_sector_median'
df = df.join(forward_thirteen_month_return_sector_median, on=['year-month', 'industry'])

forward_fourteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_fourteen_month_return']].apply(np.nanmedian)
forward_fourteen_month_return_sector_median.name = 'forward_fourteen_month_return_sector_median'
df = df.join(forward_fourteen_month_return_sector_median, on=['year-month', 'industry'])

forward_fifteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_fifteen_month_return']].apply(np.nanmedian)
forward_fifteen_month_return_sector_median.name = 'forward_fifteen_month_return_sector_median'
df = df.join(forward_fifteen_month_return_sector_median, on=['year-month', 'industry'])

forward_sixteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_sixteen_month_return']].apply(np.nanmedian)
forward_sixteen_month_return_sector_median.name = 'forward_sixteen_month_return_sector_median'
df = df.join(forward_sixteen_month_return_sector_median, on=['year-month', 'industry'])

forward_seventeen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_seventeen_month_return']].apply(np.nanmedian)
forward_seventeen_month_return_sector_median.name = 'forward_seventeen_month_return_sector_median'
df = df.join(forward_seventeen_month_return_sector_median, on=['year-month', 'industry'])

forward_eighteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_eighteen_month_return']].apply(np.nanmedian)
forward_eighteen_month_return_sector_median.name = 'forward_eighteen_month_return_sector_median'
df = df.join(forward_eighteen_month_return_sector_median, on=['year-month', 'industry'])

forward_nineteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_nineteen_month_return']].apply(np.nanmedian)
forward_nineteen_month_return_sector_median.name = 'forward_nineteen_month_return_sector_median'
df = df.join(forward_nineteen_month_return_sector_median, on=['year-month', 'industry'])

forward_twenty_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twenty_month_return']].apply(np.nanmedian)
forward_twenty_month_return_sector_median.name = 'forward_twenty_month_return_sector_median'
df = df.join(forward_twenty_month_return_sector_median, on=['year-month', 'industry'])

forward_twentyone_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twentyone_month_return']].apply(np.nanmedian)
forward_twentyone_month_return_sector_median.name = 'forward_twentyone_month_return_sector_median'
df = df.join(forward_twentyone_month_return_sector_median, on=['year-month', 'industry'])

forward_twentytwo_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twentytwo_month_return']].apply(np.nanmedian)
forward_twentytwo_month_return_sector_median.name = 'forward_twentytwo_month_return_sector_median'
df = df.join(forward_twentytwo_month_return_sector_median, on=['year-month', 'industry'])

forward_twentythree_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twentythree_month_return']].apply(np.nanmedian)
forward_twentythree_month_return_sector_median.name = 'forward_twentythree_month_return_sector_median'
df = df.join(forward_twentythree_month_return_sector_median, on=['year-month', 'industry'])

forward_twentyfour_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twentyfour_month_return']].apply(np.nanmedian)
forward_twentyfour_month_return_sector_median.name = 'forward_twentyfour_month_return_sector_median'
df = df.join(forward_twentyfour_month_return_sector_median, on=['year-month', 'industry'])

forward_twentyfive_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twentyfive_month_return']].apply(np.nanmedian)
forward_twentyfive_month_return_sector_median.name = 'forward_twentyfive_month_return_sector_median'
df = df.join(forward_twentyfive_month_return_sector_median, on=['year-month', 'industry'])

forward_twentysix_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twentysix_month_return']].apply(np.nanmedian)
forward_twentysix_month_return_sector_median.name = 'forward_twentysix_month_return_sector_median'
df = df.join(forward_twentysix_month_return_sector_median, on=['year-month', 'industry'])

forward_twentyseven_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twentyseven_month_return']].apply(np.nanmedian)
forward_twentyseven_month_return_sector_median.name = 'forward_twentyseven_month_return_sector_median'
df = df.join(forward_twentyseven_month_return_sector_median, on=['year-month', 'industry'])

forward_twentyeight_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twentyeight_month_return']].apply(np.nanmedian)
forward_twentyeight_month_return_sector_median.name = 'forward_twentyeight_month_return_sector_median'
df = df.join(forward_twentyeight_month_return_sector_median, on=['year-month', 'industry'])

forward_twentynine_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_twentynine_month_return']].apply(np.nanmedian)
forward_twentynine_month_return_sector_median.name = 'forward_twentynine_month_return_sector_median'
df = df.join(forward_twentynine_month_return_sector_median, on=['year-month', 'industry'])

forward_thirty_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_thirty_month_return']].apply(np.nanmedian)
forward_thirty_month_return_sector_median.name = 'forward_thirty_month_return_sector_median'
df = df.join(forward_thirty_month_return_sector_median, on=['year-month', 'industry'])

forward_thirtyone_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_thirtyone_month_return']].apply(np.nanmedian)
forward_thirtyone_month_return_sector_median.name = 'forward_thirtyone_month_return_sector_median'
df = df.join(forward_thirtyone_month_return_sector_median, on=['year-month', 'industry'])

forward_thirtytwo_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_thirtytwo_month_return']].apply(np.nanmedian)
forward_thirtytwo_month_return_sector_median.name = 'forward_thirtytwo_month_return_sector_median'
df = df.join(forward_thirtytwo_month_return_sector_median, on=['year-month', 'industry'])

forward_thirtythree_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_thirtythree_month_return']].apply(np.nanmedian)
forward_thirtythree_month_return_sector_median.name = 'forward_thirtythree_month_return_sector_median'
df = df.join(forward_thirtythree_month_return_sector_median, on=['year-month', 'industry'])

forward_thirtyfour_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_thirtyfour_month_return']].apply(np.nanmedian)
forward_thirtyfour_month_return_sector_median.name = 'forward_thirtyfour_month_return_sector_median'
df = df.join(forward_thirtyfour_month_return_sector_median, on=['year-month', 'industry'])

forward_thirtyfive_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_thirtyfive_month_return']].apply(np.nanmedian)
forward_thirtyfive_month_return_sector_median.name = 'forward_thirtyfive_month_return_sector_median'
df = df.join(forward_thirtyfive_month_return_sector_median, on=['year-month', 'industry'])

forward_thirtysix_month_return_sector_median = df.groupby(['year-month', 'industry'])[['forward_thirtysix_month_return']].apply(np.nanmedian)
forward_thirtysix_month_return_sector_median.name = 'forward_thirtysix_month_return_sector_median'
df = df.join(forward_thirtysix_month_return_sector_median, on=['year-month', 'industry'])

past_one_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_one_month_return']].apply(np.nanmedian)
past_one_month_return_sector_median.name = 'past_one_month_return_sector_median'
df = df.join(past_one_month_return_sector_median, on=['year-month', 'industry'])

past_two_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_two_month_return']].apply(np.nanmedian)
past_two_month_return_sector_median.name = 'past_two_month_return_sector_median'
df = df.join(past_two_month_return_sector_median, on=['year-month', 'industry'])

past_three_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_three_month_return']].apply(np.nanmedian)
past_three_month_return_sector_median.name = 'past_three_month_return_sector_median'
df = df.join(past_three_month_return_sector_median, on=['year-month', 'industry'])

past_four_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_four_month_return']].apply(np.nanmedian)
past_four_month_return_sector_median.name = 'past_four_month_return_sector_median'
df = df.join(past_four_month_return_sector_median, on=['year-month', 'industry'])

past_five_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_five_month_return']].apply(np.nanmedian)
past_five_month_return_sector_median.name = 'past_five_month_return_sector_median'
df = df.join(past_five_month_return_sector_median, on=['year-month', 'industry'])

past_six_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_six_month_return']].apply(np.nanmedian)
past_six_month_return_sector_median.name = 'past_six_month_return_sector_median'
df = df.join(past_six_month_return_sector_median, on=['year-month', 'industry'])

past_seven_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_seven_month_return']].apply(np.nanmedian)
past_seven_month_return_sector_median.name = 'past_seven_month_return_sector_median'
df = df.join(past_seven_month_return_sector_median, on=['year-month', 'industry'])

past_eight_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_eight_month_return']].apply(np.nanmedian)
past_eight_month_return_sector_median.name = 'past_eight_month_return_sector_median'
df = df.join(past_eight_month_return_sector_median, on=['year-month', 'industry'])

past_nine_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_nine_month_return']].apply(np.nanmedian)
past_nine_month_return_sector_median.name = 'past_nine_month_return_sector_median'
df = df.join(past_nine_month_return_sector_median, on=['year-month', 'industry'])

past_ten_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_ten_month_return']].apply(np.nanmedian)
past_ten_month_return_sector_median.name = 'past_ten_month_return_sector_median'
df = df.join(past_ten_month_return_sector_median, on=['year-month', 'industry'])

past_eleven_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_eleven_month_return']].apply(np.nanmedian)
past_eleven_month_return_sector_median.name = 'past_eleven_month_return_sector_median'
df = df.join(past_eleven_month_return_sector_median, on=['year-month', 'industry'])

past_twelve_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twelve_month_return']].apply(np.nanmedian)
past_twelve_month_return_sector_median.name = 'past_twelve_month_return_sector_median'
df = df.join(past_twelve_month_return_sector_median, on=['year-month', 'industry'])

past_thirteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_thirteen_month_return']].apply(np.nanmedian)
past_thirteen_month_return_sector_median.name = 'past_thirteen_month_return_sector_median'
df = df.join(past_thirteen_month_return_sector_median, on=['year-month', 'industry'])

past_fourteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_fourteen_month_return']].apply(np.nanmedian)
past_fourteen_month_return_sector_median.name = 'past_fourteen_month_return_sector_median'
df = df.join(past_fourteen_month_return_sector_median, on=['year-month', 'industry'])

past_fifteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_fifteen_month_return']].apply(np.nanmedian)
past_fifteen_month_return_sector_median.name = 'past_fifteen_month_return_sector_median'
df = df.join(past_fifteen_month_return_sector_median, on=['year-month', 'industry'])

past_sixteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_sixteen_month_return']].apply(np.nanmedian)
past_sixteen_month_return_sector_median.name = 'past_sixteen_month_return_sector_median'
df = df.join(past_sixteen_month_return_sector_median, on=['year-month', 'industry'])

past_seventeen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_seventeen_month_return']].apply(np.nanmedian)
past_seventeen_month_return_sector_median.name = 'past_seventeen_month_return_sector_median'
df = df.join(past_seventeen_month_return_sector_median, on=['year-month', 'industry'])

past_eighteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_eighteen_month_return']].apply(np.nanmedian)
past_eighteen_month_return_sector_median.name = 'past_eighteen_month_return_sector_median'
df = df.join(past_eighteen_month_return_sector_median, on=['year-month', 'industry'])

past_nineteen_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_nineteen_month_return']].apply(np.nanmedian)
past_nineteen_month_return_sector_median.name = 'past_nineteen_month_return_sector_median'
df = df.join(past_nineteen_month_return_sector_median, on=['year-month', 'industry'])

past_twenty_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twenty_month_return']].apply(np.nanmedian)
past_twenty_month_return_sector_median.name = 'past_twenty_month_return_sector_median'
df = df.join(past_twenty_month_return_sector_median, on=['year-month', 'industry'])

past_twentyone_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twentyone_month_return']].apply(np.nanmedian)
past_twentyone_month_return_sector_median.name = 'past_twentyone_month_return_sector_median'
df = df.join(past_twentyone_month_return_sector_median, on=['year-month', 'industry'])

past_twentytwo_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twentytwo_month_return']].apply(np.nanmedian)
past_twentytwo_month_return_sector_median.name = 'past_twentytwo_month_return_sector_median'
df = df.join(past_twentytwo_month_return_sector_median, on=['year-month', 'industry'])

past_twentythree_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twentythree_month_return']].apply(np.nanmedian)
past_twentythree_month_return_sector_median.name = 'past_twentythree_month_return_sector_median'
df = df.join(past_twentythree_month_return_sector_median, on=['year-month', 'industry'])

past_twentyfour_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twentyfour_month_return']].apply(np.nanmedian)
past_twentyfour_month_return_sector_median.name = 'past_twentyfour_month_return_sector_median'
df = df.join(past_twentyfour_month_return_sector_median, on=['year-month', 'industry'])

past_twentyfive_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twentyfive_month_return']].apply(np.nanmedian)
past_twentyfive_month_return_sector_median.name = 'past_twentyfive_month_return_sector_median'
df = df.join(past_twentyfive_month_return_sector_median, on=['year-month', 'industry'])

past_twentysix_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twentysix_month_return']].apply(np.nanmedian)
past_twentysix_month_return_sector_median.name = 'past_twentysix_month_return_sector_median'
df = df.join(past_twentysix_month_return_sector_median, on=['year-month', 'industry'])

past_twentyseven_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twentyseven_month_return']].apply(np.nanmedian)
past_twentyseven_month_return_sector_median.name = 'past_twentyseven_month_return_sector_median'
df = df.join(past_twentyseven_month_return_sector_median, on=['year-month', 'industry'])

past_twentyeight_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twentyeight_month_return']].apply(np.nanmedian)
past_twentyeight_month_return_sector_median.name = 'past_twentyeight_month_return_sector_median'
df = df.join(past_twentyeight_month_return_sector_median, on=['year-month', 'industry'])

past_twentynine_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_twentynine_month_return']].apply(np.nanmedian)
past_twentynine_month_return_sector_median.name = 'past_twentynine_month_return_sector_median'
df = df.join(past_twentynine_month_return_sector_median, on=['year-month', 'industry'])

past_thirty_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_thirty_month_return']].apply(np.nanmedian)
past_thirty_month_return_sector_median.name = 'past_thirty_month_return_sector_median'
df = df.join(past_thirty_month_return_sector_median, on=['year-month', 'industry'])

past_thirtyone_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_thirtyone_month_return']].apply(np.nanmedian)
past_thirtyone_month_return_sector_median.name = 'past_thirtyone_month_return_sector_median'
df = df.join(past_thirtyone_month_return_sector_median, on=['year-month', 'industry'])

past_thirtytwo_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_thirtytwo_month_return']].apply(np.nanmedian)
past_thirtytwo_month_return_sector_median.name = 'past_thirtytwo_month_return_sector_median'
df = df.join(past_thirtytwo_month_return_sector_median, on=['year-month', 'industry'])

past_thirtythree_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_thirtythree_month_return']].apply(np.nanmedian)
past_thirtythree_month_return_sector_median.name = 'past_thirtythree_month_return_sector_median'
df = df.join(past_thirtythree_month_return_sector_median, on=['year-month', 'industry'])

past_thirtyfour_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_thirtyfour_month_return']].apply(np.nanmedian)
past_thirtyfour_month_return_sector_median.name = 'past_thirtyfour_month_return_sector_median'
df = df.join(past_thirtyfour_month_return_sector_median, on=['year-month', 'industry'])

past_thirtyfive_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_thirtyfive_month_return']].apply(np.nanmedian)
past_thirtyfive_month_return_sector_median.name = 'past_thirtyfive_month_return_sector_median'
df = df.join(past_thirtyfive_month_return_sector_median, on=['year-month', 'industry'])

past_thirtysix_month_return_sector_median = df.groupby(['year-month', 'industry'])[['past_thirtysix_month_return']].apply(np.nanmedian)
past_thirtysix_month_return_sector_median.name = 'past_thirtysix_month_return_sector_median'
df = df.join(past_thirtysix_month_return_sector_median, on=['year-month', 'industry'])

accrual_sector_median = df.groupby(['year-month', 'industry'])[['accrual']].apply(np.nanmedian)
accrual_sector_median.name = 'accrual_sector_median'
df = df.join(accrual_sector_median, on=['year-month', 'industry'])

adv_sale_sector_median = df.groupby(['year-month', 'industry'])[['adv_sale']].apply(np.nanmedian)
adv_sale_sector_median.name = 'adv_sale_sector_median'
df = df.join(adv_sale_sector_median, on=['year-month', 'industry'])

aftret_eq_sector_median = df.groupby(['year-month', 'industry'])[['aftret_eq']].apply(np.nanmedian)
aftret_eq_sector_median.name = 'aftret_eq_sector_median'
df = df.join(aftret_eq_sector_median, on=['year-month', 'industry'])

aftret_equity_sector_median = df.groupby(['year-month', 'industry'])[['aftret_equity']].apply(np.nanmedian)
aftret_equity_sector_median.name = 'aftret_equity_sector_median'
df = df.join(aftret_equity_sector_median, on=['year-month', 'industry'])

aftret_invcapx_sector_median = df.groupby(['year-month', 'industry'])[['aftret_invcapx']].apply(np.nanmedian)
aftret_invcapx_sector_median.name = 'aftret_invcapx_sector_median'
df = df.join(aftret_invcapx_sector_median, on=['year-month', 'industry'])

at_turn_sector_median = df.groupby(['year-month', 'industry'])[['at_turn']].apply(np.nanmedian)
at_turn_sector_median.name = 'at_turn_sector_median'
df = df.join(at_turn_sector_median, on=['year-month', 'industry'])

bm_sector_median = df.groupby(['year-month', 'industry'])[['bm']].apply(np.nanmedian)
bm_sector_median.name = 'bm_sector_median'
df = df.join(bm_sector_median, on=['year-month', 'industry'])

CAPEI_sector_median = df.groupby(['year-month', 'industry'])[['CAPEI']].apply(np.nanmedian)
CAPEI_sector_median.name = 'CAPEI_sector_median'
df = df.join(CAPEI_sector_median, on=['year-month', 'industry'])

capital_ratio_sector_median = df.groupby(['year-month', 'industry'])[['capital_ratio']].apply(np.nanmedian)
capital_ratio_sector_median.name = 'capital_ratio_sector_median'
df = df.join(capital_ratio_sector_median, on=['year-month', 'industry'])

cash_conversion_sector_median = df.groupby(['year-month', 'industry'])[['cash_conversion']].apply(np.nanmedian)
cash_conversion_sector_median.name = 'cash_conversion_sector_median'
df = df.join(cash_conversion_sector_median, on=['year-month', 'industry'])

cash_debt_sector_median = df.groupby(['year-month', 'industry'])[['cash_debt']].apply(np.nanmedian)
cash_debt_sector_median.name = 'cash_debt_sector_median'
df = df.join(cash_debt_sector_median, on=['year-month', 'industry'])

cash_lt_sector_median = df.groupby(['year-month', 'industry'])[['cash_lt']].apply(np.nanmedian)
cash_lt_sector_median.name = 'cash_lt_sector_median'
df = df.join(cash_lt_sector_median, on=['year-month', 'industry'])

cash_ratio_sector_median = df.groupby(['year-month', 'industry'])[['cash_ratio']].apply(np.nanmedian)
cash_ratio_sector_median.name = 'cash_ratio_sector_median'
df = df.join(cash_ratio_sector_median, on=['year-month', 'industry'])

cfm_sector_median = df.groupby(['year-month', 'industry'])[['cfm']].apply(np.nanmedian)
cfm_sector_median.name = 'cfm_sector_median'
df = df.join(cfm_sector_median, on=['year-month', 'industry'])

curr_debt_sector_median = df.groupby(['year-month', 'industry'])[['curr_debt']].apply(np.nanmedian)
curr_debt_sector_median.name = 'curr_debt_sector_median'
df = df.join(curr_debt_sector_median, on=['year-month', 'industry'])

curr_ratio_sector_median = df.groupby(['year-month', 'industry'])[['curr_ratio']].apply(np.nanmedian)
curr_ratio_sector_median.name = 'curr_ratio_sector_median'
df = df.join(curr_ratio_sector_median, on=['year-month', 'industry'])

de_ratio_sector_median = df.groupby(['year-month', 'industry'])[['de_ratio']].apply(np.nanmedian)
de_ratio_sector_median.name = 'de_ratio_sector_median'
df = df.join(de_ratio_sector_median, on=['year-month', 'industry'])

debt_assets_sector_median = df.groupby(['year-month', 'industry'])[['debt_assets']].apply(np.nanmedian)
debt_assets_sector_median.name = 'debt_assets_sector_median'
df = df.join(debt_assets_sector_median, on=['year-month', 'industry'])

debt_at_sector_median = df.groupby(['year-month', 'industry'])[['debt_at']].apply(np.nanmedian)
debt_at_sector_median.name = 'debt_at_sector_median'
df = df.join(debt_at_sector_median, on=['year-month', 'industry'])

debt_capital_sector_median = df.groupby(['year-month', 'industry'])[['debt_capital']].apply(np.nanmedian)
debt_capital_sector_median.name = 'debt_capital_sector_median'
df = df.join(debt_capital_sector_median, on=['year-month', 'industry'])

debt_ebitda_sector_median = df.groupby(['year-month', 'industry'])[['debt_ebitda']].apply(np.nanmedian)
debt_ebitda_sector_median.name = 'debt_ebitda_sector_median'
df = df.join(debt_ebitda_sector_median, on=['year-month', 'industry'])

debt_invcap_sector_median = df.groupby(['year-month', 'industry'])[['debt_invcap']].apply(np.nanmedian)
debt_invcap_sector_median.name = 'debt_invcap_sector_median'
df = df.join(debt_invcap_sector_median, on=['year-month', 'industry'])

DIVYIELD_sector_median = df.groupby(['year-month', 'industry'])[['DIVYIELD']].apply(np.nanmedian)
DIVYIELD_sector_median.name = 'DIVYIELD_sector_median'
df = df.join(DIVYIELD_sector_median, on=['year-month', 'industry'])

dltt_be_sector_median = df.groupby(['year-month', 'industry'])[['dltt_be']].apply(np.nanmedian)
dltt_be_sector_median.name = 'dltt_be_sector_median'
df = df.join(dltt_be_sector_median, on=['year-month', 'industry'])

dpr_sector_median = df.groupby(['year-month', 'industry'])[['dpr']].apply(np.nanmedian)
dpr_sector_median.name = 'dpr_sector_median'
df = df.join(dpr_sector_median, on=['year-month', 'industry'])

efftax_sector_median = df.groupby(['year-month', 'industry'])[['efftax']].apply(np.nanmedian)
efftax_sector_median.name = 'efftax_sector_median'
df = df.join(efftax_sector_median, on=['year-month', 'industry'])

equity_invcap_sector_median = df.groupby(['year-month', 'industry'])[['equity_invcap']].apply(np.nanmedian)
equity_invcap_sector_median.name = 'equity_invcap_sector_median'
df = df.join(equity_invcap_sector_median, on=['year-month', 'industry'])

evm_sector_median = df.groupby(['year-month', 'industry'])[['evm']].apply(np.nanmedian)
evm_sector_median.name = 'evm_sector_median'
df = df.join(evm_sector_median, on=['year-month', 'industry'])

fcf_ocf_sector_median = df.groupby(['year-month', 'industry'])[['fcf_ocf']].apply(np.nanmedian)
fcf_ocf_sector_median.name = 'fcf_ocf_sector_median'
df = df.join(fcf_ocf_sector_median, on=['year-month', 'industry'])

gpm_sector_median = df.groupby(['year-month', 'industry'])[['gpm']].apply(np.nanmedian)
gpm_sector_median.name = 'gpm_sector_median'
df = df.join(gpm_sector_median, on=['year-month', 'industry'])

GProf_sector_median = df.groupby(['year-month', 'industry'])[['GProf']].apply(np.nanmedian)
GProf_sector_median.name = 'GProf_sector_median'
df = df.join(GProf_sector_median, on=['year-month', 'industry'])

int_debt_sector_median = df.groupby(['year-month', 'industry'])[['int_debt']].apply(np.nanmedian)
int_debt_sector_median.name = 'int_debt_sector_median'
df = df.join(int_debt_sector_median, on=['year-month', 'industry'])

int_totdebt_sector_median = df.groupby(['year-month', 'industry'])[['int_totdebt']].apply(np.nanmedian)
int_totdebt_sector_median.name = 'int_totdebt_sector_median'
df = df.join(int_totdebt_sector_median, on=['year-month', 'industry'])

intcov_sector_median = df.groupby(['year-month', 'industry'])[['intcov']].apply(np.nanmedian)
intcov_sector_median.name = 'intcov_sector_median'
df = df.join(intcov_sector_median, on=['year-month', 'industry'])

intcov_ratio_sector_median = df.groupby(['year-month', 'industry'])[['intcov_ratio']].apply(np.nanmedian)
intcov_ratio_sector_median.name = 'intcov_ratio_sector_median'
df = df.join(intcov_ratio_sector_median, on=['year-month', 'industry'])

inv_turn_sector_median = df.groupby(['year-month', 'industry'])[['inv_turn']].apply(np.nanmedian)
inv_turn_sector_median.name = 'inv_turn_sector_median'
df = df.join(inv_turn_sector_median, on=['year-month', 'industry'])

invt_act_sector_median = df.groupby(['year-month', 'industry'])[['invt_act']].apply(np.nanmedian)
invt_act_sector_median.name = 'invt_act_sector_median'
df = df.join(invt_act_sector_median, on=['year-month', 'industry'])

lt_debt_sector_median = df.groupby(['year-month', 'industry'])[['lt_debt']].apply(np.nanmedian)
lt_debt_sector_median.name = 'lt_debt_sector_median'
df = df.join(lt_debt_sector_median, on=['year-month', 'industry'])

lt_ppent_sector_median = df.groupby(['year-month', 'industry'])[['lt_ppent']].apply(np.nanmedian)
lt_ppent_sector_median.name = 'lt_ppent_sector_median'
df = df.join(lt_ppent_sector_median, on=['year-month', 'industry'])

npm_sector_median = df.groupby(['year-month', 'industry'])[['npm']].apply(np.nanmedian)
npm_sector_median.name = 'npm_sector_median'
df = df.join(npm_sector_median, on=['year-month', 'industry'])

ocf_lct_sector_median = df.groupby(['year-month', 'industry'])[['ocf_lct']].apply(np.nanmedian)
ocf_lct_sector_median.name = 'ocf_lct_sector_median'
df = df.join(ocf_lct_sector_median, on=['year-month', 'industry'])

opmad_sector_median = df.groupby(['year-month', 'industry'])[['opmad']].apply(np.nanmedian)
opmad_sector_median.name = 'opmad_sector_median'
df = df.join(opmad_sector_median, on=['year-month', 'industry'])

opmbd_sector_median = df.groupby(['year-month', 'industry'])[['opmbd']].apply(np.nanmedian)
opmbd_sector_median.name = 'opmbd_sector_median'
df = df.join(opmbd_sector_median, on=['year-month', 'industry'])

pay_turn_sector_median = df.groupby(['year-month', 'industry'])[['pay_turn']].apply(np.nanmedian)
pay_turn_sector_median.name = 'pay_turn_sector_median'
df = df.join(pay_turn_sector_median, on=['year-month', 'industry'])

pcf_sector_median = df.groupby(['year-month', 'industry'])[['pcf']].apply(np.nanmedian)
pcf_sector_median.name = 'pcf_sector_median'
df = df.join(pcf_sector_median, on=['year-month', 'industry'])

pe_exi_sector_median = df.groupby(['year-month', 'industry'])[['pe_exi']].apply(np.nanmedian)
pe_exi_sector_median.name = 'pe_exi_sector_median'
df = df.join(pe_exi_sector_median, on=['year-month', 'industry'])

pe_inc_sector_median = df.groupby(['year-month', 'industry'])[['pe_inc']].apply(np.nanmedian)
pe_inc_sector_median.name = 'pe_inc_sector_median'
df = df.join(pe_inc_sector_median, on=['year-month', 'industry'])

pe_op_basic_sector_median = df.groupby(['year-month', 'industry'])[['pe_op_basic']].apply(np.nanmedian)
pe_op_basic_sector_median.name = 'pe_op_basic_sector_median'
df = df.join(pe_op_basic_sector_median, on=['year-month', 'industry'])

pe_op_dil_sector_median = df.groupby(['year-month', 'industry'])[['pe_op_dil']].apply(np.nanmedian)
pe_op_dil_sector_median.name = 'pe_op_dil_sector_median'
df = df.join(pe_op_dil_sector_median, on=['year-month', 'industry'])

PEG_1yrforward_sector_median = df.groupby(['year-month', 'industry'])[['PEG_1yrforward']].apply(np.nanmedian)
PEG_1yrforward_sector_median.name = 'PEG_1yrforward_sector_median'
df = df.join(PEG_1yrforward_sector_median, on=['year-month', 'industry'])

PEG_ltgforward_sector_median = df.groupby(['year-month', 'industry'])[['PEG_ltgforward']].apply(np.nanmedian)
PEG_ltgforward_sector_median.name = 'PEG_ltgforward_sector_median'
df = df.join(PEG_ltgforward_sector_median, on=['year-month', 'industry'])

PEG_trailing_sector_median = df.groupby(['year-month', 'industry'])[['PEG_trailing']].apply(np.nanmedian)
PEG_trailing_sector_median.name = 'PEG_trailing_sector_median'
df = df.join(PEG_trailing_sector_median, on=['year-month', 'industry'])

pretret_earnat_sector_median = df.groupby(['year-month', 'industry'])[['pretret_earnat']].apply(np.nanmedian)
pretret_earnat_sector_median.name = 'pretret_earnat_sector_median'
df = df.join(pretret_earnat_sector_median, on=['year-month', 'industry'])

pretret_noa_sector_median = df.groupby(['year-month', 'industry'])[['pretret_noa']].apply(np.nanmedian)
pretret_noa_sector_median.name = 'pretret_noa_sector_median'
df = df.join(pretret_noa_sector_median, on=['year-month', 'industry'])

profit_lct_sector_median = df.groupby(['year-month', 'industry'])[['profit_lct']].apply(np.nanmedian)
profit_lct_sector_median.name = 'profit_lct_sector_median'
df = df.join(profit_lct_sector_median, on=['year-month', 'industry'])

ps_sector_median = df.groupby(['year-month', 'industry'])[['ps']].apply(np.nanmedian)
ps_sector_median.name = 'ps_sector_median'
df = df.join(ps_sector_median, on=['year-month', 'industry'])

ptb_sector_median = df.groupby(['year-month', 'industry'])[['ptb']].apply(np.nanmedian)
ptb_sector_median.name = 'ptb_sector_median'
df = df.join(ptb_sector_median, on=['year-month', 'industry'])

ptpm_sector_median = df.groupby(['year-month', 'industry'])[['ptpm']].apply(np.nanmedian)
ptpm_sector_median.name = 'ptpm_sector_median'
df = df.join(ptpm_sector_median, on=['year-month', 'industry'])

quick_ratio_sector_median = df.groupby(['year-month', 'industry'])[['quick_ratio']].apply(np.nanmedian)
quick_ratio_sector_median.name = 'quick_ratio_sector_median'
df = df.join(quick_ratio_sector_median, on=['year-month', 'industry'])

rd_sale_sector_median = df.groupby(['year-month', 'industry'])[['rd_sale']].apply(np.nanmedian)
rd_sale_sector_median.name = 'rd_sale_sector_median'
df = df.join(rd_sale_sector_median, on=['year-month', 'industry'])

rect_act_sector_median = df.groupby(['year-month', 'industry'])[['rect_act']].apply(np.nanmedian)
rect_act_sector_median.name = 'rect_act_sector_median'
df = df.join(rect_act_sector_median, on=['year-month', 'industry'])

rect_turn_sector_median = df.groupby(['year-month', 'industry'])[['rect_turn']].apply(np.nanmedian)
rect_turn_sector_median.name = 'rect_turn_sector_median'
df = df.join(rect_turn_sector_median, on=['year-month', 'industry'])

roa_sector_median = df.groupby(['year-month', 'industry'])[['roa']].apply(np.nanmedian)
roa_sector_median.name = 'roa_sector_median'
df = df.join(roa_sector_median, on=['year-month', 'industry'])

roce_sector_median = df.groupby(['year-month', 'industry'])[['roce']].apply(np.nanmedian)
roce_sector_median.name = 'roce_sector_median'
df = df.join(roce_sector_median, on=['year-month', 'industry'])

roe_sector_median = df.groupby(['year-month', 'industry'])[['roe']].apply(np.nanmedian)
roe_sector_median.name = 'roe_sector_median'
df = df.join(roe_sector_median, on=['year-month', 'industry'])

sale_equity_sector_median = df.groupby(['year-month', 'industry'])[['sale_equity']].apply(np.nanmedian)
sale_equity_sector_median.name = 'sale_equity_sector_median'
df = df.join(sale_equity_sector_median, on=['year-month', 'industry'])

sale_invcap_sector_median = df.groupby(['year-month', 'industry'])[['sale_invcap']].apply(np.nanmedian)
sale_invcap_sector_median.name = 'sale_invcap_sector_median'
df = df.join(sale_invcap_sector_median, on=['year-month', 'industry'])

sale_nwc_sector_median = df.groupby(['year-month', 'industry'])[['sale_nwc']].apply(np.nanmedian)
sale_nwc_sector_median.name = 'sale_nwc_sector_median'
df = df.join(sale_nwc_sector_median, on=['year-month', 'industry'])

short_debt_sector_median = df.groupby(['year-month', 'industry'])[['short_debt']].apply(np.nanmedian)
short_debt_sector_median.name = 'short_debt_sector_median'
df = df.join(short_debt_sector_median, on=['year-month', 'industry'])

staff_sale_sector_median = df.groupby(['year-month', 'industry'])[['staff_sale']].apply(np.nanmedian)
staff_sale_sector_median.name = 'staff_sale_sector_median'
df = df.join(staff_sale_sector_median, on=['year-month', 'industry'])

totdebt_invcap_sector_median = df.groupby(['year-month', 'industry'])[['totdebt_invcap']].apply(np.nanmedian)
totdebt_invcap_sector_median.name = 'totdebt_invcap_sector_median'
df = df.join(totdebt_invcap_sector_median, on=['year-month', 'industry'])

dvpspm_sector_median = df.groupby(['year-month', 'industry'])[['dvpspm']].apply(np.nanmedian)
dvpspm_sector_median.name = 'dvpspm_sector_median'
df = df.join(dvpspm_sector_median, on=['year-month', 'industry'])

dvpsxm_sector_median = df.groupby(['year-month', 'industry'])[['dvpsxm']].apply(np.nanmedian)
dvpsxm_sector_median.name = 'dvpsxm_sector_median'
df = df.join(dvpsxm_sector_median, on=['year-month', 'industry'])

dvrate_sector_median = df.groupby(['year-month', 'industry'])[['dvrate']].apply(np.nanmedian)
dvrate_sector_median.name = 'dvrate_sector_median'
df = df.join(dvrate_sector_median, on=['year-month', 'industry'])

spcsrc_sector_median = df.groupby(['year-month', 'industry'])[['spcsrc']].apply(np.nanmedian)
spcsrc_sector_median.name = 'spcsrc_sector_median'
df = df.join(spcsrc_sector_median, on=['year-month', 'industry'])

alpha_sector_median = df.groupby(['year-month', 'industry'])[['alpha']].apply(np.nanmedian)
alpha_sector_median.name = 'alpha_sector_median'
df = df.join(alpha_sector_median, on=['year-month', 'industry'])

b_hml_sector_median = df.groupby(['year-month', 'industry'])[['b_hml']].apply(np.nanmedian)
b_hml_sector_median.name = 'b_hml_sector_median'
df = df.join(b_hml_sector_median, on=['year-month', 'industry'])

b_mkt_sector_median = df.groupby(['year-month', 'industry'])[['b_mkt']].apply(np.nanmedian)
b_mkt_sector_median.name = 'b_mkt_sector_median'
df = df.join(b_mkt_sector_median, on=['year-month', 'industry'])

b_smb_sector_median = df.groupby(['year-month', 'industry'])[['b_smb']].apply(np.nanmedian)
b_smb_sector_median.name = 'b_smb_sector_median'
df = df.join(b_smb_sector_median, on=['year-month', 'industry'])

b_umd_sector_median = df.groupby(['year-month', 'industry'])[['b_umd']].apply(np.nanmedian)
b_umd_sector_median.name = 'b_umd_sector_median'
df = df.join(b_umd_sector_median, on=['year-month', 'industry'])

exret_sector_median = df.groupby(['year-month', 'industry'])[['exret']].apply(np.nanmedian)
exret_sector_median.name = 'exret_sector_median'
df = df.join(exret_sector_median, on=['year-month', 'industry'])

ivol_sector_median = df.groupby(['year-month', 'industry'])[['ivol']].apply(np.nanmedian)
ivol_sector_median.name = 'ivol_sector_median'
df = df.join(ivol_sector_median, on=['year-month', 'industry'])

n_sector_median = df.groupby(['year-month', 'industry'])[['n']].apply(np.nanmedian)
n_sector_median.name = 'n_sector_median'
df = df.join(n_sector_median, on=['year-month', 'industry'])

R2_sector_median = df.groupby(['year-month', 'industry'])[['R2']].apply(np.nanmedian)
R2_sector_median.name = 'R2_sector_median'
df = df.join(R2_sector_median, on=['year-month', 'industry'])

tvol_sector_median = df.groupby(['year-month', 'industry'])[['tvol']].apply(np.nanmedian)
tvol_sector_median.name = 'tvol_sector_median'
df = df.join(tvol_sector_median, on=['year-month', 'industry'])

BUYPCT_sector_median = df.groupby(['year-month', 'industry'])[['BUYPCT']].apply(np.nanmedian)
BUYPCT_sector_median.name = 'BUYPCT_sector_median'
df = df.join(BUYPCT_sector_median, on=['year-month', 'industry'])

HOLDPCT_sector_median = df.groupby(['year-month', 'industry'])[['HOLDPCT']].apply(np.nanmedian)
HOLDPCT_sector_median.name = 'HOLDPCT_sector_median'
df = df.join(HOLDPCT_sector_median, on=['year-month', 'industry'])

MEANREC_sector_median = df.groupby(['year-month', 'industry'])[['MEANREC']].apply(np.nanmedian)
MEANREC_sector_median.name = 'MEANREC_sector_median'
df = df.join(MEANREC_sector_median, on=['year-month', 'industry'])

MEDREC_sector_median = df.groupby(['year-month', 'industry'])[['MEDREC']].apply(np.nanmedian)
MEDREC_sector_median.name = 'MEDREC_sector_median'
df = df.join(MEDREC_sector_median, on=['year-month', 'industry'])

NUMDOWN_sector_median = df.groupby(['year-month', 'industry'])[['NUMDOWN']].apply(np.nanmedian)
NUMDOWN_sector_median.name = 'NUMDOWN_sector_median'
df = df.join(NUMDOWN_sector_median, on=['year-month', 'industry'])

NUMREC_sector_median = df.groupby(['year-month', 'industry'])[['NUMREC']].apply(np.nanmedian)
NUMREC_sector_median.name = 'NUMREC_sector_median'
df = df.join(NUMREC_sector_median, on=['year-month', 'industry'])

NUMUP_sector_median = df.groupby(['year-month', 'industry'])[['NUMUP']].apply(np.nanmedian)
NUMUP_sector_median.name = 'NUMUP_sector_median'
df = df.join(NUMUP_sector_median, on=['year-month', 'industry'])

SELLPCT_sector_median = df.groupby(['year-month', 'industry'])[['SELLPCT']].apply(np.nanmedian)
SELLPCT_sector_median.name = 'SELLPCT_sector_median'
df = df.join(SELLPCT_sector_median, on=['year-month', 'industry'])

STDEV_sector_median = df.groupby(['year-month', 'industry'])[['STDEV']].apply(np.nanmedian)
STDEV_sector_median.name = 'STDEV_sector_median'
df = df.join(STDEV_sector_median, on=['year-month', 'industry'])

ACTUAL_EPS_sector_median = df.groupby(['year-month', 'industry'])[['ACTUAL_EPS']].apply(np.nanmedian)
ACTUAL_EPS_sector_median.name = 'ACTUAL_EPS_sector_median'
df = df.join(ACTUAL_EPS_sector_median, on=['year-month', 'industry'])

CONSENSUS_EPS_sector_median = df.groupby(['year-month', 'industry'])[['CONSENSUS_EPS']].apply(np.nanmedian)
CONSENSUS_EPS_sector_median.name = 'CONSENSUS_EPS_sector_median'
df = df.join(CONSENSUS_EPS_sector_median, on=['year-month', 'industry'])

CONSENSUS_STD_sector_median = df.groupby(['year-month', 'industry'])[['CONSENSUS_STD']].apply(np.nanmedian)
CONSENSUS_STD_sector_median.name = 'CONSENSUS_STD_sector_median'
df = df.join(CONSENSUS_STD_sector_median, on=['year-month', 'industry'])

NUMBER_OF_EST_sector_median = df.groupby(['year-month', 'industry'])[['NUMBER_OF_EST']].apply(np.nanmedian)
NUMBER_OF_EST_sector_median.name = 'NUMBER_OF_EST_sector_median'
df = df.join(NUMBER_OF_EST_sector_median, on=['year-month', 'industry'])

SURPRISE_PCT_sector_median = df.groupby(['year-month', 'industry'])[['SURPRISE_PCT']].apply(np.nanmedian)
SURPRISE_PCT_sector_median.name = 'SURPRISE_PCT_sector_median'
df = df.join(SURPRISE_PCT_sector_median, on=['year-month', 'industry'])

C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:717: RuntimeWarning: All-NaN slice encountered
  warnings.warn("All-NaN slice encountered", RuntimeWarning)


In [64]:
df.head(10)

GVKEY   tic                          conm                industry  \
0   1045   AAL   AMERICAN AIRLINES GROUP INC             Industrials   
1   1050  CECE       CECO ENVIRONMENTAL CORP             Industrials   
2   1075   PNW    PINNACLE WEST CAPITAL CORP               Utilities   
3   1076   AAN                   AARON'S INC  Consumer Discretionary   
4   1078   ABT           ABBOTT LABORATORIES             Health Care   
5   1078   ABT           ABBOTT LABORATORIES             Health Care   
6   1104   ACU              ACME UNITED CORP             Industrials   
7   1117   RWC            RELM WIRELESS CORP  Information Technology   
8   1121    AE  ADAMS RESOURCES & ENERGY INC                  Energy   
9   1161   AMD        ADVANCED MICRO DEVICES  Information Technology   

  GVKEY-year-month year-month  forward_one_month_return  \
0     1045-2015-01    2015-01                 -2.200307   
1     1050-2015-01    2015-01                  3.717201   
2     1075-2015-01    2015-01                 -8.691935   
3     1076-2015-01    2015-01                 -5.843335   
4     1078-2015-01    2015-01                  5.831099   
5     1078-2015-01    2015-01                  5.831099   
6     1104-2015-01    2015-01                  1.748724   
7     1117-2015-01    2015-01                 15.226185   
8     1121-2015-01    2015-01                 15.230875   
9     1161-2015-01    2015-01                 21.011673   

   forward_two_month_return  forward_three_month_return  \
0                  7.763420                   -1.208663   
1                -22.185362                  -13.531142   
2                 -9.162154                  -11.947686   
3                -10.510038                    7.476464   
4                  3.507596                    4.245988   
5                  3.507596                    4.245988   
6                 -2.853387                   -1.896277   
7                 13.185141                   23.947007   
8                 16.178213                  -19.447928   
9                  4.280156                  -12.062257   

   forward_four_month_return  forward_five_month_return  \
0                 -13.310781                 -18.292802   
1                 -16.758139                 -16.421029   
2                 -12.350540                 -18.148756   
3                  10.732369                  14.533202   
4                   9.141642                  10.219585   
5                   9.141642                  10.219585   
6                  -4.289051                  -3.280264   
7                  -0.174416                  -8.524140   
8                 -25.843694                 -22.528081   
9                 -11.284047                  -6.614786   

   forward_six_month_return  forward_seven_month_return  \
0                -17.955212                  -20.041269   
1                -33.608937                  -28.592724   
2                -10.358036                  -13.524775   
3                 16.968733                   19.087961   
4                 14.373570                    2.189366   
5                 14.373570                    2.189366   
6                 -2.400702                   -7.555169   
7                -36.542101                  -14.647271   
8                -17.021669                  -20.773672   
9                -24.902724                  -29.571984   

   forward_eight_month_return  forward_nine_month_return  \
0                  -20.348960                  -5.190032   
1                  -39.099046                 -33.670756   
2                   -6.828139                  -6.835474   
3                   14.287472                 -21.919913   
4                   -9.250247                   1.625125   
5                   -9.250247                   1.625125   
6                   -7.423518                 -12.174680   
7                  -18.358259                 -20.213753   
8                  -28.396324                 -22.353673   
9         

In [65]:
# Z-score denominator for securities by month, use mean absolute deviation in place of median absolute deviation is MAD = 0
if df.groupby(['year-month'])[['forward_one_month_return']].apply(mad).any() == 0:
    forward_one_month_return_mad = df.groupby(['year-month'])[['forward_one_month_return']].apply(meanad)
else:
    forward_one_month_return_mad = df.groupby(['year-month'])[['forward_one_month_return']].apply(mad)
forward_one_month_return_mad.name = 'forward_one_month_return_mad'
df = df.join(forward_one_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_two_month_return']].apply(mad).any() == 0:
    forward_two_month_return_mad = df.groupby(['year-month'])[['forward_two_month_return']].apply(meanad)
else:
    forward_two_month_return_mad = df.groupby(['year-month'])[['forward_two_month_return']].apply(mad)
forward_two_month_return_mad.name = 'forward_two_month_return_mad'
df = df.join(forward_two_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_three_month_return']].apply(mad).any() == 0:
    forward_three_month_return_mad = df.groupby(['year-month'])[['forward_three_month_return']].apply(meanad)
else:
    forward_three_month_return_mad = df.groupby(['year-month'])[['forward_three_month_return']].apply(mad)
forward_three_month_return_mad.name = 'forward_three_month_return_mad'
df = df.join(forward_three_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_four_month_return']].apply(mad).any() == 0:
    forward_four_month_return_mad = df.groupby(['year-month'])[['forward_four_month_return']].apply(meanad)
else:
    forward_four_month_return_mad = df.groupby(['year-month'])[['forward_four_month_return']].apply(mad)
forward_four_month_return_mad.name = 'forward_four_month_return_mad'
df = df.join(forward_four_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_five_month_return']].apply(mad).any() == 0:
    forward_five_month_return_mad = df.groupby(['year-month'])[['forward_five_month_return']].apply(meanad)
else:
    forward_five_month_return_mad = df.groupby(['year-month'])[['forward_five_month_return']].apply(mad)
forward_five_month_return_mad.name = 'forward_five_month_return_mad'
df = df.join(forward_five_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_six_month_return']].apply(mad).any() == 0:
    forward_six_month_return_mad = df.groupby(['year-month'])[['forward_six_month_return']].apply(meanad)
else:
    forward_six_month_return_mad = df.groupby(['year-month'])[['forward_six_month_return']].apply(mad)
forward_six_month_return_mad.name = 'forward_six_month_return_mad'
df = df.join(forward_six_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_seven_month_return']].apply(mad).any() == 0:
    forward_seven_month_return_mad = df.groupby(['year-month'])[['forward_seven_month_return']].apply(meanad)
else:
    forward_seven_month_return_mad = df.groupby(['year-month'])[['forward_seven_month_return']].apply(mad)
forward_seven_month_return_mad.name = 'forward_seven_month_return_mad'
df = df.join(forward_seven_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_eight_month_return']].apply(mad).any() == 0:
    forward_eight_month_return_mad = df.groupby(['year-month'])[['forward_eight_month_return']].apply(meanad)
else:
    forward_eight_month_return_mad = df.groupby(['year-month'])[['forward_eight_month_return']].apply(mad)
forward_eight_month_return_mad.name = 'forward_eight_month_return_mad'
df = df.join(forward_eight_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_nine_month_return']].apply(mad).any() == 0:
    forward_nine_month_return_mad = df.groupby(['year-month'])[['forward_nine_month_return']].apply(meanad)
else:
    forward_nine_month_return_mad = df.groupby(['year-month'])[['forward_nine_month_return']].apply(mad)
forward_nine_month_return_mad.name = 'forward_nine_month_return_mad'
df = df.join(forward_nine_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_ten_month_return']].apply(mad).any() == 0:
    forward_ten_month_return_mad = df.groupby(['year-month'])[['forward_ten_month_return']].apply(meanad)
else:
    forward_ten_month_return_mad = df.groupby(['year-month'])[['forward_ten_month_return']].apply(mad)
forward_ten_month_return_mad.name = 'forward_ten_month_return_mad'
df = df.join(forward_ten_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_eleven_month_return']].apply(mad).any() == 0:
    forward_eleven_month_return_mad = df.groupby(['year-month'])[['forward_eleven_month_return']].apply(meanad)
else:
    forward_eleven_month_return_mad = df.groupby(['year-month'])[['forward_eleven_month_return']].apply(mad)
forward_eleven_month_return_mad.name = 'forward_eleven_month_return_mad'
df = df.join(forward_eleven_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twelve_month_return']].apply(mad).any() == 0:
    forward_twelve_month_return_mad = df.groupby(['year-month'])[['forward_twelve_month_return']].apply(meanad)
else:
    forward_twelve_month_return_mad = df.groupby(['year-month'])[['forward_twelve_month_return']].apply(mad)
forward_twelve_month_return_mad.name = 'forward_twelve_month_return_mad'
df = df.join(forward_twelve_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_thirteen_month_return']].apply(mad).any() == 0:
    forward_thirteen_month_return_mad = df.groupby(['year-month'])[['forward_thirteen_month_return']].apply(meanad)
else:
    forward_thirteen_month_return_mad = df.groupby(['year-month'])[['forward_thirteen_month_return']].apply(mad)
forward_thirteen_month_return_mad.name = 'forward_thirteen_month_return_mad'
df = df.join(forward_thirteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_fourteen_month_return']].apply(mad).any() == 0:
    forward_fourteen_month_return_mad = df.groupby(['year-month'])[['forward_fourteen_month_return']].apply(meanad)
else:
    forward_fourteen_month_return_mad = df.groupby(['year-month'])[['forward_fourteen_month_return']].apply(mad)
forward_fourteen_month_return_mad.name = 'forward_fourteen_month_return_mad'
df = df.join(forward_fourteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_fifteen_month_return']].apply(mad).any() == 0:
    forward_fifteen_month_return_mad = df.groupby(['year-month'])[['forward_fifteen_month_return']].apply(meanad)
else:
    forward_fifteen_month_return_mad = df.groupby(['year-month'])[['forward_fifteen_month_return']].apply(mad)
forward_fifteen_month_return_mad.name = 'forward_fifteen_month_return_mad'
df = df.join(forward_fifteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_sixteen_month_return']].apply(mad).any() == 0:
    forward_sixteen_month_return_mad = df.groupby(['year-month'])[['forward_sixteen_month_return']].apply(meanad)
else:
    forward_sixteen_month_return_mad = df.groupby(['year-month'])[['forward_sixteen_month_return']].apply(mad)
forward_sixteen_month_return_mad.name = 'forward_sixteen_month_return_mad'
df = df.join(forward_sixteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_seventeen_month_return']].apply(mad).any() == 0:
    forward_seventeen_month_return_mad = df.groupby(['year-month'])[['forward_seventeen_month_return']].apply(meanad)
else:
    forward_seventeen_month_return_mad = df.groupby(['year-month'])[['forward_seventeen_month_return']].apply(mad)
forward_seventeen_month_return_mad.name = 'forward_seventeen_month_return_mad'
df = df.join(forward_seventeen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_eighteen_month_return']].apply(mad).any() == 0:
    forward_eighteen_month_return_mad = df.groupby(['year-month'])[['forward_eighteen_month_return']].apply(meanad)
else:
    forward_eighteen_month_return_mad = df.groupby(['year-month'])[['forward_eighteen_month_return']].apply(mad)
forward_eighteen_month_return_mad.name = 'forward_eighteen_month_return_mad'
df = df.join(forward_eighteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_nineteen_month_return']].apply(mad).any() == 0:
    forward_nineteen_month_return_mad = df.groupby(['year-month'])[['forward_nineteen_month_return']].apply(meanad)
else:
    forward_nineteen_month_return_mad = df.groupby(['year-month'])[['forward_nineteen_month_return']].apply(mad)
forward_nineteen_month_return_mad.name = 'forward_nineteen_month_return_mad'
df = df.join(forward_nineteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twenty_month_return']].apply(mad).any() == 0:
    forward_twenty_month_return_mad = df.groupby(['year-month'])[['forward_twenty_month_return']].apply(meanad)
else:
    forward_twenty_month_return_mad = df.groupby(['year-month'])[['forward_twenty_month_return']].apply(mad)
forward_twenty_month_return_mad.name = 'forward_twenty_month_return_mad'
df = df.join(forward_twenty_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twentyone_month_return']].apply(mad).any() == 0:
    forward_twentyone_month_return_mad = df.groupby(['year-month'])[['forward_twentyone_month_return']].apply(meanad)
else:
    forward_twentyone_month_return_mad = df.groupby(['year-month'])[['forward_twentyone_month_return']].apply(mad)
forward_twentyone_month_return_mad.name = 'forward_twentyone_month_return_mad'
df = df.join(forward_twentyone_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twentytwo_month_return']].apply(mad).any() == 0:
    forward_twentytwo_month_return_mad = df.groupby(['year-month'])[['forward_twentytwo_month_return']].apply(meanad)
else:
    forward_twentytwo_month_return_mad = df.groupby(['year-month'])[['forward_twentytwo_month_return']].apply(mad)
forward_twentytwo_month_return_mad.name = 'forward_twentytwo_month_return_mad'
df = df.join(forward_twentytwo_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twentythree_month_return']].apply(mad).any() == 0:
    forward_twentythree_month_return_mad = df.groupby(['year-month'])[['forward_twentythree_month_return']].apply(meanad)
else:
    forward_twentythree_month_return_mad = df.groupby(['year-month'])[['forward_twentythree_month_return']].apply(mad)
forward_twentythree_month_return_mad.name = 'forward_twentythree_month_return_mad'
df = df.join(forward_twentythree_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twentyfour_month_return']].apply(mad).any() == 0:
    forward_twentyfour_month_return_mad = df.groupby(['year-month'])[['forward_twentyfour_month_return']].apply(meanad)
else:
    forward_twentyfour_month_return_mad = df.groupby(['year-month'])[['forward_twentyfour_month_return']].apply(mad)
forward_twentyfour_month_return_mad.name = 'forward_twentyfour_month_return_mad'
df = df.join(forward_twentyfour_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twentyfive_month_return']].apply(mad).any() == 0:
    forward_twentyfive_month_return_mad = df.groupby(['year-month'])[['forward_twentyfive_month_return']].apply(meanad)
else:
    forward_twentyfive_month_return_mad = df.groupby(['year-month'])[['forward_twentyfive_month_return']].apply(mad)
forward_twentyfive_month_return_mad.name = 'forward_twentyfive_month_return_mad'
df = df.join(forward_twentyfive_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twentysix_month_return']].apply(mad).any() == 0:
    forward_twentysix_month_return_mad = df.groupby(['year-month'])[['forward_twentysix_month_return']].apply(meanad)
else:
    forward_twentysix_month_return_mad = df.groupby(['year-month'])[['forward_twentysix_month_return']].apply(mad)
forward_twentysix_month_return_mad.name = 'forward_twentysix_month_return_mad'
df = df.join(forward_twentysix_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twentyseven_month_return']].apply(mad).any() == 0:
    forward_twentyseven_month_return_mad = df.groupby(['year-month'])[['forward_twentyseven_month_return']].apply(meanad)
else:
    forward_twentyseven_month_return_mad = df.groupby(['year-month'])[['forward_twentyseven_month_return']].apply(mad)
forward_twentyseven_month_return_mad.name = 'forward_twentyseven_month_return_mad'
df = df.join(forward_twentyseven_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twentyeight_month_return']].apply(mad).any() == 0:
    forward_twentyeight_month_return_mad = df.groupby(['year-month'])[['forward_twentyeight_month_return']].apply(meanad)
else:
    forward_twentyeight_month_return_mad = df.groupby(['year-month'])[['forward_twentyeight_month_return']].apply(mad)
forward_twentyeight_month_return_mad.name = 'forward_twentyeight_month_return_mad'
df = df.join(forward_twentyeight_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_twentynine_month_return']].apply(mad).any() == 0:
    forward_twentynine_month_return_mad = df.groupby(['year-month'])[['forward_twentynine_month_return']].apply(meanad)
else:
    forward_twentynine_month_return_mad = df.groupby(['year-month'])[['forward_twentynine_month_return']].apply(mad)
forward_twentynine_month_return_mad.name = 'forward_twentynine_month_return_mad'
df = df.join(forward_twentynine_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_thirty_month_return']].apply(mad).any() == 0:
    forward_thirty_month_return_mad = df.groupby(['year-month'])[['forward_thirty_month_return']].apply(meanad)
else:
    forward_thirty_month_return_mad = df.groupby(['year-month'])[['forward_thirty_month_return']].apply(mad)
forward_thirty_month_return_mad.name = 'forward_thirty_month_return_mad'
df = df.join(forward_thirty_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_thirtyone_month_return']].apply(mad).any() == 0:
    forward_thirtyone_month_return_mad = df.groupby(['year-month'])[['forward_thirtyone_month_return']].apply(meanad)
else:
    forward_thirtyone_month_return_mad = df.groupby(['year-month'])[['forward_thirtyone_month_return']].apply(mad)
forward_thirtyone_month_return_mad.name = 'forward_thirtyone_month_return_mad'
df = df.join(forward_thirtyone_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_thirtytwo_month_return']].apply(mad).any() == 0:
    forward_thirtytwo_month_return_mad = df.groupby(['year-month'])[['forward_thirtytwo_month_return']].apply(meanad)
else:
    forward_thirtytwo_month_return_mad = df.groupby(['year-month'])[['forward_thirtytwo_month_return']].apply(mad)
forward_thirtytwo_month_return_mad.name = 'forward_thirtytwo_month_return_mad'
df = df.join(forward_thirtytwo_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_thirtythree_month_return']].apply(mad).any() == 0:
    forward_thirtythree_month_return_mad = df.groupby(['year-month'])[['forward_thirtythree_month_return']].apply(meanad)
else:
    forward_thirtythree_month_return_mad = df.groupby(['year-month'])[['forward_thirtythree_month_return']].apply(mad)
forward_thirtythree_month_return_mad.name = 'forward_thirtythree_month_return_mad'
df = df.join(forward_thirtythree_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_thirtyfour_month_return']].apply(mad).any() == 0:
    forward_thirtyfour_month_return_mad = df.groupby(['year-month'])[['forward_thirtyfour_month_return']].apply(meanad)
else:
    forward_thirtyfour_month_return_mad = df.groupby(['year-month'])[['forward_thirtyfour_month_return']].apply(mad)
forward_thirtyfour_month_return_mad.name = 'forward_thirtyfour_month_return_mad'
df = df.join(forward_thirtyfour_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_thirtyfive_month_return']].apply(mad).any() == 0:
    forward_thirtyfive_month_return_mad = df.groupby(['year-month'])[['forward_thirtyfive_month_return']].apply(meanad)
else:
    forward_thirtyfive_month_return_mad = df.groupby(['year-month'])[['forward_thirtyfive_month_return']].apply(mad)
forward_thirtyfive_month_return_mad.name = 'forward_thirtyfive_month_return_mad'
df = df.join(forward_thirtyfive_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['forward_thirtysix_month_return']].apply(mad).any() == 0:
    forward_thirtysix_month_return_mad = df.groupby(['year-month'])[['forward_thirtysix_month_return']].apply(meanad)
else:
    forward_thirtysix_month_return_mad = df.groupby(['year-month'])[['forward_thirtysix_month_return']].apply(mad)
forward_thirtysix_month_return_mad.name = 'forward_thirtysix_month_return_mad'
df = df.join(forward_thirtysix_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_one_month_return']].apply(mad).any() == 0:
    past_one_month_return_mad = df.groupby(['year-month'])[['past_one_month_return']].apply(meanad)
else:
    past_one_month_return_mad = df.groupby(['year-month'])[['past_one_month_return']].apply(mad)
past_one_month_return_mad.name = 'past_one_month_return_mad'
df = df.join(past_one_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_two_month_return']].apply(mad).any() == 0:
    past_two_month_return_mad = df.groupby(['year-month'])[['past_two_month_return']].apply(meanad)
else:
    past_two_month_return_mad = df.groupby(['year-month'])[['past_two_month_return']].apply(mad)
past_two_month_return_mad.name = 'past_two_month_return_mad'
df = df.join(past_two_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_three_month_return']].apply(mad).any() == 0:
    past_three_month_return_mad = df.groupby(['year-month'])[['past_three_month_return']].apply(meanad)
else:
    past_three_month_return_mad = df.groupby(['year-month'])[['past_three_month_return']].apply(mad)
past_three_month_return_mad.name = 'past_three_month_return_mad'
df = df.join(past_three_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_four_month_return']].apply(mad).any() == 0:
    past_four_month_return_mad = df.groupby(['year-month'])[['past_four_month_return']].apply(meanad)
else:
    past_four_month_return_mad = df.groupby(['year-month'])[['past_four_month_return']].apply(mad)
past_four_month_return_mad.name = 'past_four_month_return_mad'
df = df.join(past_four_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_five_month_return']].apply(mad).any() == 0:
    past_five_month_return_mad = df.groupby(['year-month'])[['past_five_month_return']].apply(meanad)
else:
    past_five_month_return_mad = df.groupby(['year-month'])[['past_five_month_return']].apply(mad)
past_five_month_return_mad.name = 'past_five_month_return_mad'
df = df.join(past_five_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_six_month_return']].apply(mad).any() == 0:
    past_six_month_return_mad = df.groupby(['year-month'])[['past_six_month_return']].apply(meanad)
else:
    past_six_month_return_mad = df.groupby(['year-month'])[['past_six_month_return']].apply(mad)
past_six_month_return_mad.name = 'past_six_month_return_mad'
df = df.join(past_six_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_seven_month_return']].apply(mad).any() == 0:
    past_seven_month_return_mad = df.groupby(['year-month'])[['past_seven_month_return']].apply(meanad)
else:
    past_seven_month_return_mad = df.groupby(['year-month'])[['past_seven_month_return']].apply(mad)
past_seven_month_return_mad.name = 'past_seven_month_return_mad'
df = df.join(past_seven_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_eight_month_return']].apply(mad).any() == 0:
    past_eight_month_return_mad = df.groupby(['year-month'])[['past_eight_month_return']].apply(meanad)
else:
    past_eight_month_return_mad = df.groupby(['year-month'])[['past_eight_month_return']].apply(mad)
past_eight_month_return_mad.name = 'past_eight_month_return_mad'
df = df.join(past_eight_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_nine_month_return']].apply(mad).any() == 0:
    past_nine_month_return_mad = df.groupby(['year-month'])[['past_nine_month_return']].apply(meanad)
else:
    past_nine_month_return_mad = df.groupby(['year-month'])[['past_nine_month_return']].apply(mad)
past_nine_month_return_mad.name = 'past_nine_month_return_mad'
df = df.join(past_nine_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_ten_month_return']].apply(mad).any() == 0:
    past_ten_month_return_mad = df.groupby(['year-month'])[['past_ten_month_return']].apply(meanad)
else:
    past_ten_month_return_mad = df.groupby(['year-month'])[['past_ten_month_return']].apply(mad)
past_ten_month_return_mad.name = 'past_ten_month_return_mad'
df = df.join(past_ten_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_eleven_month_return']].apply(mad).any() == 0:
    past_eleven_month_return_mad = df.groupby(['year-month'])[['past_eleven_month_return']].apply(meanad)
else:
    past_eleven_month_return_mad = df.groupby(['year-month'])[['past_eleven_month_return']].apply(mad)
past_eleven_month_return_mad.name = 'past_eleven_month_return_mad'
df = df.join(past_eleven_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twelve_month_return']].apply(mad).any() == 0:
    past_twelve_month_return_mad = df.groupby(['year-month'])[['past_twelve_month_return']].apply(meanad)
else:
    past_twelve_month_return_mad = df.groupby(['year-month'])[['past_twelve_month_return']].apply(mad)
past_twelve_month_return_mad.name = 'past_twelve_month_return_mad'
df = df.join(past_twelve_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_thirteen_month_return']].apply(mad).any() == 0:
    past_thirteen_month_return_mad = df.groupby(['year-month'])[['past_thirteen_month_return']].apply(meanad)
else:
    past_thirteen_month_return_mad = df.groupby(['year-month'])[['past_thirteen_month_return']].apply(mad)
past_thirteen_month_return_mad.name = 'past_thirteen_month_return_mad'
df = df.join(past_thirteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_fourteen_month_return']].apply(mad).any() == 0:
    past_fourteen_month_return_mad = df.groupby(['year-month'])[['past_fourteen_month_return']].apply(meanad)
else:
    past_fourteen_month_return_mad = df.groupby(['year-month'])[['past_fourteen_month_return']].apply(mad)
past_fourteen_month_return_mad.name = 'past_fourteen_month_return_mad'
df = df.join(past_fourteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_fifteen_month_return']].apply(mad).any() == 0:
    past_fifteen_month_return_mad = df.groupby(['year-month'])[['past_fifteen_month_return']].apply(meanad)
else:
    past_fifteen_month_return_mad = df.groupby(['year-month'])[['past_fifteen_month_return']].apply(mad)
past_fifteen_month_return_mad.name = 'past_fifteen_month_return_mad'
df = df.join(past_fifteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_sixteen_month_return']].apply(mad).any() == 0:
    past_sixteen_month_return_mad = df.groupby(['year-month'])[['past_sixteen_month_return']].apply(meanad)
else:
    past_sixteen_month_return_mad = df.groupby(['year-month'])[['past_sixteen_month_return']].apply(mad)
past_sixteen_month_return_mad.name = 'past_sixteen_month_return_mad'
df = df.join(past_sixteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_seventeen_month_return']].apply(mad).any() == 0:
    past_seventeen_month_return_mad = df.groupby(['year-month'])[['past_seventeen_month_return']].apply(meanad)
else:
    past_seventeen_month_return_mad = df.groupby(['year-month'])[['past_seventeen_month_return']].apply(mad)
past_seventeen_month_return_mad.name = 'past_seventeen_month_return_mad'
df = df.join(past_seventeen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_eighteen_month_return']].apply(mad).any() == 0:
    past_eighteen_month_return_mad = df.groupby(['year-month'])[['past_eighteen_month_return']].apply(meanad)
else:
    past_eighteen_month_return_mad = df.groupby(['year-month'])[['past_eighteen_month_return']].apply(mad)
past_eighteen_month_return_mad.name = 'past_eighteen_month_return_mad'
df = df.join(past_eighteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_nineteen_month_return']].apply(mad).any() == 0:
    past_nineteen_month_return_mad = df.groupby(['year-month'])[['past_nineteen_month_return']].apply(meanad)
else:
    past_nineteen_month_return_mad = df.groupby(['year-month'])[['past_nineteen_month_return']].apply(mad)
past_nineteen_month_return_mad.name = 'past_nineteen_month_return_mad'
df = df.join(past_nineteen_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twenty_month_return']].apply(mad).any() == 0:
    past_twenty_month_return_mad = df.groupby(['year-month'])[['past_twenty_month_return']].apply(meanad)
else:
    past_twenty_month_return_mad = df.groupby(['year-month'])[['past_twenty_month_return']].apply(mad)
past_twenty_month_return_mad.name = 'past_twenty_month_return_mad'
df = df.join(past_twenty_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twentyone_month_return']].apply(mad).any() == 0:
    past_twentyone_month_return_mad = df.groupby(['year-month'])[['past_twentyone_month_return']].apply(meanad)
else:
    past_twentyone_month_return_mad = df.groupby(['year-month'])[['past_twentyone_month_return']].apply(mad)
past_twentyone_month_return_mad.name = 'past_twentyone_month_return_mad'
df = df.join(past_twentyone_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twentytwo_month_return']].apply(mad).any() == 0:
    past_twentytwo_month_return_mad = df.groupby(['year-month'])[['past_twentytwo_month_return']].apply(meanad)
else:
    past_twentytwo_month_return_mad = df.groupby(['year-month'])[['past_twentytwo_month_return']].apply(mad)
past_twentytwo_month_return_mad.name = 'past_twentytwo_month_return_mad'
df = df.join(past_twentytwo_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twentythree_month_return']].apply(mad).any() == 0:
    past_twentythree_month_return_mad = df.groupby(['year-month'])[['past_twentythree_month_return']].apply(meanad)
else:
    past_twentythree_month_return_mad = df.groupby(['year-month'])[['past_twentythree_month_return']].apply(mad)
past_twentythree_month_return_mad.name = 'past_twentythree_month_return_mad'
df = df.join(past_twentythree_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twentyfour_month_return']].apply(mad).any() == 0:
    past_twentyfour_month_return_mad = df.groupby(['year-month'])[['past_twentyfour_month_return']].apply(meanad)
else:
    past_twentyfour_month_return_mad = df.groupby(['year-month'])[['past_twentyfour_month_return']].apply(mad)
past_twentyfour_month_return_mad.name = 'past_twentyfour_month_return_mad'
df = df.join(past_twentyfour_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twentyfive_month_return']].apply(mad).any() == 0:
    past_twentyfive_month_return_mad = df.groupby(['year-month'])[['past_twentyfive_month_return']].apply(meanad)
else:
    past_twentyfive_month_return_mad = df.groupby(['year-month'])[['past_twentyfive_month_return']].apply(mad)
past_twentyfive_month_return_mad.name = 'past_twentyfive_month_return_mad'
df = df.join(past_twentyfive_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twentysix_month_return']].apply(mad).any() == 0:
    past_twentysix_month_return_mad = df.groupby(['year-month'])[['past_twentysix_month_return']].apply(meanad)
else:
    past_twentysix_month_return_mad = df.groupby(['year-month'])[['past_twentysix_month_return']].apply(mad)
past_twentysix_month_return_mad.name = 'past_twentysix_month_return_mad'
df = df.join(past_twentysix_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twentyseven_month_return']].apply(mad).any() == 0:
    past_twentyseven_month_return_mad = df.groupby(['year-month'])[['past_twentyseven_month_return']].apply(meanad)
else:
    past_twentyseven_month_return_mad = df.groupby(['year-month'])[['past_twentyseven_month_return']].apply(mad)
past_twentyseven_month_return_mad.name = 'past_twentyseven_month_return_mad'
df = df.join(past_twentyseven_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twentyeight_month_return']].apply(mad).any() == 0:
    past_twentyeight_month_return_mad = df.groupby(['year-month'])[['past_twentyeight_month_return']].apply(meanad)
else:
    past_twentyeight_month_return_mad = df.groupby(['year-month'])[['past_twentyeight_month_return']].apply(mad)
past_twentyeight_month_return_mad.name = 'past_twentyeight_month_return_mad'
df = df.join(past_twentyeight_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_twentynine_month_return']].apply(mad).any() == 0:
    past_twentynine_month_return_mad = df.groupby(['year-month'])[['past_twentynine_month_return']].apply(meanad)
else:
    past_twentynine_month_return_mad = df.groupby(['year-month'])[['past_twentynine_month_return']].apply(mad)
past_twentynine_month_return_mad.name = 'past_twentynine_month_return_mad'
df = df.join(past_twentynine_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_thirty_month_return']].apply(mad).any() == 0:
    past_thirty_month_return_mad = df.groupby(['year-month'])[['past_thirty_month_return']].apply(meanad)
else:
    past_thirty_month_return_mad = df.groupby(['year-month'])[['past_thirty_month_return']].apply(mad)
past_thirty_month_return_mad.name = 'past_thirty_month_return_mad'
df = df.join(past_thirty_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_thirtyone_month_return']].apply(mad).any() == 0:
    past_thirtyone_month_return_mad = df.groupby(['year-month'])[['past_thirtyone_month_return']].apply(meanad)
else:
    past_thirtyone_month_return_mad = df.groupby(['year-month'])[['past_thirtyone_month_return']].apply(mad)
past_thirtyone_month_return_mad.name = 'past_thirtyone_month_return_mad'
df = df.join(past_thirtyone_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_thirtytwo_month_return']].apply(mad).any() == 0:
    past_thirtytwo_month_return_mad = df.groupby(['year-month'])[['past_thirtytwo_month_return']].apply(meanad)
else:
    past_thirtytwo_month_return_mad = df.groupby(['year-month'])[['past_thirtytwo_month_return']].apply(mad)
past_thirtytwo_month_return_mad.name = 'past_thirtytwo_month_return_mad'
df = df.join(past_thirtytwo_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_thirtythree_month_return']].apply(mad).any() == 0:
    past_thirtythree_month_return_mad = df.groupby(['year-month'])[['past_thirtythree_month_return']].apply(meanad)
else:
    past_thirtythree_month_return_mad = df.groupby(['year-month'])[['past_thirtythree_month_return']].apply(mad)
past_thirtythree_month_return_mad.name = 'past_thirtythree_month_return_mad'
df = df.join(past_thirtythree_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_thirtyfour_month_return']].apply(mad).any() == 0:
    past_thirtyfour_month_return_mad = df.groupby(['year-month'])[['past_thirtyfour_month_return']].apply(meanad)
else:
    past_thirtyfour_month_return_mad = df.groupby(['year-month'])[['past_thirtyfour_month_return']].apply(mad)
past_thirtyfour_month_return_mad.name = 'past_thirtyfour_month_return_mad'
df = df.join(past_thirtyfour_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_thirtyfive_month_return']].apply(mad).any() == 0:
    past_thirtyfive_month_return_mad = df.groupby(['year-month'])[['past_thirtyfive_month_return']].apply(meanad)
else:
    past_thirtyfive_month_return_mad = df.groupby(['year-month'])[['past_thirtyfive_month_return']].apply(mad)
past_thirtyfive_month_return_mad.name = 'past_thirtyfive_month_return_mad'
df = df.join(past_thirtyfive_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['past_thirtysix_month_return']].apply(mad).any() == 0:
    past_thirtysix_month_return_mad = df.groupby(['year-month'])[['past_thirtysix_month_return']].apply(meanad)
else:
    past_thirtysix_month_return_mad = df.groupby(['year-month'])[['past_thirtysix_month_return']].apply(mad)
past_thirtysix_month_return_mad.name = 'past_thirtysix_month_return_mad'
df = df.join(past_thirtysix_month_return_mad, on=['year-month'])

if df.groupby(['year-month'])[['accrual']].apply(mad).any() == 0:
    accrual_mad = df.groupby(['year-month'])[['accrual']].apply(meanad)
else:
    accrual_mad = df.groupby(['year-month'])[['accrual']].apply(mad)
accrual_mad.name = 'accrual_mad'
df = df.join(accrual_mad, on=['year-month'])

if df.groupby(['year-month'])[['adv_sale']].apply(mad).any() == 0:
    adv_sale_mad = df.groupby(['year-month'])[['adv_sale']].apply(meanad)
else:
    adv_sale_mad = df.groupby(['year-month'])[['adv_sale']].apply(mad)
adv_sale_mad.name = 'adv_sale_mad'
df = df.join(adv_sale_mad, on=['year-month'])

if df.groupby(['year-month'])[['aftret_eq']].apply(mad).any() == 0:
    aftret_eq_mad = df.groupby(['year-month'])[['aftret_eq']].apply(meanad)
else:
    aftret_eq_mad = df.groupby(['year-month'])[['aftret_eq']].apply(mad)
aftret_eq_mad.name = 'aftret_eq_mad'
df = df.join(aftret_eq_mad, on=['year-month'])

if df.groupby(['year-month'])[['aftret_equity']].apply(mad).any() == 0:
    aftret_equity_mad = df.groupby(['year-month'])[['aftret_equity']].apply(meanad)
else:
    aftret_equity_mad = df.groupby(['year-month'])[['aftret_equity']].apply(mad)
aftret_equity_mad.name = 'aftret_equity_mad'
df = df.join(aftret_equity_mad, on=['year-month'])

if df.groupby(['year-month'])[['aftret_invcapx']].apply(mad).any() == 0:
    aftret_invcapx_mad = df.groupby(['year-month'])[['aftret_invcapx']].apply(meanad)
else:
    aftret_invcapx_mad = df.groupby(['year-month'])[['aftret_invcapx']].apply(mad)
aftret_invcapx_mad.name = 'aftret_invcapx_mad'
df = df.join(aftret_invcapx_mad, on=['year-month'])

if df.groupby(['year-month'])[['at_turn']].apply(mad).any() == 0:
    at_turn_mad = df.groupby(['year-month'])[['at_turn']].apply(meanad)
else:
    at_turn_mad = df.groupby(['year-month'])[['at_turn']].apply(mad)
at_turn_mad.name = 'at_turn_mad'
df = df.join(at_turn_mad, on=['year-month'])

if df.groupby(['year-month'])[['bm']].apply(mad).any() == 0:
    bm_mad = df.groupby(['year-month'])[['bm']].apply(meanad)
else:
    bm_mad = df.groupby(['year-month'])[['bm']].apply(mad)
bm_mad.name = 'bm_mad'
df = df.join(bm_mad, on=['year-month'])

if df.groupby(['year-month'])[['CAPEI']].apply(mad).any() == 0:
    CAPEI_mad = df.groupby(['year-month'])[['CAPEI']].apply(meanad)
else:
    CAPEI_mad = df.groupby(['year-month'])[['CAPEI']].apply(mad)
CAPEI_mad.name = 'CAPEI_mad'
df = df.join(CAPEI_mad, on=['year-month'])

if df.groupby(['year-month'])[['capital_ratio']].apply(mad).any() == 0:
    capital_ratio_mad = df.groupby(['year-month'])[['capital_ratio']].apply(meanad)
else:
    capital_ratio_mad = df.groupby(['year-month'])[['capital_ratio']].apply(mad)
capital_ratio_mad.name = 'capital_ratio_mad'
df = df.join(capital_ratio_mad, on=['year-month'])

if df.groupby(['year-month'])[['cash_conversion']].apply(mad).any() == 0:
    cash_conversion_mad = df.groupby(['year-month'])[['cash_conversion']].apply(meanad)
else:
    cash_conversion_mad = df.groupby(['year-month'])[['cash_conversion']].apply(mad)
cash_conversion_mad.name = 'cash_conversion_mad'
df = df.join(cash_conversion_mad, on=['year-month'])

if df.groupby(['year-month'])[['cash_debt']].apply(mad).any() == 0:
    cash_debt_mad = df.groupby(['year-month'])[['cash_debt']].apply(meanad)
else:
    cash_debt_mad = df.groupby(['year-month'])[['cash_debt']].apply(mad)
cash_debt_mad.name = 'cash_debt_mad'
df = df.join(cash_debt_mad, on=['year-month'])

if df.groupby(['year-month'])[['cash_lt']].apply(mad).any() == 0:
    cash_lt_mad = df.groupby(['year-month'])[['cash_lt']].apply(meanad)
else:
    cash_lt_mad = df.groupby(['year-month'])[['cash_lt']].apply(mad)
cash_lt_mad.name = 'cash_lt_mad'
df = df.join(cash_lt_mad, on=['year-month'])

if df.groupby(['year-month'])[['cash_ratio']].apply(mad).any() == 0:
    cash_ratio_mad = df.groupby(['year-month'])[['cash_ratio']].apply(meanad)
else:
    cash_ratio_mad = df.groupby(['year-month'])[['cash_ratio']].apply(mad)
cash_ratio_mad.name = 'cash_ratio_mad'
df = df.join(cash_ratio_mad, on=['year-month'])

if df.groupby(['year-month'])[['cfm']].apply(mad).any() == 0:
    cfm_mad = df.groupby(['year-month'])[['cfm']].apply(meanad)
else:
    cfm_mad = df.groupby(['year-month'])[['cfm']].apply(mad)
cfm_mad.name = 'cfm_mad'
df = df.join(cfm_mad, on=['year-month'])

if df.groupby(['year-month'])[['curr_debt']].apply(mad).any() == 0:
    curr_debt_mad = df.groupby(['year-month'])[['curr_debt']].apply(meanad)
else:
    curr_debt_mad = df.groupby(['year-month'])[['curr_debt']].apply(mad)
curr_debt_mad.name = 'curr_debt_mad'
df = df.join(curr_debt_mad, on=['year-month'])

if df.groupby(['year-month'])[['curr_ratio']].apply(mad).any() == 0:
    curr_ratio_mad = df.groupby(['year-month'])[['curr_ratio']].apply(meanad)
else:
    curr_ratio_mad = df.groupby(['year-month'])[['curr_ratio']].apply(mad)
curr_ratio_mad.name = 'curr_ratio_mad'
df = df.join(curr_ratio_mad, on=['year-month'])

if df.groupby(['year-month'])[['de_ratio']].apply(mad).any() == 0:
    de_ratio_mad = df.groupby(['year-month'])[['de_ratio']].apply(meanad)
else:
    de_ratio_mad = df.groupby(['year-month'])[['de_ratio']].apply(mad)
de_ratio_mad.name = 'de_ratio_mad'
df = df.join(de_ratio_mad, on=['year-month'])

if df.groupby(['year-month'])[['debt_assets']].apply(mad).any() == 0:
    debt_assets_mad = df.groupby(['year-month'])[['debt_assets']].apply(meanad)
else:
    debt_assets_mad = df.groupby(['year-month'])[['debt_assets']].apply(mad)
debt_assets_mad.name = 'debt_assets_mad'
df = df.join(debt_assets_mad, on=['year-month'])

if df.groupby(['year-month'])[['debt_at']].apply(mad).any() == 0:
    debt_at_mad = df.groupby(['year-month'])[['debt_at']].apply(meanad)
else:
    debt_at_mad = df.groupby(['year-month'])[['debt_at']].apply(mad)
debt_at_mad.name = 'debt_at_mad'
df = df.join(debt_at_mad, on=['year-month'])

if df.groupby(['year-month'])[['debt_capital']].apply(mad).any() == 0:
    debt_capital_mad = df.groupby(['year-month'])[['debt_capital']].apply(meanad)
else:
    debt_capital_mad = df.groupby(['year-month'])[['debt_capital']].apply(mad)
debt_capital_mad.name = 'debt_capital_mad'
df = df.join(debt_capital_mad, on=['year-month'])

if df.groupby(['year-month'])[['debt_ebitda']].apply(mad).any() == 0:
    debt_ebitda_mad = df.groupby(['year-month'])[['debt_ebitda']].apply(meanad)
else:
    debt_ebitda_mad = df.groupby(['year-month'])[['debt_ebitda']].apply(mad)
debt_ebitda_mad.name = 'debt_ebitda_mad'
df = df.join(debt_ebitda_mad, on=['year-month'])

if df.groupby(['year-month'])[['debt_invcap']].apply(mad).any() == 0:
    debt_invcap_mad = df.groupby(['year-month'])[['debt_invcap']].apply(meanad)
else:
    debt_invcap_mad = df.groupby(['year-month'])[['debt_invcap']].apply(mad)
debt_invcap_mad.name = 'debt_invcap_mad'
df = df.join(debt_invcap_mad, on=['year-month'])

if df.groupby(['year-month'])[['DIVYIELD']].apply(mad).any() == 0:
    DIVYIELD_mad = df.groupby(['year-month'])[['DIVYIELD']].apply(meanad)
else:
    DIVYIELD_mad = df.groupby(['year-month'])[['DIVYIELD']].apply(mad)
DIVYIELD_mad.name = 'DIVYIELD_mad'
df = df.join(DIVYIELD_mad, on=['year-month'])

if df.groupby(['year-month'])[['dltt_be']].apply(mad).any() == 0:
    dltt_be_mad = df.groupby(['year-month'])[['dltt_be']].apply(meanad)
else:
    dltt_be_mad = df.groupby(['year-month'])[['dltt_be']].apply(mad)
dltt_be_mad.name = 'dltt_be_mad'
df = df.join(dltt_be_mad, on=['year-month'])

if df.groupby(['year-month'])[['dpr']].apply(mad).any() == 0:
    dpr_mad = df.groupby(['year-month'])[['dpr']].apply(meanad)
else:
    dpr_mad = df.groupby(['year-month'])[['dpr']].apply(mad)
dpr_mad.name = 'dpr_mad'
df = df.join(dpr_mad, on=['year-month'])

if df.groupby(['year-month'])[['efftax']].apply(mad).any() == 0:
    efftax_mad = df.groupby(['year-month'])[['efftax']].apply(meanad)
else:
    efftax_mad = df.groupby(['year-month'])[['efftax']].apply(mad)
efftax_mad.name = 'efftax_mad'
df = df.join(efftax_mad, on=['year-month'])

if df.groupby(['year-month'])[['equity_invcap']].apply(mad).any() == 0:
    equity_invcap_mad = df.groupby(['year-month'])[['equity_invcap']].apply(meanad)
else:
    equity_invcap_mad = df.groupby(['year-month'])[['equity_invcap']].apply(mad)
equity_invcap_mad.name = 'equity_invcap_mad'
df = df.join(equity_invcap_mad, on=['year-month'])

if df.groupby(['year-month'])[['evm']].apply(mad).any() == 0:
    evm_mad = df.groupby(['year-month'])[['evm']].apply(meanad)
else:
    evm_mad = df.groupby(['year-month'])[['evm']].apply(mad)
evm_mad.name = 'evm_mad'
df = df.join(evm_mad, on=['year-month'])

if df.groupby(['year-month'])[['fcf_ocf']].apply(mad).any() == 0:
    fcf_ocf_mad = df.groupby(['year-month'])[['fcf_ocf']].apply(meanad)
else:
    fcf_ocf_mad = df.groupby(['year-month'])[['fcf_ocf']].apply(mad)
fcf_ocf_mad.name = 'fcf_ocf_mad'
df = df.join(fcf_ocf_mad, on=['year-month'])

if df.groupby(['year-month'])[['gpm']].apply(mad).any() == 0:
    gpm_mad = df.groupby(['year-month'])[['gpm']].apply(meanad)
else:
    gpm_mad = df.groupby(['year-month'])[['gpm']].apply(mad)
gpm_mad.name = 'gpm_mad'
df = df.join(gpm_mad, on=['year-month'])

if df.groupby(['year-month'])[['GProf']].apply(mad).any() == 0:
    GProf_mad = df.groupby(['year-month'])[['GProf']].apply(meanad)
else:
    GProf_mad = df.groupby(['year-month'])[['GProf']].apply(mad)
GProf_mad.name = 'GProf_mad'
df = df.join(GProf_mad, on=['year-month'])

if df.groupby(['year-month'])[['int_debt']].apply(mad).any() == 0:
    int_debt_mad = df.groupby(['year-month'])[['int_debt']].apply(meanad)
else:
    int_debt_mad = df.groupby(['year-month'])[['int_debt']].apply(mad)
int_debt_mad.name = 'int_debt_mad'
df = df.join(int_debt_mad, on=['year-month'])

if df.groupby(['year-month'])[['int_totdebt']].apply(mad).any() == 0:
    int_totdebt_mad = df.groupby(['year-month'])[['int_totdebt']].apply(meanad)
else:
    int_totdebt_mad = df.groupby(['year-month'])[['int_totdebt']].apply(mad)
int_totdebt_mad.name = 'int_totdebt_mad'
df = df.join(int_totdebt_mad, on=['year-month'])

if df.groupby(['year-month'])[['intcov']].apply(mad).any() == 0:
    intcov_mad = df.groupby(['year-month'])[['intcov']].apply(meanad)
else:
    intcov_mad = df.groupby(['year-month'])[['intcov']].apply(mad)
intcov_mad.name = 'intcov_mad'
df = df.join(intcov_mad, on=['year-month'])

if df.groupby(['year-month'])[['intcov_ratio']].apply(mad).any() == 0:
    intcov_ratio_mad = df.groupby(['year-month'])[['intcov_ratio']].apply(meanad)
else:
    intcov_ratio_mad = df.groupby(['year-month'])[['intcov_ratio']].apply(mad)
intcov_ratio_mad.name = 'intcov_ratio_mad'
df = df.join(intcov_ratio_mad, on=['year-month'])

if df.groupby(['year-month'])[['inv_turn']].apply(mad).any() == 0:
    inv_turn_mad = df.groupby(['year-month'])[['inv_turn']].apply(meanad)
else:
    inv_turn_mad = df.groupby(['year-month'])[['inv_turn']].apply(mad)
inv_turn_mad.name = 'inv_turn_mad'
df = df.join(inv_turn_mad, on=['year-month'])

if df.groupby(['year-month'])[['invt_act']].apply(mad).any() == 0:
    invt_act_mad = df.groupby(['year-month'])[['invt_act']].apply(meanad)
else:
    invt_act_mad = df.groupby(['year-month'])[['invt_act']].apply(mad)
invt_act_mad.name = 'invt_act_mad'
df = df.join(invt_act_mad, on=['year-month'])

if df.groupby(['year-month'])[['lt_debt']].apply(mad).any() == 0:
    lt_debt_mad = df.groupby(['year-month'])[['lt_debt']].apply(meanad)
else:
    lt_debt_mad = df.groupby(['year-month'])[['lt_debt']].apply(mad)
lt_debt_mad.name = 'lt_debt_mad'
df = df.join(lt_debt_mad, on=['year-month'])

if df.groupby(['year-month'])[['lt_ppent']].apply(mad).any() == 0:
    lt_ppent_mad = df.groupby(['year-month'])[['lt_ppent']].apply(meanad)
else:
    lt_ppent_mad = df.groupby(['year-month'])[['lt_ppent']].apply(mad)
lt_ppent_mad.name = 'lt_ppent_mad'
df = df.join(lt_ppent_mad, on=['year-month'])

if df.groupby(['year-month'])[['npm']].apply(mad).any() == 0:
    npm_mad = df.groupby(['year-month'])[['npm']].apply(meanad)
else:
    npm_mad = df.groupby(['year-month'])[['npm']].apply(mad)
npm_mad.name = 'npm_mad'
df = df.join(npm_mad, on=['year-month'])

if df.groupby(['year-month'])[['ocf_lct']].apply(mad).any() == 0:
    ocf_lct_mad = df.groupby(['year-month'])[['ocf_lct']].apply(meanad)
else:
    ocf_lct_mad = df.groupby(['year-month'])[['ocf_lct']].apply(mad)
ocf_lct_mad.name = 'ocf_lct_mad'
df = df.join(ocf_lct_mad, on=['year-month'])

if df.groupby(['year-month'])[['opmad']].apply(mad).any() == 0:
    opmad_mad = df.groupby(['year-month'])[['opmad']].apply(meanad)
else:
    opmad_mad = df.groupby(['year-month'])[['opmad']].apply(mad)
opmad_mad.name = 'opmad_mad'
df = df.join(opmad_mad, on=['year-month'])

if df.groupby(['year-month'])[['opmbd']].apply(mad).any() == 0:
    opmbd_mad = df.groupby(['year-month'])[['opmbd']].apply(meanad)
else:
    opmbd_mad = df.groupby(['year-month'])[['opmbd']].apply(mad)
opmbd_mad.name = 'opmbd_mad'
df = df.join(opmbd_mad, on=['year-month'])

if df.groupby(['year-month'])[['pay_turn']].apply(mad).any() == 0:
    pay_turn_mad = df.groupby(['year-month'])[['pay_turn']].apply(meanad)
else:
    pay_turn_mad = df.groupby(['year-month'])[['pay_turn']].apply(mad)
pay_turn_mad.name = 'pay_turn_mad'
df = df.join(pay_turn_mad, on=['year-month'])

if df.groupby(['year-month'])[['pcf']].apply(mad).any() == 0:
    pcf_mad = df.groupby(['year-month'])[['pcf']].apply(meanad)
else:
    pcf_mad = df.groupby(['year-month'])[['pcf']].apply(mad)
pcf_mad.name = 'pcf_mad'
df = df.join(pcf_mad, on=['year-month'])

if df.groupby(['year-month'])[['pe_exi']].apply(mad).any() == 0:
    pe_exi_mad = df.groupby(['year-month'])[['pe_exi']].apply(meanad)
else:
    pe_exi_mad = df.groupby(['year-month'])[['pe_exi']].apply(mad)
pe_exi_mad.name = 'pe_exi_mad'
df = df.join(pe_exi_mad, on=['year-month'])

if df.groupby(['year-month'])[['pe_inc']].apply(mad).any() == 0:
    pe_inc_mad = df.groupby(['year-month'])[['pe_inc']].apply(meanad)
else:
    pe_inc_mad = df.groupby(['year-month'])[['pe_inc']].apply(mad)
pe_inc_mad.name = 'pe_inc_mad'
df = df.join(pe_inc_mad, on=['year-month'])

if df.groupby(['year-month'])[['pe_op_basic']].apply(mad).any() == 0:
    pe_op_basic_mad = df.groupby(['year-month'])[['pe_op_basic']].apply(meanad)
else:
    pe_op_basic_mad = df.groupby(['year-month'])[['pe_op_basic']].apply(mad)
pe_op_basic_mad.name = 'pe_op_basic_mad'
df = df.join(pe_op_basic_mad, on=['year-month'])

if df.groupby(['year-month'])[['pe_op_dil']].apply(mad).any() == 0:
    pe_op_dil_mad = df.groupby(['year-month'])[['pe_op_dil']].apply(meanad)
else:
    pe_op_dil_mad = df.groupby(['year-month'])[['pe_op_dil']].apply(mad)
pe_op_dil_mad.name = 'pe_op_dil_mad'
df = df.join(pe_op_dil_mad, on=['year-month'])

if df.groupby(['year-month'])[['PEG_1yrforward']].apply(mad).any() == 0:
    PEG_1yrforward_mad = df.groupby(['year-month'])[['PEG_1yrforward']].apply(meanad)
else:
    PEG_1yrforward_mad = df.groupby(['year-month'])[['PEG_1yrforward']].apply(mad)
PEG_1yrforward_mad.name = 'PEG_1yrforward_mad'
df = df.join(PEG_1yrforward_mad, on=['year-month'])

if df.groupby(['year-month'])[['PEG_ltgforward']].apply(mad).any() == 0:
    PEG_ltgforward_mad = df.groupby(['year-month'])[['PEG_ltgforward']].apply(meanad)
else:
    PEG_ltgforward_mad = df.groupby(['year-month'])[['PEG_ltgforward']].apply(mad)
PEG_ltgforward_mad.name = 'PEG_ltgforward_mad'
df = df.join(PEG_ltgforward_mad, on=['year-month'])

if df.groupby(['year-month'])[['PEG_trailing']].apply(mad).any() == 0:
    PEG_trailing_mad = df.groupby(['year-month'])[['PEG_trailing']].apply(meanad)
else:
    PEG_trailing_mad = df.groupby(['year-month'])[['PEG_trailing']].apply(mad)
PEG_trailing_mad.name = 'PEG_trailing_mad'
df = df.join(PEG_trailing_mad, on=['year-month'])

if df.groupby(['year-month'])[['pretret_earnat']].apply(mad).any() == 0:
    pretret_earnat_mad = df.groupby(['year-month'])[['pretret_earnat']].apply(meanad)
else:
    pretret_earnat_mad = df.groupby(['year-month'])[['pretret_earnat']].apply(mad)
pretret_earnat_mad.name = 'pretret_earnat_mad'
df = df.join(pretret_earnat_mad, on=['year-month'])

if df.groupby(['year-month'])[['pretret_noa']].apply(mad).any() == 0:
    pretret_noa_mad = df.groupby(['year-month'])[['pretret_noa']].apply(meanad)
else:
    pretret_noa_mad = df.groupby(['year-month'])[['pretret_noa']].apply(mad)
pretret_noa_mad.name = 'pretret_noa_mad'
df = df.join(pretret_noa_mad, on=['year-month'])

if df.groupby(['year-month'])[['profit_lct']].apply(mad).any() == 0:
    profit_lct_mad = df.groupby(['year-month'])[['profit_lct']].apply(meanad)
else:
    profit_lct_mad = df.groupby(['year-month'])[['profit_lct']].apply(mad)
profit_lct_mad.name = 'profit_lct_mad'
df = df.join(profit_lct_mad, on=['year-month'])

if df.groupby(['year-month'])[['ps']].apply(mad).any() == 0:
    ps_mad = df.groupby(['year-month'])[['ps']].apply(meanad)
else:
    ps_mad = df.groupby(['year-month'])[['ps']].apply(mad)
ps_mad.name = 'ps_mad'
df = df.join(ps_mad, on=['year-month'])

if df.groupby(['year-month'])[['ptb']].apply(mad).any() == 0:
    ptb_mad = df.groupby(['year-month'])[['ptb']].apply(meanad)
else:
    ptb_mad = df.groupby(['year-month'])[['ptb']].apply(mad)
ptb_mad.name = 'ptb_mad'
df = df.join(ptb_mad, on=['year-month'])

if df.groupby(['year-month'])[['ptpm']].apply(mad).any() == 0:
    ptpm_mad = df.groupby(['year-month'])[['ptpm']].apply(meanad)
else:
    ptpm_mad = df.groupby(['year-month'])[['ptpm']].apply(mad)
ptpm_mad.name = 'ptpm_mad'
df = df.join(ptpm_mad, on=['year-month'])

if df.groupby(['year-month'])[['quick_ratio']].apply(mad).any() == 0:
    quick_ratio_mad = df.groupby(['year-month'])[['quick_ratio']].apply(meanad)
else:
    quick_ratio_mad = df.groupby(['year-month'])[['quick_ratio']].apply(mad)
quick_ratio_mad.name = 'quick_ratio_mad'
df = df.join(quick_ratio_mad, on=['year-month'])

if df.groupby(['year-month'])[['rd_sale']].apply(mad).any() == 0:
    rd_sale_mad = df.groupby(['year-month'])[['rd_sale']].apply(meanad)
else:
    rd_sale_mad = df.groupby(['year-month'])[['rd_sale']].apply(mad)
rd_sale_mad.name = 'rd_sale_mad'
df = df.join(rd_sale_mad, on=['year-month'])

if df.groupby(['year-month'])[['rect_act']].apply(mad).any() == 0:
    rect_act_mad = df.groupby(['year-month'])[['rect_act']].apply(meanad)
else:
    rect_act_mad = df.groupby(['year-month'])[['rect_act']].apply(mad)
rect_act_mad.name = 'rect_act_mad'
df = df.join(rect_act_mad, on=['year-month'])

if df.groupby(['year-month'])[['rect_turn']].apply(mad).any() == 0:
    rect_turn_mad = df.groupby(['year-month'])[['rect_turn']].apply(meanad)
else:
    rect_turn_mad = df.groupby(['year-month'])[['rect_turn']].apply(mad)
rect_turn_mad.name = 'rect_turn_mad'
df = df.join(rect_turn_mad, on=['year-month'])

if df.groupby(['year-month'])[['roa']].apply(mad).any() == 0:
    roa_mad = df.groupby(['year-month'])[['roa']].apply(meanad)
else:
    roa_mad = df.groupby(['year-month'])[['roa']].apply(mad)
roa_mad.name = 'roa_mad'
df = df.join(roa_mad, on=['year-month'])

if df.groupby(['year-month'])[['roce']].apply(mad).any() == 0:
    roce_mad = df.groupby(['year-month'])[['roce']].apply(meanad)
else:
    roce_mad = df.groupby(['year-month'])[['roce']].apply(mad)
roce_mad.name = 'roce_mad'
df = df.join(roce_mad, on=['year-month'])

if df.groupby(['year-month'])[['roe']].apply(mad).any() == 0:
    roe_mad = df.groupby(['year-month'])[['roe']].apply(meanad)
else:
    roe_mad = df.groupby(['year-month'])[['roe']].apply(mad)
roe_mad.name = 'roe_mad'
df = df.join(roe_mad, on=['year-month'])

if df.groupby(['year-month'])[['sale_equity']].apply(mad).any() == 0:
    sale_equity_mad = df.groupby(['year-month'])[['sale_equity']].apply(meanad)
else:
    sale_equity_mad = df.groupby(['year-month'])[['sale_equity']].apply(mad)
sale_equity_mad.name = 'sale_equity_mad'
df = df.join(sale_equity_mad, on=['year-month'])

if df.groupby(['year-month'])[['sale_invcap']].apply(mad).any() == 0:
    sale_invcap_mad = df.groupby(['year-month'])[['sale_invcap']].apply(meanad)
else:
    sale_invcap_mad = df.groupby(['year-month'])[['sale_invcap']].apply(mad)
sale_invcap_mad.name = 'sale_invcap_mad'
df = df.join(sale_invcap_mad, on=['year-month'])

if df.groupby(['year-month'])[['sale_nwc']].apply(mad).any() == 0:
    sale_nwc_mad = df.groupby(['year-month'])[['sale_nwc']].apply(meanad)
else:
    sale_nwc_mad = df.groupby(['year-month'])[['sale_nwc']].apply(mad)
sale_nwc_mad.name = 'sale_nwc_mad'
df = df.join(sale_nwc_mad, on=['year-month'])

if df.groupby(['year-month'])[['short_debt']].apply(mad).any() == 0:
    short_debt_mad = df.groupby(['year-month'])[['short_debt']].apply(meanad)
else:
    short_debt_mad = df.groupby(['year-month'])[['short_debt']].apply(mad)
short_debt_mad.name = 'short_debt_mad'
df = df.join(short_debt_mad, on=['year-month'])

if df.groupby(['year-month'])[['staff_sale']].apply(mad).any() == 0:
    staff_sale_mad = df.groupby(['year-month'])[['staff_sale']].apply(meanad)
else:
    staff_sale_mad = df.groupby(['year-month'])[['staff_sale']].apply(mad)
staff_sale_mad.name = 'staff_sale_mad'
df = df.join(staff_sale_mad, on=['year-month'])

if df.groupby(['year-month'])[['totdebt_invcap']].apply(mad).any() == 0:
    totdebt_invcap_mad = df.groupby(['year-month'])[['totdebt_invcap']].apply(meanad)
else:
    totdebt_invcap_mad = df.groupby(['year-month'])[['totdebt_invcap']].apply(mad)
totdebt_invcap_mad.name = 'totdebt_invcap_mad'
df = df.join(totdebt_invcap_mad, on=['year-month'])

if df.groupby(['year-month'])[['dvpspm']].apply(mad).any() == 0:
    dvpspm_mad = df.groupby(['year-month'])[['dvpspm']].apply(meanad)
else:
    dvpspm_mad = df.groupby(['year-month'])[['dvpspm']].apply(mad)
dvpspm_mad.name = 'dvpspm_mad'
df = df.join(dvpspm_mad, on=['year-month'])

if df.groupby(['year-month'])[['dvpsxm']].apply(mad).any() == 0:
    dvpsxm_mad = df.groupby(['year-month'])[['dvpsxm']].apply(meanad)
else:
    dvpsxm_mad = df.groupby(['year-month'])[['dvpsxm']].apply(mad)
dvpsxm_mad.name = 'dvpsxm_mad'
df = df.join(dvpsxm_mad, on=['year-month'])

if df.groupby(['year-month'])[['dvrate']].apply(mad).any() == 0:
    dvrate_mad = df.groupby(['year-month'])[['dvrate']].apply(meanad)
else:
    dvrate_mad = df.groupby(['year-month'])[['dvrate']].apply(mad)
dvrate_mad.name = 'dvrate_mad'
df = df.join(dvrate_mad, on=['year-month'])

if df.groupby(['year-month'])[['spcsrc']].apply(mad).any() == 0:
    spcsrc_mad = df.groupby(['year-month'])[['spcsrc']].apply(meanad)
else:
    spcsrc_mad = df.groupby(['year-month'])[['spcsrc']].apply(mad)
spcsrc_mad.name = 'spcsrc_mad'
df = df.join(spcsrc_mad, on=['year-month'])

if df.groupby(['year-month'])[['alpha']].apply(mad).any() == 0:
    alpha_mad = df.groupby(['year-month'])[['alpha']].apply(meanad)
else:
    alpha_mad = df.groupby(['year-month'])[['alpha']].apply(mad)
alpha_mad.name = 'alpha_mad'
df = df.join(alpha_mad, on=['year-month'])

if df.groupby(['year-month'])[['b_hml']].apply(mad).any() == 0:
    b_hml_mad = df.groupby(['year-month'])[['b_hml']].apply(meanad)
else:
    b_hml_mad = df.groupby(['year-month'])[['b_hml']].apply(mad)
b_hml_mad.name = 'b_hml_mad'
df = df.join(b_hml_mad, on=['year-month'])

if df.groupby(['year-month'])[['b_mkt']].apply(mad).any() == 0:
    b_mkt_mad = df.groupby(['year-month'])[['b_mkt']].apply(meanad)
else:
    b_mkt_mad = df.groupby(['year-month'])[['b_mkt']].apply(mad)
b_mkt_mad.name = 'b_mkt_mad'
df = df.join(b_mkt_mad, on=['year-month'])

if df.groupby(['year-month'])[['b_smb']].apply(mad).any() == 0:
    b_smb_mad = df.groupby(['year-month'])[['b_smb']].apply(meanad)
else:
    b_smb_mad = df.groupby(['year-month'])[['b_smb']].apply(mad)
b_smb_mad.name = 'b_smb_mad'
df = df.join(b_smb_mad, on=['year-month'])

if df.groupby(['year-month'])[['b_umd']].apply(mad).any() == 0:
    b_umd_mad = df.groupby(['year-month'])[['b_umd']].apply(meanad)
else:
    b_umd_mad = df.groupby(['year-month'])[['b_umd']].apply(mad)
b_umd_mad.name = 'b_umd_mad'
df = df.join(b_umd_mad, on=['year-month'])

if df.groupby(['year-month'])[['exret']].apply(mad).any() == 0:
    exret_mad = df.groupby(['year-month'])[['exret']].apply(meanad)
else:
    exret_mad = df.groupby(['year-month'])[['exret']].apply(mad)
exret_mad.name = 'exret_mad'
df = df.join(exret_mad, on=['year-month'])

if df.groupby(['year-month'])[['ivol']].apply(mad).any() == 0:
    ivol_mad = df.groupby(['year-month'])[['ivol']].apply(meanad)
else:
    ivol_mad = df.groupby(['year-month'])[['ivol']].apply(mad)
ivol_mad.name = 'ivol_mad'
df = df.join(ivol_mad, on=['year-month'])

if df.groupby(['year-month'])[['n']].apply(mad).any() == 0:
    n_mad = df.groupby(['year-month'])[['n']].apply(meanad)
else:
    n_mad = df.groupby(['year-month'])[['n']].apply(mad)
n_mad.name = 'n_mad'
df = df.join(n_mad, on=['year-month'])

if df.groupby(['year-month'])[['R2']].apply(mad).any() == 0:
    R2_mad = df.groupby(['year-month'])[['R2']].apply(meanad)
else:
    R2_mad = df.groupby(['year-month'])[['R2']].apply(mad)
R2_mad.name = 'R2_mad'
df = df.join(R2_mad, on=['year-month'])

if df.groupby(['year-month'])[['tvol']].apply(mad).any() == 0:
    tvol_mad = df.groupby(['year-month'])[['tvol']].apply(meanad)
else:
    tvol_mad = df.groupby(['year-month'])[['tvol']].apply(mad)
tvol_mad.name = 'tvol_mad'
df = df.join(tvol_mad, on=['year-month'])

if df.groupby(['year-month'])[['BUYPCT']].apply(mad).any() == 0:
    BUYPCT_mad = df.groupby(['year-month'])[['BUYPCT']].apply(meanad)
else:
    BUYPCT_mad = df.groupby(['year-month'])[['BUYPCT']].apply(mad)
BUYPCT_mad.name = 'BUYPCT_mad'
df = df.join(BUYPCT_mad, on=['year-month'])

if df.groupby(['year-month'])[['HOLDPCT']].apply(mad).any() == 0:
    HOLDPCT_mad = df.groupby(['year-month'])[['HOLDPCT']].apply(meanad)
else:
    HOLDPCT_mad = df.groupby(['year-month'])[['HOLDPCT']].apply(mad)
HOLDPCT_mad.name = 'HOLDPCT_mad'
df = df.join(HOLDPCT_mad, on=['year-month'])

if df.groupby(['year-month'])[['MEANREC']].apply(mad).any() == 0:
    MEANREC_mad = df.groupby(['year-month'])[['MEANREC']].apply(meanad)
else:
    MEANREC_mad = df.groupby(['year-month'])[['MEANREC']].apply(mad)
MEANREC_mad.name = 'MEANREC_mad'
df = df.join(MEANREC_mad, on=['year-month'])

if df.groupby(['year-month'])[['MEDREC']].apply(mad).any() == 0:
    MEDREC_mad = df.groupby(['year-month'])[['MEDREC']].apply(meanad)
else:
    MEDREC_mad = df.groupby(['year-month'])[['MEDREC']].apply(mad)
MEDREC_mad.name = 'MEDREC_mad'
df = df.join(MEDREC_mad, on=['year-month'])

if df.groupby(['year-month'])[['NUMDOWN']].apply(mad).any() == 0:
    NUMDOWN_mad = df.groupby(['year-month'])[['NUMDOWN']].apply(meanad)
else:
    NUMDOWN_mad = df.groupby(['year-month'])[['NUMDOWN']].apply(mad)
NUMDOWN_mad.name = 'NUMDOWN_mad'
df = df.join(NUMDOWN_mad, on=['year-month'])

if df.groupby(['year-month'])[['NUMREC']].apply(mad).any() == 0:
    NUMREC_mad = df.groupby(['year-month'])[['NUMREC']].apply(meanad)
else:
    NUMREC_mad = df.groupby(['year-month'])[['NUMREC']].apply(mad)
NUMREC_mad.name = 'NUMREC_mad'
df = df.join(NUMREC_mad, on=['year-month'])

if df.groupby(['year-month'])[['NUMUP']].apply(mad).any() == 0:
    NUMUP_mad = df.groupby(['year-month'])[['NUMUP']].apply(meanad)
else:
    NUMUP_mad = df.groupby(['year-month'])[['NUMUP']].apply(mad)
NUMUP_mad.name = 'NUMUP_mad'
df = df.join(NUMUP_mad, on=['year-month'])

if df.groupby(['year-month'])[['SELLPCT']].apply(mad).any() == 0:
    SELLPCT_mad = df.groupby(['year-month'])[['SELLPCT']].apply(meanad)
else:
    SELLPCT_mad = df.groupby(['year-month'])[['SELLPCT']].apply(mad)
SELLPCT_mad.name = 'SELLPCT_mad'
df = df.join(SELLPCT_mad, on=['year-month'])

if df.groupby(['year-month'])[['STDEV']].apply(mad).any() == 0:
    STDEV_mad = df.groupby(['year-month'])[['STDEV']].apply(meanad)
else:
    STDEV_mad = df.groupby(['year-month'])[['STDEV']].apply(mad)
STDEV_mad.name = 'STDEV_mad'
df = df.join(STDEV_mad, on=['year-month'])

if df.groupby(['year-month'])[['ACTUAL_EPS']].apply(mad).any() == 0:
    ACTUAL_EPS_mad = df.groupby(['year-month'])[['ACTUAL_EPS']].apply(meanad)
else:
    ACTUAL_EPS_mad = df.groupby(['year-month'])[['ACTUAL_EPS']].apply(mad)
ACTUAL_EPS_mad.name = 'ACTUAL_EPS_mad'
df = df.join(ACTUAL_EPS_mad, on=['year-month'])

if df.groupby(['year-month'])[['CONSENSUS_EPS']].apply(mad).any() == 0:
    CONSENSUS_EPS_mad = df.groupby(['year-month'])[['CONSENSUS_EPS']].apply(meanad)
else:
    CONSENSUS_EPS_mad = df.groupby(['year-month'])[['CONSENSUS_EPS']].apply(mad)
CONSENSUS_EPS_mad.name = 'CONSENSUS_EPS_mad'
df = df.join(CONSENSUS_EPS_mad, on=['year-month'])

if df.groupby(['year-month'])[['CONSENSUS_STD']].apply(mad).any() == 0:
    CONSENSUS_STD_mad = df.groupby(['year-month'])[['CONSENSUS_STD']].apply(meanad)
else:
    CONSENSUS_STD_mad = df.groupby(['year-month'])[['CONSENSUS_STD']].apply(mad)
CONSENSUS_STD_mad.name = 'CONSENSUS_STD_mad'
df = df.join(CONSENSUS_STD_mad, on=['year-month'])

if df.groupby(['year-month'])[['NUMBER_OF_EST']].apply(mad).any() == 0:
    NUMBER_OF_EST_mad = df.groupby(['year-month'])[['NUMBER_OF_EST']].apply(meanad)
else:
    NUMBER_OF_EST_mad = df.groupby(['year-month'])[['NUMBER_OF_EST']].apply(mad)
NUMBER_OF_EST_mad.name = 'NUMBER_OF_EST_mad'
df = df.join(NUMBER_OF_EST_mad, on=['year-month'])

if df.groupby(['year-month'])[['SURPRISE_PCT']].apply(mad).any() == 0:
    SURPRISE_PCT_mad = df.groupby(['year-month'])[['SURPRISE_PCT']].apply(meanad)
else:
    SURPRISE_PCT_mad = df.groupby(['year-month'])[['SURPRISE_PCT']].apply(mad)
SURPRISE_PCT_mad.name = 'SURPRISE_PCT_mad'
df = df.join(SURPRISE_PCT_mad, on=['year-month'])

C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:717: RuntimeWarning: All-NaN slice encountered
  warnings.warn("All-NaN slice encountered", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:717: RuntimeWarning: All-NaN slice encountered
  warnings.warn("All-NaN slice encountered", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:717: RuntimeWarning: All-NaN slice encountered
  warnings.warn("All-NaN slice encountered", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empt

In [66]:
# Z-score denominator for securities by month and industry, use mean absolute deviation in place of median absolute deviation is MAD = 0
if df.groupby(['year-month', 'industry'])[['forward_one_month_return']].apply(mad).any() == 0:
    forward_one_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_one_month_return']].apply(meanad)
else:
    forward_one_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_one_month_return']].apply(mad)
forward_one_month_return_sector_mad.name = 'forward_one_month_return_sector_mad'
df = df.join(forward_one_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_two_month_return']].apply(mad).any() == 0:
    forward_two_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_two_month_return']].apply(meanad)
else:
    forward_two_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_two_month_return']].apply(mad)
forward_two_month_return_sector_mad.name = 'forward_two_month_return_sector_mad'
df = df.join(forward_two_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_three_month_return']].apply(mad).any() == 0:
    forward_three_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_three_month_return']].apply(meanad)
else:
    forward_three_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_three_month_return']].apply(mad)
forward_three_month_return_sector_mad.name = 'forward_three_month_return_sector_mad'
df = df.join(forward_three_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_four_month_return']].apply(mad).any() == 0:
    forward_four_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_four_month_return']].apply(meanad)
else:
    forward_four_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_four_month_return']].apply(mad)
forward_four_month_return_sector_mad.name = 'forward_four_month_return_sector_mad'
df = df.join(forward_four_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_five_month_return']].apply(mad).any() == 0:
    forward_five_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_five_month_return']].apply(meanad)
else:
    forward_five_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_five_month_return']].apply(mad)
forward_five_month_return_sector_mad.name = 'forward_five_month_return_sector_mad'
df = df.join(forward_five_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_six_month_return']].apply(mad).any() == 0:
    forward_six_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_six_month_return']].apply(meanad)
else:
    forward_six_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_six_month_return']].apply(mad)
forward_six_month_return_sector_mad.name = 'forward_six_month_return_sector_mad'
df = df.join(forward_six_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_seven_month_return']].apply(mad).any() == 0:
    forward_seven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_seven_month_return']].apply(meanad)
else:
    forward_seven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_seven_month_return']].apply(mad)
forward_seven_month_return_sector_mad.name = 'forward_seven_month_return_sector_mad'
df = df.join(forward_seven_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_eight_month_return']].apply(mad).any() == 0:
    forward_eight_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_eight_month_return']].apply(meanad)
else:
    forward_eight_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_eight_month_return']].apply(mad)
forward_eight_month_return_sector_mad.name = 'forward_eight_month_return_sector_mad'
df = df.join(forward_eight_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_nine_month_return']].apply(mad).any() == 0:
    forward_nine_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_nine_month_return']].apply(meanad)
else:
    forward_nine_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_nine_month_return']].apply(mad)
forward_nine_month_return_sector_mad.name = 'forward_nine_month_return_sector_mad'
df = df.join(forward_nine_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_ten_month_return']].apply(mad).any() == 0:
    forward_ten_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_ten_month_return']].apply(meanad)
else:
    forward_ten_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_ten_month_return']].apply(mad)
forward_ten_month_return_sector_mad.name = 'forward_ten_month_return_sector_mad'
df = df.join(forward_ten_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_eleven_month_return']].apply(mad).any() == 0:
    forward_eleven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_eleven_month_return']].apply(meanad)
else:
    forward_eleven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_eleven_month_return']].apply(mad)
forward_eleven_month_return_sector_mad.name = 'forward_eleven_month_return_sector_mad'
df = df.join(forward_eleven_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twelve_month_return']].apply(mad).any() == 0:
    forward_twelve_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twelve_month_return']].apply(meanad)
else:
    forward_twelve_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twelve_month_return']].apply(mad)
forward_twelve_month_return_sector_mad.name = 'forward_twelve_month_return_sector_mad'
df = df.join(forward_twelve_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_thirteen_month_return']].apply(mad).any() == 0:
    forward_thirteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirteen_month_return']].apply(meanad)
else:
    forward_thirteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirteen_month_return']].apply(mad)
forward_thirteen_month_return_sector_mad.name = 'forward_thirteen_month_return_sector_mad'
df = df.join(forward_thirteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_fourteen_month_return']].apply(mad).any() == 0:
    forward_fourteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_fourteen_month_return']].apply(meanad)
else:
    forward_fourteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_fourteen_month_return']].apply(mad)
forward_fourteen_month_return_sector_mad.name = 'forward_fourteen_month_return_sector_mad'
df = df.join(forward_fourteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_fifteen_month_return']].apply(mad).any() == 0:
    forward_fifteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_fifteen_month_return']].apply(meanad)
else:
    forward_fifteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_fifteen_month_return']].apply(mad)
forward_fifteen_month_return_sector_mad.name = 'forward_fifteen_month_return_sector_mad'
df = df.join(forward_fifteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_sixteen_month_return']].apply(mad).any() == 0:
    forward_sixteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_sixteen_month_return']].apply(meanad)
else:
    forward_sixteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_sixteen_month_return']].apply(mad)
forward_sixteen_month_return_sector_mad.name = 'forward_sixteen_month_return_sector_mad'
df = df.join(forward_sixteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_seventeen_month_return']].apply(mad).any() == 0:
    forward_seventeen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_seventeen_month_return']].apply(meanad)
else:
    forward_seventeen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_seventeen_month_return']].apply(mad)
forward_seventeen_month_return_sector_mad.name = 'forward_seventeen_month_return_sector_mad'
df = df.join(forward_seventeen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_eighteen_month_return']].apply(mad).any() == 0:
    forward_eighteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_eighteen_month_return']].apply(meanad)
else:
    forward_eighteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_eighteen_month_return']].apply(mad)
forward_eighteen_month_return_sector_mad.name = 'forward_eighteen_month_return_sector_mad'
df = df.join(forward_eighteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_nineteen_month_return']].apply(mad).any() == 0:
    forward_nineteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_nineteen_month_return']].apply(meanad)
else:
    forward_nineteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_nineteen_month_return']].apply(mad)
forward_nineteen_month_return_sector_mad.name = 'forward_nineteen_month_return_sector_mad'
df = df.join(forward_nineteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twenty_month_return']].apply(mad).any() == 0:
    forward_twenty_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twenty_month_return']].apply(meanad)
else:
    forward_twenty_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twenty_month_return']].apply(mad)
forward_twenty_month_return_sector_mad.name = 'forward_twenty_month_return_sector_mad'
df = df.join(forward_twenty_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twentyone_month_return']].apply(mad).any() == 0:
    forward_twentyone_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyone_month_return']].apply(meanad)
else:
    forward_twentyone_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyone_month_return']].apply(mad)
forward_twentyone_month_return_sector_mad.name = 'forward_twentyone_month_return_sector_mad'
df = df.join(forward_twentyone_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twentytwo_month_return']].apply(mad).any() == 0:
    forward_twentytwo_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentytwo_month_return']].apply(meanad)
else:
    forward_twentytwo_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentytwo_month_return']].apply(mad)
forward_twentytwo_month_return_sector_mad.name = 'forward_twentytwo_month_return_sector_mad'
df = df.join(forward_twentytwo_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twentythree_month_return']].apply(mad).any() == 0:
    forward_twentythree_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentythree_month_return']].apply(meanad)
else:
    forward_twentythree_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentythree_month_return']].apply(mad)
forward_twentythree_month_return_sector_mad.name = 'forward_twentythree_month_return_sector_mad'
df = df.join(forward_twentythree_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twentyfour_month_return']].apply(mad).any() == 0:
    forward_twentyfour_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyfour_month_return']].apply(meanad)
else:
    forward_twentyfour_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyfour_month_return']].apply(mad)
forward_twentyfour_month_return_sector_mad.name = 'forward_twentyfour_month_return_sector_mad'
df = df.join(forward_twentyfour_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twentyfive_month_return']].apply(mad).any() == 0:
    forward_twentyfive_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyfive_month_return']].apply(meanad)
else:
    forward_twentyfive_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyfive_month_return']].apply(mad)
forward_twentyfive_month_return_sector_mad.name = 'forward_twentyfive_month_return_sector_mad'
df = df.join(forward_twentyfive_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twentysix_month_return']].apply(mad).any() == 0:
    forward_twentysix_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentysix_month_return']].apply(meanad)
else:
    forward_twentysix_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentysix_month_return']].apply(mad)
forward_twentysix_month_return_sector_mad.name = 'forward_twentysix_month_return_sector_mad'
df = df.join(forward_twentysix_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twentyseven_month_return']].apply(mad).any() == 0:
    forward_twentyseven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyseven_month_return']].apply(meanad)
else:
    forward_twentyseven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyseven_month_return']].apply(mad)
forward_twentyseven_month_return_sector_mad.name = 'forward_twentyseven_month_return_sector_mad'
df = df.join(forward_twentyseven_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twentyeight_month_return']].apply(mad).any() == 0:
    forward_twentyeight_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyeight_month_return']].apply(meanad)
else:
    forward_twentyeight_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentyeight_month_return']].apply(mad)
forward_twentyeight_month_return_sector_mad.name = 'forward_twentyeight_month_return_sector_mad'
df = df.join(forward_twentyeight_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_twentynine_month_return']].apply(mad).any() == 0:
    forward_twentynine_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentynine_month_return']].apply(meanad)
else:
    forward_twentynine_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_twentynine_month_return']].apply(mad)
forward_twentynine_month_return_sector_mad.name = 'forward_twentynine_month_return_sector_mad'
df = df.join(forward_twentynine_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_thirty_month_return']].apply(mad).any() == 0:
    forward_thirty_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirty_month_return']].apply(meanad)
else:
    forward_thirty_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirty_month_return']].apply(mad)
forward_thirty_month_return_sector_mad.name = 'forward_thirty_month_return_sector_mad'
df = df.join(forward_thirty_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_thirtyone_month_return']].apply(mad).any() == 0:
    forward_thirtyone_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtyone_month_return']].apply(meanad)
else:
    forward_thirtyone_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtyone_month_return']].apply(mad)
forward_thirtyone_month_return_sector_mad.name = 'forward_thirtyone_month_return_sector_mad'
df = df.join(forward_thirtyone_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_thirtytwo_month_return']].apply(mad).any() == 0:
    forward_thirtytwo_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtytwo_month_return']].apply(meanad)
else:
    forward_thirtytwo_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtytwo_month_return']].apply(mad)
forward_thirtytwo_month_return_sector_mad.name = 'forward_thirtytwo_month_return_sector_mad'
df = df.join(forward_thirtytwo_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_thirtythree_month_return']].apply(mad).any() == 0:
    forward_thirtythree_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtythree_month_return']].apply(meanad)
else:
    forward_thirtythree_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtythree_month_return']].apply(mad)
forward_thirtythree_month_return_sector_mad.name = 'forward_thirtythree_month_return_sector_mad'
df = df.join(forward_thirtythree_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_thirtyfour_month_return']].apply(mad).any() == 0:
    forward_thirtyfour_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtyfour_month_return']].apply(meanad)
else:
    forward_thirtyfour_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtyfour_month_return']].apply(mad)
forward_thirtyfour_month_return_sector_mad.name = 'forward_thirtyfour_month_return_sector_mad'
df = df.join(forward_thirtyfour_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_thirtyfive_month_return']].apply(mad).any() == 0:
    forward_thirtyfive_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtyfive_month_return']].apply(meanad)
else:
    forward_thirtyfive_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtyfive_month_return']].apply(mad)
forward_thirtyfive_month_return_sector_mad.name = 'forward_thirtyfive_month_return_sector_mad'
df = df.join(forward_thirtyfive_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['forward_thirtysix_month_return']].apply(mad).any() == 0:
    forward_thirtysix_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtysix_month_return']].apply(meanad)
else:
    forward_thirtysix_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['forward_thirtysix_month_return']].apply(mad)
forward_thirtysix_month_return_sector_mad.name = 'forward_thirtysix_month_return_sector_mad'
df = df.join(forward_thirtysix_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_one_month_return']].apply(mad).any() == 0:
    past_one_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_one_month_return']].apply(meanad)
else:
    past_one_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_one_month_return']].apply(mad)
past_one_month_return_sector_mad.name = 'past_one_month_return_sector_mad'
df = df.join(past_one_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_two_month_return']].apply(mad).any() == 0:
    past_two_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_two_month_return']].apply(meanad)
else:
    past_two_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_two_month_return']].apply(mad)
past_two_month_return_sector_mad.name = 'past_two_month_return_sector_mad'
df = df.join(past_two_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_three_month_return']].apply(mad).any() == 0:
    past_three_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_three_month_return']].apply(meanad)
else:
    past_three_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_three_month_return']].apply(mad)
past_three_month_return_sector_mad.name = 'past_three_month_return_sector_mad'
df = df.join(past_three_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_four_month_return']].apply(mad).any() == 0:
    past_four_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_four_month_return']].apply(meanad)
else:
    past_four_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_four_month_return']].apply(mad)
past_four_month_return_sector_mad.name = 'past_four_month_return_sector_mad'
df = df.join(past_four_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_five_month_return']].apply(mad).any() == 0:
    past_five_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_five_month_return']].apply(meanad)
else:
    past_five_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_five_month_return']].apply(mad)
past_five_month_return_sector_mad.name = 'past_five_month_return_sector_mad'
df = df.join(past_five_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_six_month_return']].apply(mad).any() == 0:
    past_six_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_six_month_return']].apply(meanad)
else:
    past_six_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_six_month_return']].apply(mad)
past_six_month_return_sector_mad.name = 'past_six_month_return_sector_mad'
df = df.join(past_six_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_seven_month_return']].apply(mad).any() == 0:
    past_seven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_seven_month_return']].apply(meanad)
else:
    past_seven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_seven_month_return']].apply(mad)
past_seven_month_return_sector_mad.name = 'past_seven_month_return_sector_mad'
df = df.join(past_seven_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_eight_month_return']].apply(mad).any() == 0:
    past_eight_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_eight_month_return']].apply(meanad)
else:
    past_eight_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_eight_month_return']].apply(mad)
past_eight_month_return_sector_mad.name = 'past_eight_month_return_sector_mad'
df = df.join(past_eight_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_nine_month_return']].apply(mad).any() == 0:
    past_nine_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_nine_month_return']].apply(meanad)
else:
    past_nine_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_nine_month_return']].apply(mad)
past_nine_month_return_sector_mad.name = 'past_nine_month_return_sector_mad'
df = df.join(past_nine_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_ten_month_return']].apply(mad).any() == 0:
    past_ten_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_ten_month_return']].apply(meanad)
else:
    past_ten_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_ten_month_return']].apply(mad)
past_ten_month_return_sector_mad.name = 'past_ten_month_return_sector_mad'
df = df.join(past_ten_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_eleven_month_return']].apply(mad).any() == 0:
    past_eleven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_eleven_month_return']].apply(meanad)
else:
    past_eleven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_eleven_month_return']].apply(mad)
past_eleven_month_return_sector_mad.name = 'past_eleven_month_return_sector_mad'
df = df.join(past_eleven_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twelve_month_return']].apply(mad).any() == 0:
    past_twelve_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twelve_month_return']].apply(meanad)
else:
    past_twelve_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twelve_month_return']].apply(mad)
past_twelve_month_return_sector_mad.name = 'past_twelve_month_return_sector_mad'
df = df.join(past_twelve_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_thirteen_month_return']].apply(mad).any() == 0:
    past_thirteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirteen_month_return']].apply(meanad)
else:
    past_thirteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirteen_month_return']].apply(mad)
past_thirteen_month_return_sector_mad.name = 'past_thirteen_month_return_sector_mad'
df = df.join(past_thirteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_fourteen_month_return']].apply(mad).any() == 0:
    past_fourteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_fourteen_month_return']].apply(meanad)
else:
    past_fourteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_fourteen_month_return']].apply(mad)
past_fourteen_month_return_sector_mad.name = 'past_fourteen_month_return_sector_mad'
df = df.join(past_fourteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_fifteen_month_return']].apply(mad).any() == 0:
    past_fifteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_fifteen_month_return']].apply(meanad)
else:
    past_fifteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_fifteen_month_return']].apply(mad)
past_fifteen_month_return_sector_mad.name = 'past_fifteen_month_return_sector_mad'
df = df.join(past_fifteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_sixteen_month_return']].apply(mad).any() == 0:
    past_sixteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_sixteen_month_return']].apply(meanad)
else:
    past_sixteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_sixteen_month_return']].apply(mad)
past_sixteen_month_return_sector_mad.name = 'past_sixteen_month_return_sector_mad'
df = df.join(past_sixteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_seventeen_month_return']].apply(mad).any() == 0:
    past_seventeen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_seventeen_month_return']].apply(meanad)
else:
    past_seventeen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_seventeen_month_return']].apply(mad)
past_seventeen_month_return_sector_mad.name = 'past_seventeen_month_return_sector_mad'
df = df.join(past_seventeen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_eighteen_month_return']].apply(mad).any() == 0:
    past_eighteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_eighteen_month_return']].apply(meanad)
else:
    past_eighteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_eighteen_month_return']].apply(mad)
past_eighteen_month_return_sector_mad.name = 'past_eighteen_month_return_sector_mad'
df = df.join(past_eighteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_nineteen_month_return']].apply(mad).any() == 0:
    past_nineteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_nineteen_month_return']].apply(meanad)
else:
    past_nineteen_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_nineteen_month_return']].apply(mad)
past_nineteen_month_return_sector_mad.name = 'past_nineteen_month_return_sector_mad'
df = df.join(past_nineteen_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twenty_month_return']].apply(mad).any() == 0:
    past_twenty_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twenty_month_return']].apply(meanad)
else:
    past_twenty_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twenty_month_return']].apply(mad)
past_twenty_month_return_sector_mad.name = 'past_twenty_month_return_sector_mad'
df = df.join(past_twenty_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twentyone_month_return']].apply(mad).any() == 0:
    past_twentyone_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyone_month_return']].apply(meanad)
else:
    past_twentyone_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyone_month_return']].apply(mad)
past_twentyone_month_return_sector_mad.name = 'past_twentyone_month_return_sector_mad'
df = df.join(past_twentyone_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twentytwo_month_return']].apply(mad).any() == 0:
    past_twentytwo_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentytwo_month_return']].apply(meanad)
else:
    past_twentytwo_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentytwo_month_return']].apply(mad)
past_twentytwo_month_return_sector_mad.name = 'past_twentytwo_month_return_sector_mad'
df = df.join(past_twentytwo_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twentythree_month_return']].apply(mad).any() == 0:
    past_twentythree_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentythree_month_return']].apply(meanad)
else:
    past_twentythree_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentythree_month_return']].apply(mad)
past_twentythree_month_return_sector_mad.name = 'past_twentythree_month_return_sector_mad'
df = df.join(past_twentythree_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twentyfour_month_return']].apply(mad).any() == 0:
    past_twentyfour_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyfour_month_return']].apply(meanad)
else:
    past_twentyfour_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyfour_month_return']].apply(mad)
past_twentyfour_month_return_sector_mad.name = 'past_twentyfour_month_return_sector_mad'
df = df.join(past_twentyfour_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twentyfive_month_return']].apply(mad).any() == 0:
    past_twentyfive_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyfive_month_return']].apply(meanad)
else:
    past_twentyfive_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyfive_month_return']].apply(mad)
past_twentyfive_month_return_sector_mad.name = 'past_twentyfive_month_return_sector_mad'
df = df.join(past_twentyfive_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twentysix_month_return']].apply(mad).any() == 0:
    past_twentysix_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentysix_month_return']].apply(meanad)
else:
    past_twentysix_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentysix_month_return']].apply(mad)
past_twentysix_month_return_sector_mad.name = 'past_twentysix_month_return_sector_mad'
df = df.join(past_twentysix_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twentyseven_month_return']].apply(mad).any() == 0:
    past_twentyseven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyseven_month_return']].apply(meanad)
else:
    past_twentyseven_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyseven_month_return']].apply(mad)
past_twentyseven_month_return_sector_mad.name = 'past_twentyseven_month_return_sector_mad'
df = df.join(past_twentyseven_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twentyeight_month_return']].apply(mad).any() == 0:
    past_twentyeight_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyeight_month_return']].apply(meanad)
else:
    past_twentyeight_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentyeight_month_return']].apply(mad)
past_twentyeight_month_return_sector_mad.name = 'past_twentyeight_month_return_sector_mad'
df = df.join(past_twentyeight_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_twentynine_month_return']].apply(mad).any() == 0:
    past_twentynine_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentynine_month_return']].apply(meanad)
else:
    past_twentynine_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_twentynine_month_return']].apply(mad)
past_twentynine_month_return_sector_mad.name = 'past_twentynine_month_return_sector_mad'
df = df.join(past_twentynine_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_thirty_month_return']].apply(mad).any() == 0:
    past_thirty_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirty_month_return']].apply(meanad)
else:
    past_thirty_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirty_month_return']].apply(mad)
past_thirty_month_return_sector_mad.name = 'past_thirty_month_return_sector_mad'
df = df.join(past_thirty_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_thirtyone_month_return']].apply(mad).any() == 0:
    past_thirtyone_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtyone_month_return']].apply(meanad)
else:
    past_thirtyone_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtyone_month_return']].apply(mad)
past_thirtyone_month_return_sector_mad.name = 'past_thirtyone_month_return_sector_mad'
df = df.join(past_thirtyone_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_thirtytwo_month_return']].apply(mad).any() == 0:
    past_thirtytwo_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtytwo_month_return']].apply(meanad)
else:
    past_thirtytwo_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtytwo_month_return']].apply(mad)
past_thirtytwo_month_return_sector_mad.name = 'past_thirtytwo_month_return_sector_mad'
df = df.join(past_thirtytwo_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_thirtythree_month_return']].apply(mad).any() == 0:
    past_thirtythree_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtythree_month_return']].apply(meanad)
else:
    past_thirtythree_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtythree_month_return']].apply(mad)
past_thirtythree_month_return_sector_mad.name = 'past_thirtythree_month_return_sector_mad'
df = df.join(past_thirtythree_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_thirtyfour_month_return']].apply(mad).any() == 0:
    past_thirtyfour_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtyfour_month_return']].apply(meanad)
else:
    past_thirtyfour_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtyfour_month_return']].apply(mad)
past_thirtyfour_month_return_sector_mad.name = 'past_thirtyfour_month_return_sector_mad'
df = df.join(past_thirtyfour_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_thirtyfive_month_return']].apply(mad).any() == 0:
    past_thirtyfive_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtyfive_month_return']].apply(meanad)
else:
    past_thirtyfive_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtyfive_month_return']].apply(mad)
past_thirtyfive_month_return_sector_mad.name = 'past_thirtyfive_month_return_sector_mad'
df = df.join(past_thirtyfive_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['past_thirtysix_month_return']].apply(mad).any() == 0:
    past_thirtysix_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtysix_month_return']].apply(meanad)
else:
    past_thirtysix_month_return_sector_mad = df.groupby(['year-month', 'industry'])[['past_thirtysix_month_return']].apply(mad)
past_thirtysix_month_return_sector_mad.name = 'past_thirtysix_month_return_sector_mad'
df = df.join(past_thirtysix_month_return_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['accrual']].apply(mad).any() == 0:
    accrual_sector_mad = df.groupby(['year-month', 'industry'])[['accrual']].apply(meanad)
else:
    accrual_sector_mad = df.groupby(['year-month', 'industry'])[['accrual']].apply(mad)
accrual_sector_mad.name = 'accrual_sector_mad'
df = df.join(accrual_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['adv_sale']].apply(mad).any() == 0:
    adv_sale_sector_mad = df.groupby(['year-month', 'industry'])[['adv_sale']].apply(meanad)
else:
    adv_sale_sector_mad = df.groupby(['year-month', 'industry'])[['adv_sale']].apply(mad)
adv_sale_sector_mad.name = 'adv_sale_sector_mad'
df = df.join(adv_sale_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['aftret_eq']].apply(mad).any() == 0:
    aftret_eq_sector_mad = df.groupby(['year-month', 'industry'])[['aftret_eq']].apply(meanad)
else:
    aftret_eq_sector_mad = df.groupby(['year-month', 'industry'])[['aftret_eq']].apply(mad)
aftret_eq_sector_mad.name = 'aftret_eq_sector_mad'
df = df.join(aftret_eq_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['aftret_equity']].apply(mad).any() == 0:
    aftret_equity_sector_mad = df.groupby(['year-month', 'industry'])[['aftret_equity']].apply(meanad)
else:
    aftret_equity_sector_mad = df.groupby(['year-month', 'industry'])[['aftret_equity']].apply(mad)
aftret_equity_sector_mad.name = 'aftret_equity_sector_mad'
df = df.join(aftret_equity_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['aftret_invcapx']].apply(mad).any() == 0:
    aftret_invcapx_sector_mad = df.groupby(['year-month', 'industry'])[['aftret_invcapx']].apply(meanad)
else:
    aftret_invcapx_sector_mad = df.groupby(['year-month', 'industry'])[['aftret_invcapx']].apply(mad)
aftret_invcapx_sector_mad.name = 'aftret_invcapx_sector_mad'
df = df.join(aftret_invcapx_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['at_turn']].apply(mad).any() == 0:
    at_turn_sector_mad = df.groupby(['year-month', 'industry'])[['at_turn']].apply(meanad)
else:
    at_turn_sector_mad = df.groupby(['year-month', 'industry'])[['at_turn']].apply(mad)
at_turn_sector_mad.name = 'at_turn_sector_mad'
df = df.join(at_turn_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['bm']].apply(mad).any() == 0:
    bm_sector_mad = df.groupby(['year-month', 'industry'])[['bm']].apply(meanad)
else:
    bm_sector_mad = df.groupby(['year-month', 'industry'])[['bm']].apply(mad)
bm_sector_mad.name = 'bm_sector_mad'
df = df.join(bm_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['CAPEI']].apply(mad).any() == 0:
    CAPEI_sector_mad = df.groupby(['year-month', 'industry'])[['CAPEI']].apply(meanad)
else:
    CAPEI_sector_mad = df.groupby(['year-month', 'industry'])[['CAPEI']].apply(mad)
CAPEI_sector_mad.name = 'CAPEI_sector_mad'
df = df.join(CAPEI_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['capital_ratio']].apply(mad).any() == 0:
    capital_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['capital_ratio']].apply(meanad)
else:
    capital_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['capital_ratio']].apply(mad)
capital_ratio_sector_mad.name = 'capital_ratio_sector_mad'
df = df.join(capital_ratio_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['cash_conversion']].apply(mad).any() == 0:
    cash_conversion_sector_mad = df.groupby(['year-month', 'industry'])[['cash_conversion']].apply(meanad)
else:
    cash_conversion_sector_mad = df.groupby(['year-month', 'industry'])[['cash_conversion']].apply(mad)
cash_conversion_sector_mad.name = 'cash_conversion_sector_mad'
df = df.join(cash_conversion_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['cash_debt']].apply(mad).any() == 0:
    cash_debt_sector_mad = df.groupby(['year-month', 'industry'])[['cash_debt']].apply(meanad)
else:
    cash_debt_sector_mad = df.groupby(['year-month', 'industry'])[['cash_debt']].apply(mad)
cash_debt_sector_mad.name = 'cash_debt_sector_mad'
df = df.join(cash_debt_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['cash_lt']].apply(mad).any() == 0:
    cash_lt_sector_mad = df.groupby(['year-month', 'industry'])[['cash_lt']].apply(meanad)
else:
    cash_lt_sector_mad = df.groupby(['year-month', 'industry'])[['cash_lt']].apply(mad)
cash_lt_sector_mad.name = 'cash_lt_sector_mad'
df = df.join(cash_lt_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['cash_ratio']].apply(mad).any() == 0:
    cash_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['cash_ratio']].apply(meanad)
else:
    cash_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['cash_ratio']].apply(mad)
cash_ratio_sector_mad.name = 'cash_ratio_sector_mad'
df = df.join(cash_ratio_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['cfm']].apply(mad).any() == 0:
    cfm_sector_mad = df.groupby(['year-month', 'industry'])[['cfm']].apply(meanad)
else:
    cfm_sector_mad = df.groupby(['year-month', 'industry'])[['cfm']].apply(mad)
cfm_sector_mad.name = 'cfm_sector_mad'
df = df.join(cfm_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['curr_debt']].apply(mad).any() == 0:
    curr_debt_sector_mad = df.groupby(['year-month', 'industry'])[['curr_debt']].apply(meanad)
else:
    curr_debt_sector_mad = df.groupby(['year-month', 'industry'])[['curr_debt']].apply(mad)
curr_debt_sector_mad.name = 'curr_debt_sector_mad'
df = df.join(curr_debt_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['curr_ratio']].apply(mad).any() == 0:
    curr_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['curr_ratio']].apply(meanad)
else:
    curr_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['curr_ratio']].apply(mad)
curr_ratio_sector_mad.name = 'curr_ratio_sector_mad'
df = df.join(curr_ratio_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['de_ratio']].apply(mad).any() == 0:
    de_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['de_ratio']].apply(meanad)
else:
    de_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['de_ratio']].apply(mad)
de_ratio_sector_mad.name = 'de_ratio_sector_mad'
df = df.join(de_ratio_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['debt_assets']].apply(mad).any() == 0:
    debt_assets_sector_mad = df.groupby(['year-month', 'industry'])[['debt_assets']].apply(meanad)
else:
    debt_assets_sector_mad = df.groupby(['year-month', 'industry'])[['debt_assets']].apply(mad)
debt_assets_sector_mad.name = 'debt_assets_sector_mad'
df = df.join(debt_assets_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['debt_at']].apply(mad).any() == 0:
    debt_at_sector_mad = df.groupby(['year-month', 'industry'])[['debt_at']].apply(meanad)
else:
    debt_at_sector_mad = df.groupby(['year-month', 'industry'])[['debt_at']].apply(mad)
debt_at_sector_mad.name = 'debt_at_sector_mad'
df = df.join(debt_at_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['debt_capital']].apply(mad).any() == 0:
    debt_capital_sector_mad = df.groupby(['year-month', 'industry'])[['debt_capital']].apply(meanad)
else:
    debt_capital_sector_mad = df.groupby(['year-month', 'industry'])[['debt_capital']].apply(mad)
debt_capital_sector_mad.name = 'debt_capital_sector_mad'
df = df.join(debt_capital_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['debt_ebitda']].apply(mad).any() == 0:
    debt_ebitda_sector_mad = df.groupby(['year-month', 'industry'])[['debt_ebitda']].apply(meanad)
else:
    debt_ebitda_sector_mad = df.groupby(['year-month', 'industry'])[['debt_ebitda']].apply(mad)
debt_ebitda_sector_mad.name = 'debt_ebitda_sector_mad'
df = df.join(debt_ebitda_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['debt_invcap']].apply(mad).any() == 0:
    debt_invcap_sector_mad = df.groupby(['year-month', 'industry'])[['debt_invcap']].apply(meanad)
else:
    debt_invcap_sector_mad = df.groupby(['year-month', 'industry'])[['debt_invcap']].apply(mad)
debt_invcap_sector_mad.name = 'debt_invcap_sector_mad'
df = df.join(debt_invcap_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['DIVYIELD']].apply(mad).any() == 0:
    DIVYIELD_sector_mad = df.groupby(['year-month', 'industry'])[['DIVYIELD']].apply(meanad)
else:
    DIVYIELD_sector_mad = df.groupby(['year-month', 'industry'])[['DIVYIELD']].apply(mad)
DIVYIELD_sector_mad.name = 'DIVYIELD_sector_mad'
df = df.join(DIVYIELD_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['dltt_be']].apply(mad).any() == 0:
    dltt_be_sector_mad = df.groupby(['year-month', 'industry'])[['dltt_be']].apply(meanad)
else:
    dltt_be_sector_mad = df.groupby(['year-month', 'industry'])[['dltt_be']].apply(mad)
dltt_be_sector_mad.name = 'dltt_be_sector_mad'
df = df.join(dltt_be_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['dpr']].apply(mad).any() == 0:
    dpr_sector_mad = df.groupby(['year-month', 'industry'])[['dpr']].apply(meanad)
else:
    dpr_sector_mad = df.groupby(['year-month', 'industry'])[['dpr']].apply(mad)
dpr_sector_mad.name = 'dpr_sector_mad'
df = df.join(dpr_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['efftax']].apply(mad).any() == 0:
    efftax_sector_mad = df.groupby(['year-month', 'industry'])[['efftax']].apply(meanad)
else:
    efftax_sector_mad = df.groupby(['year-month', 'industry'])[['efftax']].apply(mad)
efftax_sector_mad.name = 'efftax_sector_mad'
df = df.join(efftax_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['equity_invcap']].apply(mad).any() == 0:
    equity_invcap_sector_mad = df.groupby(['year-month', 'industry'])[['equity_invcap']].apply(meanad)
else:
    equity_invcap_sector_mad = df.groupby(['year-month', 'industry'])[['equity_invcap']].apply(mad)
equity_invcap_sector_mad.name = 'equity_invcap_sector_mad'
df = df.join(equity_invcap_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['evm']].apply(mad).any() == 0:
    evm_sector_mad = df.groupby(['year-month', 'industry'])[['evm']].apply(meanad)
else:
    evm_sector_mad = df.groupby(['year-month', 'industry'])[['evm']].apply(mad)
evm_sector_mad.name = 'evm_sector_mad'
df = df.join(evm_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['fcf_ocf']].apply(mad).any() == 0:
    fcf_ocf_sector_mad = df.groupby(['year-month', 'industry'])[['fcf_ocf']].apply(meanad)
else:
    fcf_ocf_sector_mad = df.groupby(['year-month', 'industry'])[['fcf_ocf']].apply(mad)
fcf_ocf_sector_mad.name = 'fcf_ocf_sector_mad'
df = df.join(fcf_ocf_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['gpm']].apply(mad).any() == 0:
    gpm_sector_mad = df.groupby(['year-month', 'industry'])[['gpm']].apply(meanad)
else:
    gpm_sector_mad = df.groupby(['year-month', 'industry'])[['gpm']].apply(mad)
gpm_sector_mad.name = 'gpm_sector_mad'
df = df.join(gpm_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['GProf']].apply(mad).any() == 0:
    GProf_sector_mad = df.groupby(['year-month', 'industry'])[['GProf']].apply(meanad)
else:
    GProf_sector_mad = df.groupby(['year-month', 'industry'])[['GProf']].apply(mad)
GProf_sector_mad.name = 'GProf_sector_mad'
df = df.join(GProf_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['int_debt']].apply(mad).any() == 0:
    int_debt_sector_mad = df.groupby(['year-month', 'industry'])[['int_debt']].apply(meanad)
else:
    int_debt_sector_mad = df.groupby(['year-month', 'industry'])[['int_debt']].apply(mad)
int_debt_sector_mad.name = 'int_debt_sector_mad'
df = df.join(int_debt_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['int_totdebt']].apply(mad).any() == 0:
    int_totdebt_sector_mad = df.groupby(['year-month', 'industry'])[['int_totdebt']].apply(meanad)
else:
    int_totdebt_sector_mad = df.groupby(['year-month', 'industry'])[['int_totdebt']].apply(mad)
int_totdebt_sector_mad.name = 'int_totdebt_sector_mad'
df = df.join(int_totdebt_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['intcov']].apply(mad).any() == 0:
    intcov_sector_mad = df.groupby(['year-month', 'industry'])[['intcov']].apply(meanad)
else:
    intcov_sector_mad = df.groupby(['year-month', 'industry'])[['intcov']].apply(mad)
intcov_sector_mad.name = 'intcov_sector_mad'
df = df.join(intcov_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['intcov_ratio']].apply(mad).any() == 0:
    intcov_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['intcov_ratio']].apply(meanad)
else:
    intcov_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['intcov_ratio']].apply(mad)
intcov_ratio_sector_mad.name = 'intcov_ratio_sector_mad'
df = df.join(intcov_ratio_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['inv_turn']].apply(mad).any() == 0:
    inv_turn_sector_mad = df.groupby(['year-month', 'industry'])[['inv_turn']].apply(meanad)
else:
    inv_turn_sector_mad = df.groupby(['year-month', 'industry'])[['inv_turn']].apply(mad)
inv_turn_sector_mad.name = 'inv_turn_sector_mad'
df = df.join(inv_turn_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['invt_act']].apply(mad).any() == 0:
    invt_act_sector_mad = df.groupby(['year-month', 'industry'])[['invt_act']].apply(meanad)
else:
    invt_act_sector_mad = df.groupby(['year-month', 'industry'])[['invt_act']].apply(mad)
invt_act_sector_mad.name = 'invt_act_sector_mad'
df = df.join(invt_act_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['lt_debt']].apply(mad).any() == 0:
    lt_debt_sector_mad = df.groupby(['year-month', 'industry'])[['lt_debt']].apply(meanad)
else:
    lt_debt_sector_mad = df.groupby(['year-month', 'industry'])[['lt_debt']].apply(mad)
lt_debt_sector_mad.name = 'lt_debt_sector_mad'
df = df.join(lt_debt_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['lt_ppent']].apply(mad).any() == 0:
    lt_ppent_sector_mad = df.groupby(['year-month', 'industry'])[['lt_ppent']].apply(meanad)
else:
    lt_ppent_sector_mad = df.groupby(['year-month', 'industry'])[['lt_ppent']].apply(mad)
lt_ppent_sector_mad.name = 'lt_ppent_sector_mad'
df = df.join(lt_ppent_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['npm']].apply(mad).any() == 0:
    npm_sector_mad = df.groupby(['year-month', 'industry'])[['npm']].apply(meanad)
else:
    npm_sector_mad = df.groupby(['year-month', 'industry'])[['npm']].apply(mad)
npm_sector_mad.name = 'npm_sector_mad'
df = df.join(npm_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['ocf_lct']].apply(mad).any() == 0:
    ocf_lct_sector_mad = df.groupby(['year-month', 'industry'])[['ocf_lct']].apply(meanad)
else:
    ocf_lct_sector_mad = df.groupby(['year-month', 'industry'])[['ocf_lct']].apply(mad)
ocf_lct_sector_mad.name = 'ocf_lct_sector_mad'
df = df.join(ocf_lct_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['opmad']].apply(mad).any() == 0:
    opmad_sector_mad = df.groupby(['year-month', 'industry'])[['opmad']].apply(meanad)
else:
    opmad_sector_mad = df.groupby(['year-month', 'industry'])[['opmad']].apply(mad)
opmad_sector_mad.name = 'opmad_sector_mad'
df = df.join(opmad_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['opmbd']].apply(mad).any() == 0:
    opmbd_sector_mad = df.groupby(['year-month', 'industry'])[['opmbd']].apply(meanad)
else:
    opmbd_sector_mad = df.groupby(['year-month', 'industry'])[['opmbd']].apply(mad)
opmbd_sector_mad.name = 'opmbd_sector_mad'
df = df.join(opmbd_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['pay_turn']].apply(mad).any() == 0:
    pay_turn_sector_mad = df.groupby(['year-month', 'industry'])[['pay_turn']].apply(meanad)
else:
    pay_turn_sector_mad = df.groupby(['year-month', 'industry'])[['pay_turn']].apply(mad)
pay_turn_sector_mad.name = 'pay_turn_sector_mad'
df = df.join(pay_turn_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['pcf']].apply(mad).any() == 0:
    pcf_sector_mad = df.groupby(['year-month', 'industry'])[['pcf']].apply(meanad)
else:
    pcf_sector_mad = df.groupby(['year-month', 'industry'])[['pcf']].apply(mad)
pcf_sector_mad.name = 'pcf_sector_mad'
df = df.join(pcf_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['pe_exi']].apply(mad).any() == 0:
    pe_exi_sector_mad = df.groupby(['year-month', 'industry'])[['pe_exi']].apply(meanad)
else:
    pe_exi_sector_mad = df.groupby(['year-month', 'industry'])[['pe_exi']].apply(mad)
pe_exi_sector_mad.name = 'pe_exi_sector_mad'
df = df.join(pe_exi_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['pe_inc']].apply(mad).any() == 0:
    pe_inc_sector_mad = df.groupby(['year-month', 'industry'])[['pe_inc']].apply(meanad)
else:
    pe_inc_sector_mad = df.groupby(['year-month', 'industry'])[['pe_inc']].apply(mad)
pe_inc_sector_mad.name = 'pe_inc_sector_mad'
df = df.join(pe_inc_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['pe_op_basic']].apply(mad).any() == 0:
    pe_op_basic_sector_mad = df.groupby(['year-month', 'industry'])[['pe_op_basic']].apply(meanad)
else:
    pe_op_basic_sector_mad = df.groupby(['year-month', 'industry'])[['pe_op_basic']].apply(mad)
pe_op_basic_sector_mad.name = 'pe_op_basic_sector_mad'
df = df.join(pe_op_basic_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['pe_op_dil']].apply(mad).any() == 0:
    pe_op_dil_sector_mad = df.groupby(['year-month', 'industry'])[['pe_op_dil']].apply(meanad)
else:
    pe_op_dil_sector_mad = df.groupby(['year-month', 'industry'])[['pe_op_dil']].apply(mad)
pe_op_dil_sector_mad.name = 'pe_op_dil_sector_mad'
df = df.join(pe_op_dil_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['PEG_1yrforward']].apply(mad).any() == 0:
    PEG_1yrforward_sector_mad = df.groupby(['year-month', 'industry'])[['PEG_1yrforward']].apply(meanad)
else:
    PEG_1yrforward_sector_mad = df.groupby(['year-month', 'industry'])[['PEG_1yrforward']].apply(mad)
PEG_1yrforward_sector_mad.name = 'PEG_1yrforward_sector_mad'
df = df.join(PEG_1yrforward_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['PEG_ltgforward']].apply(mad).any() == 0:
    PEG_ltgforward_sector_mad = df.groupby(['year-month', 'industry'])[['PEG_ltgforward']].apply(meanad)
else:
    PEG_ltgforward_sector_mad = df.groupby(['year-month', 'industry'])[['PEG_ltgforward']].apply(mad)
PEG_ltgforward_sector_mad.name = 'PEG_ltgforward_sector_mad'
df = df.join(PEG_ltgforward_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['PEG_trailing']].apply(mad).any() == 0:
    PEG_trailing_sector_mad = df.groupby(['year-month', 'industry'])[['PEG_trailing']].apply(meanad)
else:
    PEG_trailing_sector_mad = df.groupby(['year-month', 'industry'])[['PEG_trailing']].apply(mad)
PEG_trailing_sector_mad.name = 'PEG_trailing_sector_mad'
df = df.join(PEG_trailing_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['pretret_earnat']].apply(mad).any() == 0:
    pretret_earnat_sector_mad = df.groupby(['year-month', 'industry'])[['pretret_earnat']].apply(meanad)
else:
    pretret_earnat_sector_mad = df.groupby(['year-month', 'industry'])[['pretret_earnat']].apply(mad)
pretret_earnat_sector_mad.name = 'pretret_earnat_sector_mad'
df = df.join(pretret_earnat_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['pretret_noa']].apply(mad).any() == 0:
    pretret_noa_sector_mad = df.groupby(['year-month', 'industry'])[['pretret_noa']].apply(meanad)
else:
    pretret_noa_sector_mad = df.groupby(['year-month', 'industry'])[['pretret_noa']].apply(mad)
pretret_noa_sector_mad.name = 'pretret_noa_sector_mad'
df = df.join(pretret_noa_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['profit_lct']].apply(mad).any() == 0:
    profit_lct_sector_mad = df.groupby(['year-month', 'industry'])[['profit_lct']].apply(meanad)
else:
    profit_lct_sector_mad = df.groupby(['year-month', 'industry'])[['profit_lct']].apply(mad)
profit_lct_sector_mad.name = 'profit_lct_sector_mad'
df = df.join(profit_lct_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['ps']].apply(mad).any() == 0:
    ps_sector_mad = df.groupby(['year-month', 'industry'])[['ps']].apply(meanad)
else:
    ps_sector_mad = df.groupby(['year-month', 'industry'])[['ps']].apply(mad)
ps_sector_mad.name = 'ps_sector_mad'
df = df.join(ps_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['ptb']].apply(mad).any() == 0:
    ptb_sector_mad = df.groupby(['year-month', 'industry'])[['ptb']].apply(meanad)
else:
    ptb_sector_mad = df.groupby(['year-month', 'industry'])[['ptb']].apply(mad)
ptb_sector_mad.name = 'ptb_sector_mad'
df = df.join(ptb_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['ptpm']].apply(mad).any() == 0:
    ptpm_sector_mad = df.groupby(['year-month', 'industry'])[['ptpm']].apply(meanad)
else:
    ptpm_sector_mad = df.groupby(['year-month', 'industry'])[['ptpm']].apply(mad)
ptpm_sector_mad.name = 'ptpm_sector_mad'
df = df.join(ptpm_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['quick_ratio']].apply(mad).any() == 0:
    quick_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['quick_ratio']].apply(meanad)
else:
    quick_ratio_sector_mad = df.groupby(['year-month', 'industry'])[['quick_ratio']].apply(mad)
quick_ratio_sector_mad.name = 'quick_ratio_sector_mad'
df = df.join(quick_ratio_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['rd_sale']].apply(mad).any() == 0:
    rd_sale_sector_mad = df.groupby(['year-month', 'industry'])[['rd_sale']].apply(meanad)
else:
    rd_sale_sector_mad = df.groupby(['year-month', 'industry'])[['rd_sale']].apply(mad)
rd_sale_sector_mad.name = 'rd_sale_sector_mad'
df = df.join(rd_sale_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['rect_act']].apply(mad).any() == 0:
    rect_act_sector_mad = df.groupby(['year-month', 'industry'])[['rect_act']].apply(meanad)
else:
    rect_act_sector_mad = df.groupby(['year-month', 'industry'])[['rect_act']].apply(mad)
rect_act_sector_mad.name = 'rect_act_sector_mad'
df = df.join(rect_act_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['rect_turn']].apply(mad).any() == 0:
    rect_turn_sector_mad = df.groupby(['year-month', 'industry'])[['rect_turn']].apply(meanad)
else:
    rect_turn_sector_mad = df.groupby(['year-month', 'industry'])[['rect_turn']].apply(mad)
rect_turn_sector_mad.name = 'rect_turn_sector_mad'
df = df.join(rect_turn_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['roa']].apply(mad).any() == 0:
    roa_sector_mad = df.groupby(['year-month', 'industry'])[['roa']].apply(meanad)
else:
    roa_sector_mad = df.groupby(['year-month', 'industry'])[['roa']].apply(mad)
roa_sector_mad.name = 'roa_sector_mad'
df = df.join(roa_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['roce']].apply(mad).any() == 0:
    roce_sector_mad = df.groupby(['year-month', 'industry'])[['roce']].apply(meanad)
else:
    roce_sector_mad = df.groupby(['year-month', 'industry'])[['roce']].apply(mad)
roce_sector_mad.name = 'roce_sector_mad'
df = df.join(roce_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['roe']].apply(mad).any() == 0:
    roe_sector_mad = df.groupby(['year-month', 'industry'])[['roe']].apply(meanad)
else:
    roe_sector_mad = df.groupby(['year-month', 'industry'])[['roe']].apply(mad)
roe_sector_mad.name = 'roe_sector_mad'
df = df.join(roe_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['sale_equity']].apply(mad).any() == 0:
    sale_equity_sector_mad = df.groupby(['year-month', 'industry'])[['sale_equity']].apply(meanad)
else:
    sale_equity_sector_mad = df.groupby(['year-month', 'industry'])[['sale_equity']].apply(mad)
sale_equity_sector_mad.name = 'sale_equity_sector_mad'
df = df.join(sale_equity_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['sale_invcap']].apply(mad).any() == 0:
    sale_invcap_sector_mad = df.groupby(['year-month', 'industry'])[['sale_invcap']].apply(meanad)
else:
    sale_invcap_sector_mad = df.groupby(['year-month', 'industry'])[['sale_invcap']].apply(mad)
sale_invcap_sector_mad.name = 'sale_invcap_sector_mad'
df = df.join(sale_invcap_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['sale_nwc']].apply(mad).any() == 0:
    sale_nwc_sector_mad = df.groupby(['year-month', 'industry'])[['sale_nwc']].apply(meanad)
else:
    sale_nwc_sector_mad = df.groupby(['year-month', 'industry'])[['sale_nwc']].apply(mad)
sale_nwc_sector_mad.name = 'sale_nwc_sector_mad'
df = df.join(sale_nwc_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['short_debt']].apply(mad).any() == 0:
    short_debt_sector_mad = df.groupby(['year-month', 'industry'])[['short_debt']].apply(meanad)
else:
    short_debt_sector_mad = df.groupby(['year-month', 'industry'])[['short_debt']].apply(mad)
short_debt_sector_mad.name = 'short_debt_sector_mad'
df = df.join(short_debt_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['staff_sale']].apply(mad).any() == 0:
    staff_sale_sector_mad = df.groupby(['year-month', 'industry'])[['staff_sale']].apply(meanad)
else:
    staff_sale_sector_mad = df.groupby(['year-month', 'industry'])[['staff_sale']].apply(mad)
staff_sale_sector_mad.name = 'staff_sale_sector_mad'
df = df.join(staff_sale_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['totdebt_invcap']].apply(mad).any() == 0:
    totdebt_invcap_sector_mad = df.groupby(['year-month', 'industry'])[['totdebt_invcap']].apply(meanad)
else:
    totdebt_invcap_sector_mad = df.groupby(['year-month', 'industry'])[['totdebt_invcap']].apply(mad)
totdebt_invcap_sector_mad.name = 'totdebt_invcap_sector_mad'
df = df.join(totdebt_invcap_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['dvpspm']].apply(mad).any() == 0:
    dvpspm_sector_mad = df.groupby(['year-month', 'industry'])[['dvpspm']].apply(meanad)
else:
    dvpspm_sector_mad = df.groupby(['year-month', 'industry'])[['dvpspm']].apply(mad)
dvpspm_sector_mad.name = 'dvpspm_sector_mad'
df = df.join(dvpspm_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['dvpsxm']].apply(mad).any() == 0:
    dvpsxm_sector_mad = df.groupby(['year-month', 'industry'])[['dvpsxm']].apply(meanad)
else:
    dvpsxm_sector_mad = df.groupby(['year-month', 'industry'])[['dvpsxm']].apply(mad)
dvpsxm_sector_mad.name = 'dvpsxm_sector_mad'
df = df.join(dvpsxm_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['dvrate']].apply(mad).any() == 0:
    dvrate_sector_mad = df.groupby(['year-month', 'industry'])[['dvrate']].apply(meanad)
else:
    dvrate_sector_mad = df.groupby(['year-month', 'industry'])[['dvrate']].apply(mad)
dvrate_sector_mad.name = 'dvrate_sector_mad'
df = df.join(dvrate_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['spcsrc']].apply(mad).any() == 0:
    spcsrc_sector_mad = df.groupby(['year-month', 'industry'])[['spcsrc']].apply(meanad)
else:
    spcsrc_sector_mad = df.groupby(['year-month', 'industry'])[['spcsrc']].apply(mad)
spcsrc_sector_mad.name = 'spcsrc_sector_mad'
df = df.join(spcsrc_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['alpha']].apply(mad).any() == 0:
    alpha_sector_mad = df.groupby(['year-month', 'industry'])[['alpha']].apply(meanad)
else:
    alpha_sector_mad = df.groupby(['year-month', 'industry'])[['alpha']].apply(mad)
alpha_sector_mad.name = 'alpha_sector_mad'
df = df.join(alpha_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['b_hml']].apply(mad).any() == 0:
    b_hml_sector_mad = df.groupby(['year-month', 'industry'])[['b_hml']].apply(meanad)
else:
    b_hml_sector_mad = df.groupby(['year-month', 'industry'])[['b_hml']].apply(mad)
b_hml_sector_mad.name = 'b_hml_sector_mad'
df = df.join(b_hml_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['b_mkt']].apply(mad).any() == 0:
    b_mkt_sector_mad = df.groupby(['year-month', 'industry'])[['b_mkt']].apply(meanad)
else:
    b_mkt_sector_mad = df.groupby(['year-month', 'industry'])[['b_mkt']].apply(mad)
b_mkt_sector_mad.name = 'b_mkt_sector_mad'
df = df.join(b_mkt_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['b_smb']].apply(mad).any() == 0:
    b_smb_sector_mad = df.groupby(['year-month', 'industry'])[['b_smb']].apply(meanad)
else:
    b_smb_sector_mad = df.groupby(['year-month', 'industry'])[['b_smb']].apply(mad)
b_smb_sector_mad.name = 'b_smb_sector_mad'
df = df.join(b_smb_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['b_umd']].apply(mad).any() == 0:
    b_umd_sector_mad = df.groupby(['year-month', 'industry'])[['b_umd']].apply(meanad)
else:
    b_umd_sector_mad = df.groupby(['year-month', 'industry'])[['b_umd']].apply(mad)
b_umd_sector_mad.name = 'b_umd_sector_mad'
df = df.join(b_umd_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['exret']].apply(mad).any() == 0:
    exret_sector_mad = df.groupby(['year-month', 'industry'])[['exret']].apply(meanad)
else:
    exret_sector_mad = df.groupby(['year-month', 'industry'])[['exret']].apply(mad)
exret_sector_mad.name = 'exret_sector_mad'
df = df.join(exret_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['ivol']].apply(mad).any() == 0:
    ivol_sector_mad = df.groupby(['year-month', 'industry'])[['ivol']].apply(meanad)
else:
    ivol_sector_mad = df.groupby(['year-month', 'industry'])[['ivol']].apply(mad)
ivol_sector_mad.name = 'ivol_sector_mad'
df = df.join(ivol_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['n']].apply(mad).any() == 0:
    n_sector_mad = df.groupby(['year-month', 'industry'])[['n']].apply(meanad)
else:
    n_sector_mad = df.groupby(['year-month', 'industry'])[['n']].apply(mad)
n_sector_mad.name = 'n_sector_mad'
df = df.join(n_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['R2']].apply(mad).any() == 0:
    R2_sector_mad = df.groupby(['year-month', 'industry'])[['R2']].apply(meanad)
else:
    R2_sector_mad = df.groupby(['year-month', 'industry'])[['R2']].apply(mad)
R2_sector_mad.name = 'R2_sector_mad'
df = df.join(R2_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['tvol']].apply(mad).any() == 0:
    tvol_sector_mad = df.groupby(['year-month', 'industry'])[['tvol']].apply(meanad)
else:
    tvol_sector_mad = df.groupby(['year-month', 'industry'])[['tvol']].apply(mad)
tvol_sector_mad.name = 'tvol_sector_mad'
df = df.join(tvol_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['BUYPCT']].apply(mad).any() == 0:
    BUYPCT_sector_mad = df.groupby(['year-month', 'industry'])[['BUYPCT']].apply(meanad)
else:
    BUYPCT_sector_mad = df.groupby(['year-month', 'industry'])[['BUYPCT']].apply(mad)
BUYPCT_sector_mad.name = 'BUYPCT_sector_mad'
df = df.join(BUYPCT_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['HOLDPCT']].apply(mad).any() == 0:
    HOLDPCT_sector_mad = df.groupby(['year-month', 'industry'])[['HOLDPCT']].apply(meanad)
else:
    HOLDPCT_sector_mad = df.groupby(['year-month', 'industry'])[['HOLDPCT']].apply(mad)
HOLDPCT_sector_mad.name = 'HOLDPCT_sector_mad'
df = df.join(HOLDPCT_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['MEANREC']].apply(mad).any() == 0:
    MEANREC_sector_mad = df.groupby(['year-month', 'industry'])[['MEANREC']].apply(meanad)
else:
    MEANREC_sector_mad = df.groupby(['year-month', 'industry'])[['MEANREC']].apply(mad)
MEANREC_sector_mad.name = 'MEANREC_sector_mad'
df = df.join(MEANREC_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['MEDREC']].apply(mad).any() == 0:
    MEDREC_sector_mad = df.groupby(['year-month', 'industry'])[['MEDREC']].apply(meanad)
else:
    MEDREC_sector_mad = df.groupby(['year-month', 'industry'])[['MEDREC']].apply(mad)
MEDREC_sector_mad.name = 'MEDREC_sector_mad'
df = df.join(MEDREC_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['NUMDOWN']].apply(mad).any() == 0:
    NUMDOWN_sector_mad = df.groupby(['year-month', 'industry'])[['NUMDOWN']].apply(meanad)
else:
    NUMDOWN_sector_mad = df.groupby(['year-month', 'industry'])[['NUMDOWN']].apply(mad)
NUMDOWN_sector_mad.name = 'NUMDOWN_sector_mad'
df = df.join(NUMDOWN_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['NUMREC']].apply(mad).any() == 0:
    NUMREC_sector_mad = df.groupby(['year-month', 'industry'])[['NUMREC']].apply(meanad)
else:
    NUMREC_sector_mad = df.groupby(['year-month', 'industry'])[['NUMREC']].apply(mad)
NUMREC_sector_mad.name = 'NUMREC_sector_mad'
df = df.join(NUMREC_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['NUMUP']].apply(mad).any() == 0:
    NUMUP_sector_mad = df.groupby(['year-month', 'industry'])[['NUMUP']].apply(meanad)
else:
    NUMUP_sector_mad = df.groupby(['year-month', 'industry'])[['NUMUP']].apply(mad)
NUMUP_sector_mad.name = 'NUMUP_sector_mad'
df = df.join(NUMUP_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['SELLPCT']].apply(mad).any() == 0:
    SELLPCT_sector_mad = df.groupby(['year-month', 'industry'])[['SELLPCT']].apply(meanad)
else:
    SELLPCT_sector_mad = df.groupby(['year-month', 'industry'])[['SELLPCT']].apply(mad)
SELLPCT_sector_mad.name = 'SELLPCT_sector_mad'
df = df.join(SELLPCT_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['STDEV']].apply(mad).any() == 0:
    STDEV_sector_mad = df.groupby(['year-month', 'industry'])[['STDEV']].apply(meanad)
else:
    STDEV_sector_mad = df.groupby(['year-month', 'industry'])[['STDEV']].apply(mad)
STDEV_sector_mad.name = 'STDEV_sector_mad'
df = df.join(STDEV_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['ACTUAL_EPS']].apply(mad).any() == 0:
    ACTUAL_EPS_sector_mad = df.groupby(['year-month', 'industry'])[['ACTUAL_EPS']].apply(meanad)
else:
    ACTUAL_EPS_sector_mad = df.groupby(['year-month', 'industry'])[['ACTUAL_EPS']].apply(mad)
ACTUAL_EPS_sector_mad.name = 'ACTUAL_EPS_sector_mad'
df = df.join(ACTUAL_EPS_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['CONSENSUS_EPS']].apply(mad).any() == 0:
    CONSENSUS_EPS_sector_mad = df.groupby(['year-month', 'industry'])[['CONSENSUS_EPS']].apply(meanad)
else:
    CONSENSUS_EPS_sector_mad = df.groupby(['year-month', 'industry'])[['CONSENSUS_EPS']].apply(mad)
CONSENSUS_EPS_sector_mad.name = 'CONSENSUS_EPS_sector_mad'
df = df.join(CONSENSUS_EPS_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['CONSENSUS_STD']].apply(mad).any() == 0:
    CONSENSUS_STD_sector_mad = df.groupby(['year-month', 'industry'])[['CONSENSUS_STD']].apply(meanad)
else:
    CONSENSUS_STD_sector_mad = df.groupby(['year-month', 'industry'])[['CONSENSUS_STD']].apply(mad)
CONSENSUS_STD_sector_mad.name = 'CONSENSUS_STD_sector_mad'
df = df.join(CONSENSUS_STD_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['NUMBER_OF_EST']].apply(mad).any() == 0:
    NUMBER_OF_EST_sector_mad = df.groupby(['year-month', 'industry'])[['NUMBER_OF_EST']].apply(meanad)
else:
    NUMBER_OF_EST_sector_mad = df.groupby(['year-month', 'industry'])[['NUMBER_OF_EST']].apply(mad)
NUMBER_OF_EST_sector_mad.name = 'NUMBER_OF_EST_sector_mad'
df = df.join(NUMBER_OF_EST_sector_mad, on=['year-month', 'industry'])

if df.groupby(['year-month', 'industry'])[['SURPRISE_PCT']].apply(mad).any() == 0:
    SURPRISE_PCT_sector_mad = df.groupby(['year-month', 'industry'])[['SURPRISE_PCT']].apply(meanad)
else:
    SURPRISE_PCT_sector_mad = df.groupby(['year-month', 'industry'])[['SURPRISE_PCT']].apply(mad)
SURPRISE_PCT_sector_mad.name = 'SURPRISE_PCT_sector_mad'
df = df.join(SURPRISE_PCT_sector_mad, on=['year-month', 'industry'])

C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:717: RuntimeWarning: All-NaN slice encountered
  warnings.warn("All-NaN slice encountered", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:717: RuntimeWarning: All-NaN slice encountered
  warnings.warn("All-NaN slice encountered", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:717: RuntimeWarning: All-NaN slice encountered
  warnings.warn("All-NaN slice encountered", RuntimeWarning)
C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\nanfunctions.py:703: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empt

In [67]:
return_all_columns(df)

GVKEY   tic                         conm                industry  \
0   1045   AAL  AMERICAN AIRLINES GROUP INC             Industrials   
1   1050  CECE      CECO ENVIRONMENTAL CORP             Industrials   
2   1075   PNW   PINNACLE WEST CAPITAL CORP               Utilities   
3   1076   AAN                  AARON'S INC  Consumer Discretionary   
4   1078   ABT          ABBOTT LABORATORIES             Health Care   

  GVKEY-year-month year-month  forward_one_month_return  \
0     1045-2015-01    2015-01                 -2.200307   
1     1050-2015-01    2015-01                  3.717201   
2     1075-2015-01    2015-01                 -8.691935   
3     1076-2015-01    2015-01                 -5.843335   
4     1078-2015-01    2015-01                  5.831099   

   forward_two_month_return  forward_three_month_return  \
0                  7.763420                   -1.208663   
1                -22.185362                  -13.531142   
2                 -9.162154                  -11.947686   
3                -10.510038                    7.476464   
4                  3.507596                    4.245988   

   forward_four_month_return  forward_five_month_return  \
0                 -13.310781                 -18.292802   
1                 -16.758139                 -16.421029   
2                 -12.350540                 -18.148756   
3                  10.732369                  14.533202   
4                   9.141642                  10.219585   

   forward_six_month_return  forward_seven_month_return  \
0                -17.955212                  -20.041269   
1                -33.608937                  -28.592724   
2                -10.358036                  -13.524775   
3                 16.968733                   19.087961   
4                 14.373570                    2.189366   

   forward_eight_month_return  forward_nine_month_return  \
0                  -20.348960                  -5.190032   
1                  -39.099046                 -33.670756   
2                   -6.828139                  -6.835474   
3                   14.287472                 -21.919913   
4                   -9.250247                   1.625125   

   forward_ten_month_return  forward_eleven_month_return  \
0                -15.163603                   -12.922409   
1                -35.381039                   -42.399508   
2                 -7.055513                    -5.412555   
3                -23.104592                   -29.061055   
4                  1.897335                     1.874651   

   forward_twelve_month_return  forward_thirteen_month_return  \
0                          NaN                            NaN   
1                          NaN                            NaN   
2                          NaN                            NaN   
3                          NaN                            NaN   
4                          NaN                            NaN   

   forward_fourteen_month_return  forward_fifteen_month_return  \
0                            NaN                           NaN   
1                            NaN                           NaN   
2                            NaN                           NaN   
3                            NaN                           NaN   
4                            NaN                           NaN   

   forward_sixteen_month_return  forward_seventeen_month_return  \
0                           NaN                             NaN   
1                           NaN                             NaN   
2                           NaN                             NaN   
3                           NaN                             NaN   
4                           NaN                             NaN   

   forward_eighteen_month_return  forward_nineteen_month_return  \
0                            NaN                            NaN   
1                            NaN                            NaN   
2                            NaN          

In [68]:
df['forward_one_month_return_zscore'] = (df['forward_one_month_return'] - df['forward_one_month_return_median']) / df['forward_one_month_return_mad']
df['forward_two_month_return_zscore'] = (df['forward_two_month_return'] - df['forward_two_month_return_median']) / df['forward_two_month_return_mad']
df['forward_three_month_return_zscore'] = (df['forward_three_month_return'] - df['forward_three_month_return_median']) / df['forward_three_month_return_mad']
df['forward_four_month_return_zscore'] = (df['forward_four_month_return'] - df['forward_four_month_return_median']) / df['forward_four_month_return_mad']
df['forward_five_month_return_zscore'] = (df['forward_five_month_return'] - df['forward_five_month_return_median']) / df['forward_five_month_return_mad']
df['forward_six_month_return_zscore'] = (df['forward_six_month_return'] - df['forward_six_month_return_median']) / df['forward_six_month_return_mad']
df['forward_seven_month_return_zscore'] = (df['forward_seven_month_return'] - df['forward_seven_month_return_median']) / df['forward_seven_month_return_mad']
df['forward_eight_month_return_zscore'] = (df['forward_eight_month_return'] - df['forward_eight_month_return_median']) / df['forward_eight_month_return_mad']
df['forward_nine_month_return_zscore'] = (df['forward_nine_month_return'] - df['forward_nine_month_return_median']) / df['forward_nine_month_return_mad']
df['forward_ten_month_return_zscore'] = (df['forward_ten_month_return'] - df['forward_ten_month_return_median']) / df['forward_ten_month_return_mad']
df['forward_eleven_month_return_zscore'] = (df['forward_eleven_month_return'] - df['forward_eleven_month_return_median']) / df['forward_eleven_month_return_mad']
df['forward_twelve_month_return_zscore'] = (df['forward_twelve_month_return'] - df['forward_twelve_month_return_median']) / df['forward_twelve_month_return_mad']
df['forward_thirteen_month_return_zscore'] = (df['forward_thirteen_month_return'] - df['forward_thirteen_month_return_median']) / df['forward_thirteen_month_return_mad']
df['forward_fourteen_month_return_zscore'] = (df['forward_fourteen_month_return'] - df['forward_fourteen_month_return_median']) / df['forward_fourteen_month_return_mad']
df['forward_fifteen_month_return_zscore'] = (df['forward_fifteen_month_return'] - df['forward_fifteen_month_return_median']) / df['forward_fifteen_month_return_mad']
df['forward_sixteen_month_return_zscore'] = (df['forward_sixteen_month_return'] - df['forward_sixteen_month_return_median']) / df['forward_sixteen_month_return_mad']
df['forward_seventeen_month_return_zscore'] = (df['forward_seventeen_month_return'] - df['forward_seventeen_month_return_median']) / df['forward_seventeen_month_return_mad']
df['forward_eighteen_month_return_zscore'] = (df['forward_eighteen_month_return'] - df['forward_eighteen_month_return_median']) / df['forward_eighteen_month_return_mad']
df['forward_nineteen_month_return_zscore'] = (df['forward_nineteen_month_return'] - df['forward_nineteen_month_return_median']) / df['forward_nineteen_month_return_mad']
df['forward_twenty_month_return_zscore'] = (df['forward_twenty_month_return'] - df['forward_twenty_month_return_median']) / df['forward_twenty_month_return_mad']
df['forward_twentyone_month_return_zscore'] = (df['forward_twentyone_month_return'] - df['forward_twentyone_month_return_median']) / df['forward_twentyone_month_return_mad']
df['forward_twentytwo_month_return_zscore'] = (df['forward_twentytwo_month_return'] - df['forward_twentytwo_month_return_median']) / df['forward_twentytwo_month_return_mad']
df['forward_twentythree_month_return_zscore'] = (df['forward_twentythree_month_return'] - df['forward_twentythree_month_return_median']) / df['forward_twentythree_month_return_mad']
df['forward_twentyfour_month_return_zscore'] = (df['forward_twentyfour_month_return'] - df['forward_twentyfour_month_return_median']) / df['forward_twentyfour_month_return_mad']
df['forward_twentyfive_month_return_zscore'] = (df['forward_twentyfive_month_return'] - df['forward_twentyfive_month_return_median']) / df['forward_twentyfive_month_return_mad']
df['forward_twentysix_month_return_zscore'] = (df['forward_twentysix_month_return'] - df['forward_twentysix_month_return_median']) / df['forward_twentysix_month_return_mad']
df['forward_twentyseven_month_return_zscore'] = (df['forward_twentyseven_month_return'] - df['forward_twentyseven_month_return_median']) / df['forward_twentyseven_month_return_mad']
df['forward_twentyeight_month_return_zscore'] = (df['forward_twentyeight_month_return'] - df['forward_twentyeight_month_return_median']) / df['forward_twentyeight_month_return_mad']
df['forward_twentynine_month_return_zscore'] = (df['forward_twentynine_month_return'] - df['forward_twentynine_month_return_median']) / df['forward_twentynine_month_return_mad']
df['forward_thirty_month_return_zscore'] = (df['forward_thirty_month_return'] - df['forward_thirty_month_return_median']) / df['forward_thirty_month_return_mad']
df['forward_thirtyone_month_return_zscore'] = (df['forward_thirtyone_month_return'] - df['forward_thirtyone_month_return_median']) / df['forward_thirtyone_month_return_mad']
df['forward_thirtytwo_month_return_zscore'] = (df['forward_thirtytwo_month_return'] - df['forward_thirtytwo_month_return_median']) / df['forward_thirtytwo_month_return_mad']
df['forward_thirtythree_month_return_zscore'] = (df['forward_thirtythree_month_return'] - df['forward_thirtythree_month_return_median']) / df['forward_thirtythree_month_return_mad']
df['forward_thirtyfour_month_return_zscore'] = (df['forward_thirtyfour_month_return'] - df['forward_thirtyfour_month_return_median']) / df['forward_thirtyfour_month_return_mad']
df['forward_thirtyfive_month_return_zscore'] = (df['forward_thirtyfive_month_return'] - df['forward_thirtyfive_month_return_median']) / df['forward_thirtyfive_month_return_mad']
df['forward_thirtysix_month_return_zscore'] = (df['forward_thirtysix_month_return'] - df['forward_thirtysix_month_return_median']) / df['forward_thirtysix_month_return_mad']
df['past_one_month_return_zscore'] = (df['past_one_month_return'] - df['past_one_month_return_median']) / df['past_one_month_return_mad']
df['past_two_month_return_zscore'] = (df['past_two_month_return'] - df['past_two_month_return_median']) / df['past_two_month_return_mad']
df['past_three_month_return_zscore'] = (df['past_three_month_return'] - df['past_three_month_return_median']) / df['past_three_month_return_mad']
df['past_four_month_return_zscore'] = (df['past_four_month_return'] - df['past_four_month_return_median']) / df['past_four_month_return_mad']
df['past_five_month_return_zscore'] = (df['past_five_month_return'] - df['past_five_month_return_median']) / df['past_five_month_return_mad']
df['past_six_month_return_zscore'] = (df['past_six_month_return'] - df['past_six_month_return_median']) / df['past_six_month_return_mad']
df['past_seven_month_return_zscore'] = (df['past_seven_month_return'] - df['past_seven_month_return_median']) / df['past_seven_month_return_mad']
df['past_eight_month_return_zscore'] = (df['past_eight_month_return'] - df['past_eight_month_return_median']) / df['past_eight_month_return_mad']
df['past_nine_month_return_zscore'] = (df['past_nine_month_return'] - df['past_nine_month_return_median']) / df['past_nine_month_return_mad']
df['past_ten_month_return_zscore'] = (df['past_ten_month_return'] - df['past_ten_month_return_median']) / df['past_ten_month_return_mad']
df['past_eleven_month_return_zscore'] = (df['past_eleven_month_return'] - df['past_eleven_month_return_median']) / df['past_eleven_month_return_mad']
df['past_twelve_month_return_zscore'] = (df['past_twelve_month_return'] - df['past_twelve_month_return_median']) / df['past_twelve_month_return_mad']
df['past_thirteen_month_return_zscore'] = (df['past_thirteen_month_return'] - df['past_thirteen_month_return_median']) / df['past_thirteen_month_return_mad']
df['past_fourteen_month_return_zscore'] = (df['past_fourteen_month_return'] - df['past_fourteen_month_return_median']) / df['past_fourteen_month_return_mad']
df['past_fifteen_month_return_zscore'] = (df['past_fifteen_month_return'] - df['past_fifteen_month_return_median']) / df['past_fifteen_month_return_mad']
df['past_sixteen_month_return_zscore'] = (df['past_sixteen_month_return'] - df['past_sixteen_month_return_median']) / df['past_sixteen_month_return_mad']
df['past_seventeen_month_return_zscore'] = (df['past_seventeen_month_return'] - df['past_seventeen_month_return_median']) / df['past_seventeen_month_return_mad']
df['past_eighteen_month_return_zscore'] = (df['past_eighteen_month_return'] - df['past_eighteen_month_return_median']) / df['past_eighteen_month_return_mad']
df['past_nineteen_month_return_zscore'] = (df['past_nineteen_month_return'] - df['past_nineteen_month_return_median']) / df['past_nineteen_month_return_mad']
df['past_twenty_month_return_zscore'] = (df['past_twenty_month_return'] - df['past_twenty_month_return_median']) / df['past_twenty_month_return_mad']
df['past_twentyone_month_return_zscore'] = (df['past_twentyone_month_return'] - df['past_twentyone_month_return_median']) / df['past_twentyone_month_return_mad']
df['past_twentytwo_month_return_zscore'] = (df['past_twentytwo_month_return'] - df['past_twentytwo_month_return_median']) / df['past_twentytwo_month_return_mad']
df['past_twentythree_month_return_zscore'] = (df['past_twentythree_month_return'] - df['past_twentythree_month_return_median']) / df['past_twentythree_month_return_mad']
df['past_twentyfour_month_return_zscore'] = (df['past_twentyfour_month_return'] - df['past_twentyfour_month_return_median']) / df['past_twentyfour_month_return_mad']
df['past_twentyfive_month_return_zscore'] = (df['past_twentyfive_month_return'] - df['past_twentyfive_month_return_median']) / df['past_twentyfive_month_return_mad']
df['past_twentysix_month_return_zscore'] = (df['past_twentysix_month_return'] - df['past_twentysix_month_return_median']) / df['past_twentysix_month_return_mad']
df['past_twentyseven_month_return_zscore'] = (df['past_twentyseven_month_return'] - df['past_twentyseven_month_return_median']) / df['past_twentyseven_month_return_mad']
df['past_twentyeight_month_return_zscore'] = (df['past_twentyeight_month_return'] - df['past_twentyeight_month_return_median']) / df['past_twentyeight_month_return_mad']
df['past_twentynine_month_return_zscore'] = (df['past_twentynine_month_return'] - df['past_twentynine_month_return_median']) / df['past_twentynine_month_return_mad']
df['past_thirty_month_return_zscore'] = (df['past_thirty_month_return'] - df['past_thirty_month_return_median']) / df['past_thirty_month_return_mad']
df['past_thirtyone_month_return_zscore'] = (df['past_thirtyone_month_return'] - df['past_thirtyone_month_return_median']) / df['past_thirtyone_month_return_mad']
df['past_thirtytwo_month_return_zscore'] = (df['past_thirtytwo_month_return'] - df['past_thirtytwo_month_return_median']) / df['past_thirtytwo_month_return_mad']
df['past_thirtythree_month_return_zscore'] = (df['past_thirtythree_month_return'] - df['past_thirtythree_month_return_median']) / df['past_thirtythree_month_return_mad']
df['past_thirtyfour_month_return_zscore'] = (df['past_thirtyfour_month_return'] - df['past_thirtyfour_month_return_median']) / df['past_thirtyfour_month_return_mad']
df['past_thirtyfive_month_return_zscore'] = (df['past_thirtyfive_month_return'] - df['past_thirtyfive_month_return_median']) / df['past_thirtyfive_month_return_mad']
df['past_thirtysix_month_return_zscore'] = (df['past_thirtysix_month_return'] - df['past_thirtysix_month_return_median']) / df['past_thirtysix_month_return_mad']
df['accrual_zscore'] = (df['accrual'] - df['accrual_median']) / df['accrual_mad']
df['adv_sale_zscore'] = (df['adv_sale'] - df['adv_sale_median']) / df['adv_sale_mad']
df['aftret_eq_zscore'] = (df['aftret_eq'] - df['aftret_eq_median']) / df['aftret_eq_mad']
df['aftret_equity_zscore'] = (df['aftret_equity'] - df['aftret_equity_median']) / df['aftret_equity_mad']
df['aftret_invcapx_zscore'] = (df['aftret_invcapx'] - df['aftret_invcapx_median']) / df['aftret_invcapx_mad']
df['at_turn_zscore'] = (df['at_turn'] - df['at_turn_median']) / df['at_turn_mad']
df['bm_zscore'] = (df['bm'] - df['bm_median']) / df['bm_mad']
df['CAPEI_zscore'] = (df['CAPEI'] - df['CAPEI_median']) / df['CAPEI_mad']
df['capital_ratio_zscore'] = (df['capital_ratio'] - df['capital_ratio_median']) / df['capital_ratio_mad']
df['cash_conversion_zscore'] = (df['cash_conversion'] - df['cash_conversion_median']) / df['cash_conversion_mad']
df['cash_debt_zscore'] = (df['cash_debt'] - df['cash_debt_median']) / df['cash_debt_mad']
df['cash_lt_zscore'] = (df['cash_lt'] - df['cash_lt_median']) / df['cash_lt_mad']
df['cash_ratio_zscore'] = (df['cash_ratio'] - df['cash_ratio_median']) / df['cash_ratio_mad']
df['cfm_zscore'] = (df['cfm'] - df['cfm_median']) / df['cfm_mad']
df['curr_debt_zscore'] = (df['curr_debt'] - df['curr_debt_median']) / df['curr_debt_mad']
df['curr_ratio_zscore'] = (df['curr_ratio'] - df['curr_ratio_median']) / df['curr_ratio_mad']
df['de_ratio_zscore'] = (df['de_ratio'] - df['de_ratio_median']) / df['de_ratio_mad']
df['debt_assets_zscore'] = (df['debt_assets'] - df['debt_assets_median']) / df['debt_assets_mad']
df['debt_at_zscore'] = (df['debt_at'] - df['debt_at_median']) / df['debt_at_mad']
df['debt_capital_zscore'] = (df['debt_capital'] - df['debt_capital_median']) / df['debt_capital_mad']
df['debt_ebitda_zscore'] = (df['debt_ebitda'] - df['debt_ebitda_median']) / df['debt_ebitda_mad']
df['debt_invcap_zscore'] = (df['debt_invcap'] - df['debt_invcap_median']) / df['debt_invcap_mad']
df['DIVYIELD_zscore'] = (df['DIVYIELD'] - df['DIVYIELD_median']) / df['DIVYIELD_mad']
df['dltt_be_zscore'] = (df['dltt_be'] - df['dltt_be_median']) / df['dltt_be_mad']
df['dpr_zscore'] = (df['dpr'] - df['dpr_median']) / df['dpr_mad']
df['efftax_zscore'] = (df['efftax'] - df['efftax_median']) / df['efftax_mad']
df['equity_invcap_zscore'] = (df['equity_invcap'] - df['equity_invcap_median']) / df['equity_invcap_mad']
df['evm_zscore'] = (df['evm'] - df['evm_median']) / df['evm_mad']
df['fcf_ocf_zscore'] = (df['fcf_ocf'] - df['fcf_ocf_median']) / df['fcf_ocf_mad']
df['gpm_zscore'] = (df['gpm'] - df['gpm_median']) / df['gpm_mad']
df['GProf_zscore'] = (df['GProf'] - df['GProf_median']) / df['GProf_mad']
df['int_debt_zscore'] = (df['int_debt'] - df['int_debt_median']) / df['int_debt_mad']
df['int_totdebt_zscore'] = (df['int_totdebt'] - df['int_totdebt_median']) / df['int_totdebt_mad']
df['intcov_zscore'] = (df['intcov'] - df['intcov_median']) / df['intcov_mad']
df['intcov_ratio_zscore'] = (df['intcov_ratio'] - df['intcov_ratio_median']) / df['intcov_ratio_mad']
df['inv_turn_zscore'] = (df['inv_turn'] - df['inv_turn_median']) / df['inv_turn_mad']
df['invt_act_zscore'] = (df['invt_act'] - df['invt_act_median']) / df['invt_act_mad']
df['lt_debt_zscore'] = (df['lt_debt'] - df['lt_debt_median']) / df['lt_debt_mad']
df['lt_ppent_zscore'] = (df['lt_ppent'] - df['lt_ppent_median']) / df['lt_ppent_mad']
df['npm_zscore'] = (df['npm'] - df['npm_median']) / df['npm_mad']
df['ocf_lct_zscore'] = (df['ocf_lct'] - df['ocf_lct_median']) / df['ocf_lct_mad']
df['opmad_zscore'] = (df['opmad'] - df['opmad_median']) / df['opmad_mad']
df['opmbd_zscore'] = (df['opmbd'] - df['opmbd_median']) / df['opmbd_mad']
df['pay_turn_zscore'] = (df['pay_turn'] - df['pay_turn_median']) / df['pay_turn_mad']
df['pcf_zscore'] = (df['pcf'] - df['pcf_median']) / df['pcf_mad']
df['pe_exi_zscore'] = (df['pe_exi'] - df['pe_exi_median']) / df['pe_exi_mad']
df['pe_inc_zscore'] = (df['pe_inc'] - df['pe_inc_median']) / df['pe_inc_mad']
df['pe_op_basic_zscore'] = (df['pe_op_basic'] - df['pe_op_basic_median']) / df['pe_op_basic_mad']
df['pe_op_dil_zscore'] = (df['pe_op_dil'] - df['pe_op_dil_median']) / df['pe_op_dil_mad']
df['PEG_1yrforward_zscore'] = (df['PEG_1yrforward'] - df['PEG_1yrforward_median']) / df['PEG_1yrforward_mad']
df['PEG_ltgforward_zscore'] = (df['PEG_ltgforward'] - df['PEG_ltgforward_median']) / df['PEG_ltgforward_mad']
df['PEG_trailing_zscore'] = (df['PEG_trailing'] - df['PEG_trailing_median']) / df['PEG_trailing_mad']
df['pretret_earnat_zscore'] = (df['pretret_earnat'] - df['pretret_earnat_median']) / df['pretret_earnat_mad']
df['pretret_noa_zscore'] = (df['pretret_noa'] - df['pretret_noa_median']) / df['pretret_noa_mad']
df['profit_lct_zscore'] = (df['profit_lct'] - df['profit_lct_median']) / df['profit_lct_mad']
df['ps_zscore'] = (df['ps'] - df['ps_median']) / df['ps_mad']
df['ptb_zscore'] = (df['ptb'] - df['ptb_median']) / df['ptb_mad']
df['ptpm_zscore'] = (df['ptpm'] - df['ptpm_median']) / df['ptpm_mad']
df['quick_ratio_zscore'] = (df['quick_ratio'] - df['quick_ratio_median']) / df['quick_ratio_mad']
df['rd_sale_zscore'] = (df['rd_sale'] - df['rd_sale_median']) / df['rd_sale_mad']
df['rect_act_zscore'] = (df['rect_act'] - df['rect_act_median']) / df['rect_act_mad']
df['rect_turn_zscore'] = (df['rect_turn'] - df['rect_turn_median']) / df['rect_turn_mad']
df['roa_zscore'] = (df['roa'] - df['roa_median']) / df['roa_mad']
df['roce_zscore'] = (df['roce'] - df['roce_median']) / df['roce_mad']
df['roe_zscore'] = (df['roe'] - df['roe_median']) / df['roe_mad']
df['sale_equity_zscore'] = (df['sale_equity'] - df['sale_equity_median']) / df['sale_equity_mad']
df['sale_invcap_zscore'] = (df['sale_invcap'] - df['sale_invcap_median']) / df['sale_invcap_mad']
df['sale_nwc_zscore'] = (df['sale_nwc'] - df['sale_nwc_median']) / df['sale_nwc_mad']
df['short_debt_zscore'] = (df['short_debt'] - df['short_debt_median']) / df['short_debt_mad']
df['staff_sale_zscore'] = (df['staff_sale'] - df['staff_sale_median']) / df['staff_sale_mad']
df['totdebt_invcap_zscore'] = (df['totdebt_invcap'] - df['totdebt_invcap_median']) / df['totdebt_invcap_mad']
df['dvpspm_zscore'] = (df['dvpspm'] - df['dvpspm_median']) / df['dvpspm_mad']
df['dvpsxm_zscore'] = (df['dvpsxm'] - df['dvpsxm_median']) / df['dvpsxm_mad']
df['dvrate_zscore'] = (df['dvrate'] - df['dvrate_median']) / df['dvrate_mad']
df['spcsrc_zscore'] = (df['spcsrc'] - df['spcsrc_median']) / df['spcsrc_mad']
df['alpha_zscore'] = (df['alpha'] - df['alpha_median']) / df['alpha_mad']
df['b_hml_zscore'] = (df['b_hml'] - df['b_hml_median']) / df['b_hml_mad']
df['b_mkt_zscore'] = (df['b_mkt'] - df['b_mkt_median']) / df['b_mkt_mad']
df['b_smb_zscore'] = (df['b_smb'] - df['b_smb_median']) / df['b_smb_mad']
df['b_umd_zscore'] = (df['b_umd'] - df['b_umd_median']) / df['b_umd_mad']
df['exret_zscore'] = (df['exret'] - df['exret_median']) / df['exret_mad']
df['ivol_zscore'] = (df['ivol'] - df['ivol_median']) / df['ivol_mad']
df['n_zscore'] = (df['n'] - df['n_median']) / df['n_mad']
df['R2_zscore'] = (df['R2'] - df['R2_median']) / df['R2_mad']
df['tvol_zscore'] = (df['tvol'] - df['tvol_median']) / df['tvol_mad']
df['BUYPCT_zscore'] = (df['BUYPCT'] - df['BUYPCT_median']) / df['BUYPCT_mad']
df['HOLDPCT_zscore'] = (df['HOLDPCT'] - df['HOLDPCT_median']) / df['HOLDPCT_mad']
df['MEANREC_zscore'] = (df['MEANREC'] - df['MEANREC_median']) / df['MEANREC_mad']
df['MEDREC_zscore'] = (df['MEDREC'] - df['MEDREC_median']) / df['MEDREC_mad']
df['NUMDOWN_zscore'] = (df['NUMDOWN'] - df['NUMDOWN_median']) / df['NUMDOWN_mad']
df['NUMREC_zscore'] = (df['NUMREC'] - df['NUMREC_median']) / df['NUMREC_mad']
df['NUMUP_zscore'] = (df['NUMUP'] - df['NUMUP_median']) / df['NUMUP_mad']
df['SELLPCT_zscore'] = (df['SELLPCT'] - df['SELLPCT_median']) / df['SELLPCT_mad']
df['STDEV_zscore'] = (df['STDEV'] - df['STDEV_median']) / df['STDEV_mad']
# df['ACTUAL_EPS_zscore'] = (df['ACTUAL_EPS'] - df['ACTUAL_EPS_median']) / df['ACTUAL_EPS_mad']
# df['CONSENSUS_EPS_zscore'] = (df['CONSENSUS_EPS'] - df['CONSENSUS_EPS_median']) / df['CONSENSUS_EPS_mad']
# df['CONSENSUS_STD_zscore'] = (df['CONSENSUS_STD'] - df['CONSENSUS_STD_median']) / df['CONSENSUS_STD_mad']
# df['NUMBER_OF_EST_zscore'] = (df['NUMBER_OF_EST'] - df['NUMBER_OF_EST_median']) / df['NUMBER_OF_EST_mad']
# df['SURPRISE_PCT_zscore'] = (df['SURPRISE_PCT'] - df['SURPRISE_PCT_median']) / df['SURPRISE_PCT_mad']

In [69]:
df['forward_one_month_return_sector_zscore'] = (df['forward_one_month_return'] - df['forward_one_month_return_sector_median']) / df['forward_one_month_return_sector_mad']
df['forward_two_month_return_sector_zscore'] = (df['forward_two_month_return'] - df['forward_two_month_return_sector_median']) / df['forward_two_month_return_sector_mad']
df['forward_three_month_return_sector_zscore'] = (df['forward_three_month_return'] - df['forward_three_month_return_sector_median']) / df['forward_three_month_return_sector_mad']
df['forward_four_month_return_sector_zscore'] = (df['forward_four_month_return'] - df['forward_four_month_return_sector_median']) / df['forward_four_month_return_sector_mad']
df['forward_five_month_return_sector_zscore'] = (df['forward_five_month_return'] - df['forward_five_month_return_sector_median']) / df['forward_five_month_return_sector_mad']
df['forward_six_month_return_sector_zscore'] = (df['forward_six_month_return'] - df['forward_six_month_return_sector_median']) / df['forward_six_month_return_sector_mad']
df['forward_seven_month_return_sector_zscore'] = (df['forward_seven_month_return'] - df['forward_seven_month_return_sector_median']) / df['forward_seven_month_return_sector_mad']
df['forward_eight_month_return_sector_zscore'] = (df['forward_eight_month_return'] - df['forward_eight_month_return_sector_median']) / df['forward_eight_month_return_sector_mad']
df['forward_nine_month_return_sector_zscore'] = (df['forward_nine_month_return'] - df['forward_nine_month_return_sector_median']) / df['forward_nine_month_return_sector_mad']
df['forward_ten_month_return_sector_zscore'] = (df['forward_ten_month_return'] - df['forward_ten_month_return_sector_median']) / df['forward_ten_month_return_sector_mad']
df['forward_eleven_month_return_sector_zscore'] = (df['forward_eleven_month_return'] - df['forward_eleven_month_return_sector_median']) / df['forward_eleven_month_return_sector_mad']
df['forward_twelve_month_return_sector_zscore'] = (df['forward_twelve_month_return'] - df['forward_twelve_month_return_sector_median']) / df['forward_twelve_month_return_sector_mad']
df['forward_thirteen_month_return_sector_zscore'] = (df['forward_thirteen_month_return'] - df['forward_thirteen_month_return_sector_median']) / df['forward_thirteen_month_return_sector_mad']
df['forward_fourteen_month_return_sector_zscore'] = (df['forward_fourteen_month_return'] - df['forward_fourteen_month_return_sector_median']) / df['forward_fourteen_month_return_sector_mad']
df['forward_fifteen_month_return_sector_zscore'] = (df['forward_fifteen_month_return'] - df['forward_fifteen_month_return_sector_median']) / df['forward_fifteen_month_return_sector_mad']
df['forward_sixteen_month_return_sector_zscore'] = (df['forward_sixteen_month_return'] - df['forward_sixteen_month_return_sector_median']) / df['forward_sixteen_month_return_sector_mad']
df['forward_seventeen_month_return_sector_zscore'] = (df['forward_seventeen_month_return'] - df['forward_seventeen_month_return_sector_median']) / df['forward_seventeen_month_return_sector_mad']
df['forward_eighteen_month_return_sector_zscore'] = (df['forward_eighteen_month_return'] - df['forward_eighteen_month_return_sector_median']) / df['forward_eighteen_month_return_sector_mad']
df['forward_nineteen_month_return_sector_zscore'] = (df['forward_nineteen_month_return'] - df['forward_nineteen_month_return_sector_median']) / df['forward_nineteen_month_return_sector_mad']
df['forward_twenty_month_return_sector_zscore'] = (df['forward_twenty_month_return'] - df['forward_twenty_month_return_sector_median']) / df['forward_twenty_month_return_sector_mad']
df['forward_twentyone_month_return_sector_zscore'] = (df['forward_twentyone_month_return'] - df['forward_twentyone_month_return_sector_median']) / df['forward_twentyone_month_return_sector_mad']
df['forward_twentytwo_month_return_sector_zscore'] = (df['forward_twentytwo_month_return'] - df['forward_twentytwo_month_return_sector_median']) / df['forward_twentytwo_month_return_sector_mad']
df['forward_twentythree_month_return_sector_zscore'] = (df['forward_twentythree_month_return'] - df['forward_twentythree_month_return_sector_median']) / df['forward_twentythree_month_return_sector_mad']
df['forward_twentyfour_month_return_sector_zscore'] = (df['forward_twentyfour_month_return'] - df['forward_twentyfour_month_return_sector_median']) / df['forward_twentyfour_month_return_sector_mad']
df['forward_twentyfive_month_return_sector_zscore'] = (df['forward_twentyfive_month_return'] - df['forward_twentyfive_month_return_sector_median']) / df['forward_twentyfive_month_return_sector_mad']
df['forward_twentysix_month_return_sector_zscore'] = (df['forward_twentysix_month_return'] - df['forward_twentysix_month_return_sector_median']) / df['forward_twentysix_month_return_sector_mad']
df['forward_twentyseven_month_return_sector_zscore'] = (df['forward_twentyseven_month_return'] - df['forward_twentyseven_month_return_sector_median']) / df['forward_twentyseven_month_return_sector_mad']
df['forward_twentyeight_month_return_sector_zscore'] = (df['forward_twentyeight_month_return'] - df['forward_twentyeight_month_return_sector_median']) / df['forward_twentyeight_month_return_sector_mad']
df['forward_twentynine_month_return_sector_zscore'] = (df['forward_twentynine_month_return'] - df['forward_twentynine_month_return_sector_median']) / df['forward_twentynine_month_return_sector_mad']
df['forward_thirty_month_return_sector_zscore'] = (df['forward_thirty_month_return'] - df['forward_thirty_month_return_sector_median']) / df['forward_thirty_month_return_sector_mad']
df['forward_thirtyone_month_return_sector_zscore'] = (df['forward_thirtyone_month_return'] - df['forward_thirtyone_month_return_sector_median']) / df['forward_thirtyone_month_return_sector_mad']
df['forward_thirtytwo_month_return_sector_zscore'] = (df['forward_thirtytwo_month_return'] - df['forward_thirtytwo_month_return_sector_median']) / df['forward_thirtytwo_month_return_sector_mad']
df['forward_thirtythree_month_return_sector_zscore'] = (df['forward_thirtythree_month_return'] - df['forward_thirtythree_month_return_sector_median']) / df['forward_thirtythree_month_return_sector_mad']
df['forward_thirtyfour_month_return_sector_zscore'] = (df['forward_thirtyfour_month_return'] - df['forward_thirtyfour_month_return_sector_median']) / df['forward_thirtyfour_month_return_sector_mad']
df['forward_thirtyfive_month_return_sector_zscore'] = (df['forward_thirtyfive_month_return'] - df['forward_thirtyfive_month_return_sector_median']) / df['forward_thirtyfive_month_return_sector_mad']
df['forward_thirtysix_month_return_sector_zscore'] = (df['forward_thirtysix_month_return'] - df['forward_thirtysix_month_return_sector_median']) / df['forward_thirtysix_month_return_sector_mad']
df['past_one_month_return_sector_zscore'] = (df['past_one_month_return'] - df['past_one_month_return_sector_median']) / df['past_one_month_return_sector_mad']
df['past_two_month_return_sector_zscore'] = (df['past_two_month_return'] - df['past_two_month_return_sector_median']) / df['past_two_month_return_sector_mad']
df['past_three_month_return_sector_zscore'] = (df['past_three_month_return'] - df['past_three_month_return_sector_median']) / df['past_three_month_return_sector_mad']
df['past_four_month_return_sector_zscore'] = (df['past_four_month_return'] - df['past_four_month_return_sector_median']) / df['past_four_month_return_sector_mad']
df['past_five_month_return_sector_zscore'] = (df['past_five_month_return'] - df['past_five_month_return_sector_median']) / df['past_five_month_return_sector_mad']
df['past_six_month_return_sector_zscore'] = (df['past_six_month_return'] - df['past_six_month_return_sector_median']) / df['past_six_month_return_sector_mad']
df['past_seven_month_return_sector_zscore'] = (df['past_seven_month_return'] - df['past_seven_month_return_sector_median']) / df['past_seven_month_return_sector_mad']
df['past_eight_month_return_sector_zscore'] = (df['past_eight_month_return'] - df['past_eight_month_return_sector_median']) / df['past_eight_month_return_sector_mad']
df['past_nine_month_return_sector_zscore'] = (df['past_nine_month_return'] - df['past_nine_month_return_sector_median']) / df['past_nine_month_return_sector_mad']
df['past_ten_month_return_sector_zscore'] = (df['past_ten_month_return'] - df['past_ten_month_return_sector_median']) / df['past_ten_month_return_sector_mad']
df['past_eleven_month_return_sector_zscore'] = (df['past_eleven_month_return'] - df['past_eleven_month_return_sector_median']) / df['past_eleven_month_return_sector_mad']
df['past_twelve_month_return_sector_zscore'] = (df['past_twelve_month_return'] - df['past_twelve_month_return_sector_median']) / df['past_twelve_month_return_sector_mad']
df['past_thirteen_month_return_sector_zscore'] = (df['past_thirteen_month_return'] - df['past_thirteen_month_return_sector_median']) / df['past_thirteen_month_return_sector_mad']
df['past_fourteen_month_return_sector_zscore'] = (df['past_fourteen_month_return'] - df['past_fourteen_month_return_sector_median']) / df['past_fourteen_month_return_sector_mad']
df['past_fifteen_month_return_sector_zscore'] = (df['past_fifteen_month_return'] - df['past_fifteen_month_return_sector_median']) / df['past_fifteen_month_return_sector_mad']
df['past_sixteen_month_return_sector_zscore'] = (df['past_sixteen_month_return'] - df['past_sixteen_month_return_sector_median']) / df['past_sixteen_month_return_sector_mad']
df['past_seventeen_month_return_sector_zscore'] = (df['past_seventeen_month_return'] - df['past_seventeen_month_return_sector_median']) / df['past_seventeen_month_return_sector_mad']
df['past_eighteen_month_return_sector_zscore'] = (df['past_eighteen_month_return'] - df['past_eighteen_month_return_sector_median']) / df['past_eighteen_month_return_sector_mad']
df['past_nineteen_month_return_sector_zscore'] = (df['past_nineteen_month_return'] - df['past_nineteen_month_return_sector_median']) / df['past_nineteen_month_return_sector_mad']
df['past_twenty_month_return_sector_zscore'] = (df['past_twenty_month_return'] - df['past_twenty_month_return_sector_median']) / df['past_twenty_month_return_sector_mad']
df['past_twentyone_month_return_sector_zscore'] = (df['past_twentyone_month_return'] - df['past_twentyone_month_return_sector_median']) / df['past_twentyone_month_return_sector_mad']
df['past_twentytwo_month_return_sector_zscore'] = (df['past_twentytwo_month_return'] - df['past_twentytwo_month_return_sector_median']) / df['past_twentytwo_month_return_sector_mad']
df['past_twentythree_month_return_sector_zscore'] = (df['past_twentythree_month_return'] - df['past_twentythree_month_return_sector_median']) / df['past_twentythree_month_return_sector_mad']
df['past_twentyfour_month_return_sector_zscore'] = (df['past_twentyfour_month_return'] - df['past_twentyfour_month_return_sector_median']) / df['past_twentyfour_month_return_sector_mad']
df['past_twentyfive_month_return_sector_zscore'] = (df['past_twentyfive_month_return'] - df['past_twentyfive_month_return_sector_median']) / df['past_twentyfive_month_return_sector_mad']
df['past_twentysix_month_return_sector_zscore'] = (df['past_twentysix_month_return'] - df['past_twentysix_month_return_sector_median']) / df['past_twentysix_month_return_sector_mad']
df['past_twentyseven_month_return_sector_zscore'] = (df['past_twentyseven_month_return'] - df['past_twentyseven_month_return_sector_median']) / df['past_twentyseven_month_return_sector_mad']
df['past_twentyeight_month_return_sector_zscore'] = (df['past_twentyeight_month_return'] - df['past_twentyeight_month_return_sector_median']) / df['past_twentyeight_month_return_sector_mad']
df['past_twentynine_month_return_sector_zscore'] = (df['past_twentynine_month_return'] - df['past_twentynine_month_return_sector_median']) / df['past_twentynine_month_return_sector_mad']
df['past_thirty_month_return_sector_zscore'] = (df['past_thirty_month_return'] - df['past_thirty_month_return_sector_median']) / df['past_thirty_month_return_sector_mad']
df['past_thirtyone_month_return_sector_zscore'] = (df['past_thirtyone_month_return'] - df['past_thirtyone_month_return_sector_median']) / df['past_thirtyone_month_return_sector_mad']
df['past_thirtytwo_month_return_sector_zscore'] = (df['past_thirtytwo_month_return'] - df['past_thirtytwo_month_return_sector_median']) / df['past_thirtytwo_month_return_sector_mad']
df['past_thirtythree_month_return_sector_zscore'] = (df['past_thirtythree_month_return'] - df['past_thirtythree_month_return_sector_median']) / df['past_thirtythree_month_return_sector_mad']
df['past_thirtyfour_month_return_sector_zscore'] = (df['past_thirtyfour_month_return'] - df['past_thirtyfour_month_return_sector_median']) / df['past_thirtyfour_month_return_sector_mad']
df['past_thirtyfive_month_return_sector_zscore'] = (df['past_thirtyfive_month_return'] - df['past_thirtyfive_month_return_sector_median']) / df['past_thirtyfive_month_return_sector_mad']
df['past_thirtysix_month_return_sector_zscore'] = (df['past_thirtysix_month_return'] - df['past_thirtysix_month_return_sector_median']) / df['past_thirtysix_month_return_sector_mad']
df['accrual_sector_zscore'] = (df['accrual'] - df['accrual_sector_median']) / df['accrual_sector_mad']
df['adv_sale_sector_zscore'] = (df['adv_sale'] - df['adv_sale_sector_median']) / df['adv_sale_sector_mad']
df['aftret_eq_sector_zscore'] = (df['aftret_eq'] - df['aftret_eq_sector_median']) / df['aftret_eq_sector_mad']
df['aftret_equity_sector_zscore'] = (df['aftret_equity'] - df['aftret_equity_sector_median']) / df['aftret_equity_sector_mad']
df['aftret_invcapx_sector_zscore'] = (df['aftret_invcapx'] - df['aftret_invcapx_sector_median']) / df['aftret_invcapx_sector_mad']
df['at_turn_sector_zscore'] = (df['at_turn'] - df['at_turn_sector_median']) / df['at_turn_sector_mad']
df['bm_sector_zscore'] = (df['bm'] - df['bm_sector_median']) / df['bm_sector_mad']
df['CAPEI_sector_zscore'] = (df['CAPEI'] - df['CAPEI_sector_median']) / df['CAPEI_sector_mad']
df['capital_ratio_sector_zscore'] = (df['capital_ratio'] - df['capital_ratio_sector_median']) / df['capital_ratio_sector_mad']
df['cash_conversion_sector_zscore'] = (df['cash_conversion'] - df['cash_conversion_sector_median']) / df['cash_conversion_sector_mad']
df['cash_debt_sector_zscore'] = (df['cash_debt'] - df['cash_debt_sector_median']) / df['cash_debt_sector_mad']
df['cash_lt_sector_zscore'] = (df['cash_lt'] - df['cash_lt_sector_median']) / df['cash_lt_sector_mad']
df['cash_ratio_sector_zscore'] = (df['cash_ratio'] - df['cash_ratio_sector_median']) / df['cash_ratio_sector_mad']
df['cfm_sector_zscore'] = (df['cfm'] - df['cfm_sector_median']) / df['cfm_sector_mad']
df['curr_debt_sector_zscore'] = (df['curr_debt'] - df['curr_debt_sector_median']) / df['curr_debt_sector_mad']
df['curr_ratio_sector_zscore'] = (df['curr_ratio'] - df['curr_ratio_sector_median']) / df['curr_ratio_sector_mad']
df['de_ratio_sector_zscore'] = (df['de_ratio'] - df['de_ratio_sector_median']) / df['de_ratio_sector_mad']
df['debt_assets_sector_zscore'] = (df['debt_assets'] - df['debt_assets_sector_median']) / df['debt_assets_sector_mad']
df['debt_at_sector_zscore'] = (df['debt_at'] - df['debt_at_sector_median']) / df['debt_at_sector_mad']
df['debt_capital_sector_zscore'] = (df['debt_capital'] - df['debt_capital_sector_median']) / df['debt_capital_sector_mad']
df['debt_ebitda_sector_zscore'] = (df['debt_ebitda'] - df['debt_ebitda_sector_median']) / df['debt_ebitda_sector_mad']
df['debt_invcap_sector_zscore'] = (df['debt_invcap'] - df['debt_invcap_sector_median']) / df['debt_invcap_sector_mad']
df['DIVYIELD_sector_zscore'] = (df['DIVYIELD'] - df['DIVYIELD_sector_median']) / df['DIVYIELD_sector_mad']
df['dltt_be_sector_zscore'] = (df['dltt_be'] - df['dltt_be_sector_median']) / df['dltt_be_sector_mad']
df['dpr_sector_zscore'] = (df['dpr'] - df['dpr_sector_median']) / df['dpr_sector_mad']
df['efftax_sector_zscore'] = (df['efftax'] - df['efftax_sector_median']) / df['efftax_sector_mad']
df['equity_invcap_sector_zscore'] = (df['equity_invcap'] - df['equity_invcap_sector_median']) / df['equity_invcap_sector_mad']
df['evm_sector_zscore'] = (df['evm'] - df['evm_sector_median']) / df['evm_sector_mad']
df['fcf_ocf_sector_zscore'] = (df['fcf_ocf'] - df['fcf_ocf_sector_median']) / df['fcf_ocf_sector_mad']
df['gpm_sector_zscore'] = (df['gpm'] - df['gpm_sector_median']) / df['gpm_sector_mad']
df['GProf_sector_zscore'] = (df['GProf'] - df['GProf_sector_median']) / df['GProf_sector_mad']
df['int_debt_sector_zscore'] = (df['int_debt'] - df['int_debt_sector_median']) / df['int_debt_sector_mad']
df['int_totdebt_sector_zscore'] = (df['int_totdebt'] - df['int_totdebt_sector_median']) / df['int_totdebt_sector_mad']
df['intcov_sector_zscore'] = (df['intcov'] - df['intcov_sector_median']) / df['intcov_sector_mad']
df['intcov_ratio_sector_zscore'] = (df['intcov_ratio'] - df['intcov_ratio_sector_median']) / df['intcov_ratio_sector_mad']
df['inv_turn_sector_zscore'] = (df['inv_turn'] - df['inv_turn_sector_median']) / df['inv_turn_sector_mad']
df['invt_act_sector_zscore'] = (df['invt_act'] - df['invt_act_sector_median']) / df['invt_act_sector_mad']
df['lt_debt_sector_zscore'] = (df['lt_debt'] - df['lt_debt_sector_median']) / df['lt_debt_sector_mad']
df['lt_ppent_sector_zscore'] = (df['lt_ppent'] - df['lt_ppent_sector_median']) / df['lt_ppent_sector_mad']
df['npm_sector_zscore'] = (df['npm'] - df['npm_sector_median']) / df['npm_sector_mad']
df['ocf_lct_sector_zscore'] = (df['ocf_lct'] - df['ocf_lct_sector_median']) / df['ocf_lct_sector_mad']
df['opmad_sector_zscore'] = (df['opmad'] - df['opmad_sector_median']) / df['opmad_sector_mad']
df['opmbd_sector_zscore'] = (df['opmbd'] - df['opmbd_sector_median']) / df['opmbd_sector_mad']
df['pay_turn_sector_zscore'] = (df['pay_turn'] - df['pay_turn_sector_median']) / df['pay_turn_sector_mad']
df['pcf_sector_zscore'] = (df['pcf'] - df['pcf_sector_median']) / df['pcf_sector_mad']
df['pe_exi_sector_zscore'] = (df['pe_exi'] - df['pe_exi_sector_median']) / df['pe_exi_sector_mad']
df['pe_inc_sector_zscore'] = (df['pe_inc'] - df['pe_inc_sector_median']) / df['pe_inc_sector_mad']
df['pe_op_basic_sector_zscore'] = (df['pe_op_basic'] - df['pe_op_basic_sector_median']) / df['pe_op_basic_sector_mad']
df['pe_op_dil_sector_zscore'] = (df['pe_op_dil'] - df['pe_op_dil_sector_median']) / df['pe_op_dil_sector_mad']
df['PEG_1yrforward_sector_zscore'] = (df['PEG_1yrforward'] - df['PEG_1yrforward_sector_median']) / df['PEG_1yrforward_sector_mad']
df['PEG_ltgforward_sector_zscore'] = (df['PEG_ltgforward'] - df['PEG_ltgforward_sector_median']) / df['PEG_ltgforward_sector_mad']
df['PEG_trailing_sector_zscore'] = (df['PEG_trailing'] - df['PEG_trailing_sector_median']) / df['PEG_trailing_sector_mad']
df['pretret_earnat_sector_zscore'] = (df['pretret_earnat'] - df['pretret_earnat_sector_median']) / df['pretret_earnat_sector_mad']
df['pretret_noa_sector_zscore'] = (df['pretret_noa'] - df['pretret_noa_sector_median']) / df['pretret_noa_sector_mad']
df['profit_lct_sector_zscore'] = (df['profit_lct'] - df['profit_lct_sector_median']) / df['profit_lct_sector_mad']
df['ps_sector_zscore'] = (df['ps'] - df['ps_sector_median']) / df['ps_sector_mad']
df['ptb_sector_zscore'] = (df['ptb'] - df['ptb_sector_median']) / df['ptb_sector_mad']
df['ptpm_sector_zscore'] = (df['ptpm'] - df['ptpm_sector_median']) / df['ptpm_sector_mad']
df['quick_ratio_sector_zscore'] = (df['quick_ratio'] - df['quick_ratio_sector_median']) / df['quick_ratio_sector_mad']
df['rd_sale_sector_zscore'] = (df['rd_sale'] - df['rd_sale_sector_median']) / df['rd_sale_sector_mad']
df['rect_act_sector_zscore'] = (df['rect_act'] - df['rect_act_sector_median']) / df['rect_act_sector_mad']
df['rect_turn_sector_zscore'] = (df['rect_turn'] - df['rect_turn_sector_median']) / df['rect_turn_sector_mad']
df['roa_sector_zscore'] = (df['roa'] - df['roa_sector_median']) / df['roa_sector_mad']
df['roce_sector_zscore'] = (df['roce'] - df['roce_sector_median']) / df['roce_sector_mad']
df['roe_sector_zscore'] = (df['roe'] - df['roe_sector_median']) / df['roe_sector_mad']
df['sale_equity_sector_zscore'] = (df['sale_equity'] - df['sale_equity_sector_median']) / df['sale_equity_sector_mad']
df['sale_invcap_sector_zscore'] = (df['sale_invcap'] - df['sale_invcap_sector_median']) / df['sale_invcap_sector_mad']
df['sale_nwc_sector_zscore'] = (df['sale_nwc'] - df['sale_nwc_sector_median']) / df['sale_nwc_sector_mad']
df['short_debt_sector_zscore'] = (df['short_debt'] - df['short_debt_sector_median']) / df['short_debt_sector_mad']
df['staff_sale_sector_zscore'] = (df['staff_sale'] - df['staff_sale_sector_median']) / df['staff_sale_sector_mad']
df['totdebt_invcap_sector_zscore'] = (df['totdebt_invcap'] - df['totdebt_invcap_sector_median']) / df['totdebt_invcap_sector_mad']
df['dvpspm_sector_zscore'] = (df['dvpspm'] - df['dvpspm_sector_median']) / df['dvpspm_sector_mad']
df['dvpsxm_sector_zscore'] = (df['dvpsxm'] - df['dvpsxm_sector_median']) / df['dvpsxm_sector_mad']
df['dvrate_sector_zscore'] = (df['dvrate'] - df['dvrate_sector_median']) / df['dvrate_sector_mad']
df['spcsrc_sector_zscore'] = (df['spcsrc'] - df['spcsrc_sector_median']) / df['spcsrc_sector_mad']
df['alpha_sector_zscore'] = (df['alpha'] - df['alpha_sector_median']) / df['alpha_sector_mad']
df['b_hml_sector_zscore'] = (df['b_hml'] - df['b_hml_sector_median']) / df['b_hml_sector_mad']
df['b_mkt_sector_zscore'] = (df['b_mkt'] - df['b_mkt_sector_median']) / df['b_mkt_sector_mad']
df['b_smb_sector_zscore'] = (df['b_smb'] - df['b_smb_sector_median']) / df['b_smb_sector_mad']
df['b_umd_sector_zscore'] = (df['b_umd'] - df['b_umd_sector_median']) / df['b_umd_sector_mad']
df['exret_sector_zscore'] = (df['exret'] - df['exret_sector_median']) / df['exret_sector_mad']
df['ivol_sector_zscore'] = (df['ivol'] - df['ivol_sector_median']) / df['ivol_sector_mad']
df['n_sector_zscore'] = (df['n'] - df['n_sector_median']) / df['n_sector_mad']
df['R2_sector_zscore'] = (df['R2'] - df['R2_sector_median']) / df['R2_sector_mad']
df['tvol_sector_zscore'] = (df['tvol'] - df['tvol_sector_median']) / df['tvol_sector_mad']
df['BUYPCT_sector_zscore'] = (df['BUYPCT'] - df['BUYPCT_sector_median']) / df['BUYPCT_sector_mad']
df['HOLDPCT_sector_zscore'] = (df['HOLDPCT'] - df['HOLDPCT_sector_median']) / df['HOLDPCT_sector_mad']
df['MEANREC_sector_zscore'] = (df['MEANREC'] - df['MEANREC_sector_median']) / df['MEANREC_sector_mad']
df['MEDREC_sector_zscore'] = (df['MEDREC'] - df['MEDREC_sector_median']) / df['MEDREC_sector_mad']
df['NUMDOWN_sector_zscore'] = (df['NUMDOWN'] - df['NUMDOWN_sector_median']) / df['NUMDOWN_sector_mad']
df['NUMREC_sector_zscore'] = (df['NUMREC'] - df['NUMREC_sector_median']) / df['NUMREC_sector_mad']
df['NUMUP_sector_zscore'] = (df['NUMUP'] - df['NUMUP_sector_median']) / df['NUMUP_sector_mad']
df['SELLPCT_sector_zscore'] = (df['SELLPCT'] - df['SELLPCT_sector_median']) / df['SELLPCT_sector_mad']
df['STDEV_sector_zscore'] = (df['STDEV'] - df['STDEV_sector_median']) / df['STDEV_sector_mad']
# df['ACTUAL_EPS_sector_zscore'] = (df['ACTUAL_EPS'] - df['ACTUAL_EPS_sector_median']) / df['ACTUAL_EPS_sector_mad']
# df['CONSENSUS_EPS_sector_zscore'] = (df['CONSENSUS_EPS'] - df['CONSENSUS_EPS_sector_median']) / df['CONSENSUS_EPS_sector_mad']
# df['CONSENSUS_STD_sector_zscore'] = (df['CONSENSUS_STD'] - df['CONSENSUS_STD_sector_median']) / df['CONSENSUS_STD_sector_mad']
# df['NUMBER_OF_EST_sector_zscore'] = (df['NUMBER_OF_EST'] - df['NUMBER_OF_EST_sector_median']) / df['NUMBER_OF_EST_sector_mad']
# df['SURPRISE_PCT_sector_zscore'] = (df['SURPRISE_PCT'] - df['SURPRISE_PCT_sector_median']) / df['SURPRISE_PCT_sector_mad']

In [70]:
return_all_columns(df)

GVKEY   tic                         conm                industry  \
0   1045   AAL  AMERICAN AIRLINES GROUP INC             Industrials   
1   1050  CECE      CECO ENVIRONMENTAL CORP             Industrials   
2   1075   PNW   PINNACLE WEST CAPITAL CORP               Utilities   
3   1076   AAN                  AARON'S INC  Consumer Discretionary   
4   1078   ABT          ABBOTT LABORATORIES             Health Care   

  GVKEY-year-month year-month  forward_one_month_return  \
0     1045-2015-01    2015-01                 -2.200307   
1     1050-2015-01    2015-01                  3.717201   
2     1075-2015-01    2015-01                 -8.691935   
3     1076-2015-01    2015-01                 -5.843335   
4     1078-2015-01    2015-01                  5.831099   

   forward_two_month_return  forward_three_month_return  \
0                  7.763420                   -1.208663   
1                -22.185362                  -13.531142   
2                 -9.162154                  -11.947686   
3                -10.510038                    7.476464   
4                  3.507596                    4.245988   

   forward_four_month_return  forward_five_month_return  \
0                 -13.310781                 -18.292802   
1                 -16.758139                 -16.421029   
2                 -12.350540                 -18.148756   
3                  10.732369                  14.533202   
4                   9.141642                  10.219585   

   forward_six_month_return  forward_seven_month_return  \
0                -17.955212                  -20.041269   
1                -33.608937                  -28.592724   
2                -10.358036                  -13.524775   
3                 16.968733                   19.087961   
4                 14.373570                    2.189366   

   forward_eight_month_return  forward_nine_month_return  \
0                  -20.348960                  -5.190032   
1                  -39.099046                 -33.670756   
2                   -6.828139                  -6.835474   
3                   14.287472                 -21.919913   
4                   -9.250247                   1.625125   

   forward_ten_month_return  forward_eleven_month_return  \
0                -15.163603                   -12.922409   
1                -35.381039                   -42.399508   
2                 -7.055513                    -5.412555   
3                -23.104592                   -29.061055   
4                  1.897335                     1.874651   

   forward_twelve_month_return  forward_thirteen_month_return  \
0                          NaN                            NaN   
1                          NaN                            NaN   
2                          NaN                            NaN   
3                          NaN                            NaN   
4                          NaN                            NaN   

   forward_fourteen_month_return  forward_fifteen_month_return  \
0                            NaN                           NaN   
1                            NaN                           NaN   
2                            NaN                           NaN   
3                            NaN                           NaN   
4                            NaN                           NaN   

   forward_sixteen_month_return  forward_seventeen_month_return  \
0                           NaN                             NaN   
1                           NaN                             NaN   
2                           NaN                             NaN   
3                           NaN                             NaN   
4                           NaN                             NaN   

   forward_eighteen_month_return  forward_nineteen_month_return  \
0                            NaN                            NaN   
1                            NaN                            NaN   
2                            NaN          

In [71]:
df.describe()

C:\Users\shane\Anaconda3\lib\site-packages\numpy\lib\function_base.py:3817: RuntimeWarning: invalid value encountered in multiply
  x2 = take(ap, indices_above, axis=axis) * weights_above


GVKEY  forward_one_month_return  forward_two_month_return  \
count   43526.000000              43526.000000              39515.000000   
mean    70691.439852                 77.441549                 15.672907   
std     71146.683965               3376.106959               1512.722422   
min      1004.000000                -99.937364                -99.936634   
25%     12597.000000                 -6.661865                 -9.843702   
50%     26071.000000                 -0.322200                 -0.579950   
75%    147349.000000                  5.559735                  7.519293   
max    315318.000000             151022.441753             157125.773272   

       forward_three_month_return  forward_four_month_return  \
count                35510.000000               31535.000000   
mean                    75.253328                  16.217750   
std                   3353.783481                1654.273516   
min                    -99.939065                 -99.936218   
25%                    -12.913026                 -16.200097   
50%                     -0.952474                  -2.309859   
75%                      8.830979                   8.547325   
max                 156798.773006              148699.500404   

       forward_five_month_return  forward_six_month_return  \
count               27612.000000              23724.000000   
mean                   82.757921                 19.330307   
std                  3560.845173               1852.110290   
min                   -99.937598                -99.937421   
25%                   -19.956513                -21.926817   
50%                    -3.758622                 -4.649209   
75%                     8.975702                  9.023031   
max                154317.177914             143342.803615   

       forward_seven_month_return  forward_eight_month_return  \
count                19881.000000                16072.000000   
mean                    99.524942                   30.805133   
std                   3911.688183                 2282.385848   
min                    -99.939292                  -99.938462   
25%                    -24.812734                  -25.157145   
50%                     -5.235602                   -5.071970   
75%                     10.172235                   10.689899   
max                 151587.116564               150216.655646   

       forward_nine_month_return  forward_ten_month_return  \
count               12289.000000               8553.000000   
mean                  138.788900                 67.040667   
std                  4508.509912               3137.397751   
min                   -99.938894                -99.936947   
25%                   -26.096459                -25.205693   
50%                    -4.166667                 -3.165891   
75%                    13.723908                 14.950602   
max                149159.954138             147839.166850   

       forward_eleven_month_return  forward_twelve_month_return  \
count                  4834.000000                  1150.000000   
mean                    295.823191                   261.309597   
std                    6407.826714                  6053.795001   
min                     -99.940046                   -99.935543   
25%                     -28.063614                   -15.673706   
50%                      -2.719014                    -2.376238   
75%                      18.434760                     9.023669   
max                  145073.326097                145223.635295   

       forward_thirteen_month_return  forward_fourteen_month_return  \
count                    1056.000000                     963.000000   
mean                     1365.410273                      16.306716   
std                     13699.404328                     118.022617   
min                       -99.941043                     -93.545584   
25%                       -26.668558                     -16.671793   
50%                

In [72]:
# Load IBES Surprise History from Wharton
# surprise_history = pd.read_csv('c:/users/shane/Desktop/W205_Final/sample_data/Sample_Surprise_History.csv', low_memory=False)

In [73]:
# surprise_history.head(5)

In [74]:
# # Add additional time based columns
# surprise_history['anndats'] = pd.to_datetime(surprise_history['anndats'])

# # Create year
# surprise_history['year'] = surprise_history['anndats'].dt.year

# # Create month
# surprise_history['month'] = surprise_history['anndats'].dt.month

# surprise_history['year-month'] = surprise_history['anndats'].apply(lambda x: x.strftime('%Y-%m'))

# surprise_history["TIC-year-month"] = surprise_history["OFTIC"].map(str) + "-" + surprise_history["year-month"]

In [75]:
# pd.value_counts(surprise_history['FISCALP'])

In [76]:
# pd.value_counts(surprise_history['MEASURE'])

In [77]:
# surprise_history.head(5)

In [78]:
# surprise_history = surprise_history.drop('year', 1)
# surprise_history = surprise_history.drop('month', 1)
# surprise_history = surprise_history.drop('year-month', 1)

In [79]:
# # Individual features for each surprise metric and duration
# SAL_ANN = surprise_history.loc[(surprise_history.MEASURE == 'SAL') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NET_ANN = surprise_history.loc[(surprise_history.MEASURE == 'NET') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EPS_ANN = surprise_history.loc[(surprise_history.MEASURE == 'EPS') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# PRE_ANN = surprise_history.loc[(surprise_history.MEASURE == 'PRE') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBI_ANN = surprise_history.loc[(surprise_history.MEASURE == 'EBI') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# GPS_ANN = surprise_history.loc[(surprise_history.MEASURE == 'GPS') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBT_ANN = surprise_history.loc[(surprise_history.MEASURE == 'EBT') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# DPS_ANN = surprise_history.loc[(surprise_history.MEASURE == 'DPS') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# GRM_ANN = surprise_history.loc[(surprise_history.MEASURE == 'GRM') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NAV_ANN = surprise_history.loc[(surprise_history.MEASURE == 'NAV') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# BPS_ANN = surprise_history.loc[(surprise_history.MEASURE == 'BPS') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CPX_ANN = surprise_history.loc[(surprise_history.MEASURE == 'CPX') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ROE_ANN = surprise_history.loc[(surprise_history.MEASURE == 'ROE') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CPS_ANN = surprise_history.loc[(surprise_history.MEASURE == 'CPS') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NDT_ANN = surprise_history.loc[(surprise_history.MEASURE == 'NDT') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ROA_ANN = surprise_history.loc[(surprise_history.MEASURE == 'ROA') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ENT_ANN = surprise_history.loc[(surprise_history.MEASURE == 'ENT') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# OPR_ANN = surprise_history.loc[(surprise_history.MEASURE == 'OPR') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBS_ANN = surprise_history.loc[(surprise_history.MEASURE == 'EBS') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CSH_ANN = surprise_history.loc[(surprise_history.MEASURE == 'CSH') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# FFO_ANN = surprise_history.loc[(surprise_history.MEASURE == 'FFO') & (surprise_history.FISCALP == 'ANN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# SAL_QTR = surprise_history.loc[(surprise_history.MEASURE == 'SAL') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NET_QTR = surprise_history.loc[(surprise_history.MEASURE == 'NET') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EPS_QTR = surprise_history.loc[(surprise_history.MEASURE == 'EPS') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# PRE_QTR = surprise_history.loc[(surprise_history.MEASURE == 'PRE') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBI_QTR = surprise_history.loc[(surprise_history.MEASURE == 'EBI') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# GPS_QTR = surprise_history.loc[(surprise_history.MEASURE == 'GPS') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBT_QTR = surprise_history.loc[(surprise_history.MEASURE == 'EBT') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# DPS_QTR = surprise_history.loc[(surprise_history.MEASURE == 'DPS') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# GRM_QTR = surprise_history.loc[(surprise_history.MEASURE == 'GRM') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NAV_QTR = surprise_history.loc[(surprise_history.MEASURE == 'NAV') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# BPS_QTR = surprise_history.loc[(surprise_history.MEASURE == 'BPS') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CPX_QTR = surprise_history.loc[(surprise_history.MEASURE == 'CPX') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ROE_QTR = surprise_history.loc[(surprise_history.MEASURE == 'ROE') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CPS_QTR = surprise_history.loc[(surprise_history.MEASURE == 'CPS') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NDT_QTR = surprise_history.loc[(surprise_history.MEASURE == 'NDT') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ROA_QTR = surprise_history.loc[(surprise_history.MEASURE == 'ROA') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ENT_QTR = surprise_history.loc[(surprise_history.MEASURE == 'ENT') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# OPR_QTR = surprise_history.loc[(surprise_history.MEASURE == 'OPR') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBS_QTR = surprise_history.loc[(surprise_history.MEASURE == 'EBS') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CSH_QTR = surprise_history.loc[(surprise_history.MEASURE == 'CSH') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# FFO_QTR = surprise_history.loc[(surprise_history.MEASURE == 'FFO') & (surprise_history.FISCALP == 'QTR'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# SAL_SAN = surprise_history.loc[(surprise_history.MEASURE == 'SAL') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NET_SAN = surprise_history.loc[(surprise_history.MEASURE == 'NET') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EPS_SAN = surprise_history.loc[(surprise_history.MEASURE == 'EPS') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# PRE_SAN = surprise_history.loc[(surprise_history.MEASURE == 'PRE') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBI_SAN = surprise_history.loc[(surprise_history.MEASURE == 'EBI') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# GPS_SAN = surprise_history.loc[(surprise_history.MEASURE == 'GPS') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBT_SAN = surprise_history.loc[(surprise_history.MEASURE == 'EBT') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# DPS_SAN = surprise_history.loc[(surprise_history.MEASURE == 'DPS') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# GRM_SAN = surprise_history.loc[(surprise_history.MEASURE == 'GRM') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NAV_SAN = surprise_history.loc[(surprise_history.MEASURE == 'NAV') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# BPS_SAN = surprise_history.loc[(surprise_history.MEASURE == 'BPS') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CPX_SAN = surprise_history.loc[(surprise_history.MEASURE == 'CPX') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ROE_SAN = surprise_history.loc[(surprise_history.MEASURE == 'ROE') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CPS_SAN = surprise_history.loc[(surprise_history.MEASURE == 'CPS') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NDT_SAN = surprise_history.loc[(surprise_history.MEASURE == 'NDT') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ROA_SAN = surprise_history.loc[(surprise_history.MEASURE == 'ROA') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ENT_SAN = surprise_history.loc[(surprise_history.MEASURE == 'ENT') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# OPR_SAN = surprise_history.loc[(surprise_history.MEASURE == 'OPR') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBS_SAN = surprise_history.loc[(surprise_history.MEASURE == 'EBS') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CSH_SAN = surprise_history.loc[(surprise_history.MEASURE == 'CSH') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# FFO_SAN = surprise_history.loc[(surprise_history.MEASURE == 'FFO') & (surprise_history.FISCALP == 'SAN'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# SAL_LTG = surprise_history.loc[(surprise_history.MEASURE == 'SAL') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NET_LTG = surprise_history.loc[(surprise_history.MEASURE == 'NET') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EPS_LTG = surprise_history.loc[(surprise_history.MEASURE == 'EPS') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# PRE_LTG = surprise_history.loc[(surprise_history.MEASURE == 'PRE') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBI_LTG = surprise_history.loc[(surprise_history.MEASURE == 'EBI') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# GPS_LTG = surprise_history.loc[(surprise_history.MEASURE == 'GPS') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBT_LTG = surprise_history.loc[(surprise_history.MEASURE == 'EBT') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# DPS_LTG = surprise_history.loc[(surprise_history.MEASURE == 'DPS') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# GRM_LTG = surprise_history.loc[(surprise_history.MEASURE == 'GRM') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NAV_LTG = surprise_history.loc[(surprise_history.MEASURE == 'NAV') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# BPS_LTG = surprise_history.loc[(surprise_history.MEASURE == 'BPS') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CPX_LTG = surprise_history.loc[(surprise_history.MEASURE == 'CPX') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ROE_LTG = surprise_history.loc[(surprise_history.MEASURE == 'ROE') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CPS_LTG = surprise_history.loc[(surprise_history.MEASURE == 'CPS') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# NDT_LTG = surprise_history.loc[(surprise_history.MEASURE == 'NDT') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ROA_LTG = surprise_history.loc[(surprise_history.MEASURE == 'ROA') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# ENT_LTG = surprise_history.loc[(surprise_history.MEASURE == 'ENT') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# OPR_LTG = surprise_history.loc[(surprise_history.MEASURE == 'OPR') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# EBS_LTG = surprise_history.loc[(surprise_history.MEASURE == 'EBS') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# CSH_LTG = surprise_history.loc[(surprise_history.MEASURE == 'CSH') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

# FFO_LTG = surprise_history.loc[(surprise_history.MEASURE == 'FFO') & (surprise_history.FISCALP == 'LTG'), ['actual', 'surpmean', 'surpstdev', 'suescore', 'TIC-year-month']]

In [80]:
# # Rename the columns before merging
# SAL_ANN = SAL_ANN.rename(columns={'actual': 'actual_SAL_ANN', 'surpmean': 'surpmean_SAL_ANN', 'surpstdev': 'surpstdev_SAL_ANN', 'suescore': 'suescore_SAL_ANN'})

# NET_ANN = NET_ANN.rename(columns={'actual': 'actual_NET_ANN', 'surpmean': 'surpmean_NET_ANN', 'surpstdev': 'surpstdev_NET_ANN', 'suescore': 'suescore_NET_ANN'})

# EPS_ANN = EPS_ANN.rename(columns={'actual': 'actual_EPS_ANN', 'surpmean': 'surpmean_EPS_ANN', 'surpstdev': 'surpstdev_EPS_ANN', 'suescore': 'suescore_EPS_ANN'})

# PRE_ANN = PRE_ANN.rename(columns={'actual': 'actual_PRE_ANN', 'surpmean': 'surpmean_PRE_ANN', 'surpstdev': 'surpstdev_PRE_ANN', 'suescore': 'suescore_PRE_ANN'})

# EBI_ANN = EBI_ANN.rename(columns={'actual': 'actual_EBI_ANN', 'surpmean': 'surpmean_EBI_ANN', 'surpstdev': 'surpstdev_EBI_ANN', 'suescore': 'suescore_EBI_ANN'})

# GPS_ANN = GPS_ANN.rename(columns={'actual': 'actual_GPS_ANN', 'surpmean': 'surpmean_GPS_ANN', 'surpstdev': 'surpstdev_GPS_ANN', 'suescore': 'suescore_GPS_ANN'})

# EBT_ANN = EBT_ANN.rename(columns={'actual': 'actual_EBT_ANN', 'surpmean': 'surpmean_EBT_ANN', 'surpstdev': 'surpstdev_EBT_ANN', 'suescore': 'suescore_EBT_ANN'})

# DPS_ANN = DPS_ANN.rename(columns={'actual': 'actual_DPS_ANN', 'surpmean': 'surpmean_DPS_ANN', 'surpstdev': 'surpstdev_DPS_ANN', 'suescore': 'suescore_DPS_ANN'})

# GRM_ANN = GRM_ANN.rename(columns={'actual': 'actual_GRM_ANN', 'surpmean': 'surpmean_GRM_ANN', 'surpstdev': 'surpstdev_GRM_ANN', 'suescore': 'suescore_GRM_ANN'})

# NAV_ANN = NAV_ANN.rename(columns={'actual': 'actual_NAV_ANN', 'surpmean': 'surpmean_NAV_ANN', 'surpstdev': 'surpstdev_NAV_ANN', 'suescore': 'suescore_NAV_ANN'})

# BPS_ANN = BPS_ANN.rename(columns={'actual': 'actual_BPS_ANN', 'surpmean': 'surpmean_BPS_ANN', 'surpstdev': 'surpstdev_BPS_ANN', 'suescore': 'suescore_BPS_ANN'})

# CPX_ANN = CPX_ANN.rename(columns={'actual': 'actual_CPX_ANN', 'surpmean': 'surpmean_CPX_ANN', 'surpstdev': 'surpstdev_CPX_ANN', 'suescore': 'suescore_CPX_ANN'})

# ROE_ANN = ROE_ANN.rename(columns={'actual': 'actual_ROE_ANN', 'surpmean': 'surpmean_ROE_ANN', 'surpstdev': 'surpstdev_ROE_ANN', 'suescore': 'suescore_ROE_ANN'})

# CPS_ANN = CPS_ANN.rename(columns={'actual': 'actual_CPS_ANN', 'surpmean': 'surpmean_CPS_ANN', 'surpstdev': 'surpstdev_CPS_ANN', 'suescore': 'suescore_CPS_ANN'})

# NDT_ANN = NDT_ANN.rename(columns={'actual': 'actual_NDT_ANN', 'surpmean': 'surpmean_NDT_ANN', 'surpstdev': 'surpstdev_NDT_ANN', 'suescore': 'suescore_NDT_ANN'})

# ROA_ANN = ROA_ANN.rename(columns={'actual': 'actual_ROA_ANN', 'surpmean': 'surpmean_ROA_ANN', 'surpstdev': 'surpstdev_ROA_ANN', 'suescore': 'suescore_ROA_ANN'})

# ENT_ANN = ENT_ANN.rename(columns={'actual': 'actual_ENT_ANN', 'surpmean': 'surpmean_ENT_ANN', 'surpstdev': 'surpstdev_ENT_ANN', 'suescore': 'suescore_ENT_ANN'})

# OPR_ANN = OPR_ANN.rename(columns={'actual': 'actual_OPR_ANN', 'surpmean': 'surpmean_OPR_ANN', 'surpstdev': 'surpstdev_OPR_ANN', 'suescore': 'suescore_OPR_ANN'})

# EBS_ANN = EBS_ANN.rename(columns={'actual': 'actual_EBS_ANN', 'surpmean': 'surpmean_EBS_ANN', 'surpstdev': 'surpstdev_EBS_ANN', 'suescore': 'suescore_EBS_ANN'})

# CSH_ANN = CSH_ANN.rename(columns={'actual': 'actual_CSH_ANN', 'surpmean': 'surpmean_CSH_ANN', 'surpstdev': 'surpstdev_CSH_ANN', 'suescore': 'suescore_CSH_ANN'})

# FFO_ANN = FFO_ANN.rename(columns={'actual': 'actual_FFO_ANN', 'surpmean': 'surpmean_FFO_ANN', 'surpstdev': 'surpstdev_FFO_ANN', 'suescore': 'suescore_FFO_ANN'})

# SAL_QTR = SAL_QTR.rename(columns={'actual': 'actual_SAL_QTR', 'surpmean': 'surpmean_SAL_QTR', 'surpstdev': 'surpstdev_SAL_QTR', 'suescore': 'suescore_SAL_QTR'})

# NET_QTR = NET_QTR.rename(columns={'actual': 'actual_NET_QTR', 'surpmean': 'surpmean_NET_QTR', 'surpstdev': 'surpstdev_NET_QTR', 'suescore': 'suescore_NET_QTR'})

# EPS_QTR = EPS_QTR.rename(columns={'actual': 'actual_EPS_QTR', 'surpmean': 'surpmean_EPS_QTR', 'surpstdev': 'surpstdev_EPS_QTR', 'suescore': 'suescore_EPS_QTR'})

# PRE_QTR = PRE_QTR.rename(columns={'actual': 'actual_PRE_QTR', 'surpmean': 'surpmean_PRE_QTR', 'surpstdev': 'surpstdev_PRE_QTR', 'suescore': 'suescore_PRE_QTR'})

# EBI_QTR = EBI_QTR.rename(columns={'actual': 'actual_EBI_QTR', 'surpmean': 'surpmean_EBI_QTR', 'surpstdev': 'surpstdev_EBI_QTR', 'suescore': 'suescore_EBI_QTR'})

# GPS_QTR = GPS_QTR.rename(columns={'actual': 'actual_GPS_QTR', 'surpmean': 'surpmean_GPS_QTR', 'surpstdev': 'surpstdev_GPS_QTR', 'suescore': 'suescore_GPS_QTR'})

# EBT_QTR = EBT_QTR.rename(columns={'actual': 'actual_EBT_QTR', 'surpmean': 'surpmean_EBT_QTR', 'surpstdev': 'surpstdev_EBT_QTR', 'suescore': 'suescore_EBT_QTR'})

# DPS_QTR = DPS_QTR.rename(columns={'actual': 'actual_DPS_QTR', 'surpmean': 'surpmean_DPS_QTR', 'surpstdev': 'surpstdev_DPS_QTR', 'suescore': 'suescore_DPS_QTR'})

# GRM_QTR = GRM_QTR.rename(columns={'actual': 'actual_GRM_QTR', 'surpmean': 'surpmean_GRM_QTR', 'surpstdev': 'surpstdev_GRM_QTR', 'suescore': 'suescore_GRM_QTR'})

# NAV_QTR = NAV_QTR.rename(columns={'actual': 'actual_NAV_QTR', 'surpmean': 'surpmean_NAV_QTR', 'surpstdev': 'surpstdev_NAV_QTR', 'suescore': 'suescore_NAV_QTR'})

# BPS_QTR = BPS_QTR.rename(columns={'actual': 'actual_BPS_QTR', 'surpmean': 'surpmean_BPS_QTR', 'surpstdev': 'surpstdev_BPS_QTR', 'suescore': 'suescore_BPS_QTR'})

# CPX_QTR = CPX_QTR.rename(columns={'actual': 'actual_CPX_QTR', 'surpmean': 'surpmean_CPX_QTR', 'surpstdev': 'surpstdev_CPX_QTR', 'suescore': 'suescore_CPX_QTR'})

# ROE_QTR = ROE_QTR.rename(columns={'actual': 'actual_ROE_QTR', 'surpmean': 'surpmean_ROE_QTR', 'surpstdev': 'surpstdev_ROE_QTR', 'suescore': 'suescore_ROE_QTR'})

# CPS_QTR = CPS_QTR.rename(columns={'actual': 'actual_CPS_QTR', 'surpmean': 'surpmean_CPS_QTR', 'surpstdev': 'surpstdev_CPS_QTR', 'suescore': 'suescore_CPS_QTR'})

# NDT_QTR = NDT_QTR.rename(columns={'actual': 'actual_NDT_QTR', 'surpmean': 'surpmean_NDT_QTR', 'surpstdev': 'surpstdev_NDT_QTR', 'suescore': 'suescore_NDT_QTR'})

# ROA_QTR = ROA_QTR.rename(columns={'actual': 'actual_ROA_QTR', 'surpmean': 'surpmean_ROA_QTR', 'surpstdev': 'surpstdev_ROA_QTR', 'suescore': 'suescore_ROA_QTR'})

# ENT_QTR = ENT_QTR.rename(columns={'actual': 'actual_ENT_QTR', 'surpmean': 'surpmean_ENT_QTR', 'surpstdev': 'surpstdev_ENT_QTR', 'suescore': 'suescore_ENT_QTR'})

# OPR_QTR = OPR_QTR.rename(columns={'actual': 'actual_OPR_QTR', 'surpmean': 'surpmean_OPR_QTR', 'surpstdev': 'surpstdev_OPR_QTR', 'suescore': 'suescore_OPR_QTR'})

# EBS_QTR = EBS_QTR.rename(columns={'actual': 'actual_EBS_QTR', 'surpmean': 'surpmean_EBS_QTR', 'surpstdev': 'surpstdev_EBS_QTR', 'suescore': 'suescore_EBS_QTR'})

# CSH_QTR = CSH_QTR.rename(columns={'actual': 'actual_CSH_QTR', 'surpmean': 'surpmean_CSH_QTR', 'surpstdev': 'surpstdev_CSH_QTR', 'suescore': 'suescore_CSH_QTR'})

# FFO_QTR = FFO_QTR.rename(columns={'actual': 'actual_FFO_QTR', 'surpmean': 'surpmean_FFO_QTR', 'surpstdev': 'surpstdev_FFO_QTR', 'suescore': 'suescore_FFO_QTR'})

# SAL_SAN = SAL_SAN.rename(columns={'actual': 'actual_SAL_SAN', 'surpmean': 'surpmean_SAL_SAN', 'surpstdev': 'surpstdev_SAL_SAN', 'suescore': 'suescore_SAL_SAN'})

# NET_SAN = NET_SAN.rename(columns={'actual': 'actual_NET_SAN', 'surpmean': 'surpmean_NET_SAN', 'surpstdev': 'surpstdev_NET_SAN', 'suescore': 'suescore_NET_SAN'})

# EPS_SAN = EPS_SAN.rename(columns={'actual': 'actual_EPS_SAN', 'surpmean': 'surpmean_EPS_SAN', 'surpstdev': 'surpstdev_EPS_SAN', 'suescore': 'suescore_EPS_SAN'})

# PRE_SAN = PRE_SAN.rename(columns={'actual': 'actual_PRE_SAN', 'surpmean': 'surpmean_PRE_SAN', 'surpstdev': 'surpstdev_PRE_SAN', 'suescore': 'suescore_PRE_SAN'})

# EBI_SAN = EBI_SAN.rename(columns={'actual': 'actual_EBI_SAN', 'surpmean': 'surpmean_EBI_SAN', 'surpstdev': 'surpstdev_EBI_SAN', 'suescore': 'suescore_EBI_SAN'})

# GPS_SAN = GPS_SAN.rename(columns={'actual': 'actual_GPS_SAN', 'surpmean': 'surpmean_GPS_SAN', 'surpstdev': 'surpstdev_GPS_SAN', 'suescore': 'suescore_GPS_SAN'})

# EBT_SAN = EBT_SAN.rename(columns={'actual': 'actual_EBT_SAN', 'surpmean': 'surpmean_EBT_SAN', 'surpstdev': 'surpstdev_EBT_SAN', 'suescore': 'suescore_EBT_SAN'})

# DPS_SAN = DPS_SAN.rename(columns={'actual': 'actual_DPS_SAN', 'surpmean': 'surpmean_DPS_SAN', 'surpstdev': 'surpstdev_DPS_SAN', 'suescore': 'suescore_DPS_SAN'})

# GRM_SAN = GRM_SAN.rename(columns={'actual': 'actual_GRM_SAN', 'surpmean': 'surpmean_GRM_SAN', 'surpstdev': 'surpstdev_GRM_SAN', 'suescore': 'suescore_GRM_SAN'})

# NAV_SAN = NAV_SAN.rename(columns={'actual': 'actual_NAV_SAN', 'surpmean': 'surpmean_NAV_SAN', 'surpstdev': 'surpstdev_NAV_SAN', 'suescore': 'suescore_NAV_SAN'})

# BPS_SAN = BPS_SAN.rename(columns={'actual': 'actual_BPS_SAN', 'surpmean': 'surpmean_BPS_SAN', 'surpstdev': 'surpstdev_BPS_SAN', 'suescore': 'suescore_BPS_SAN'})

# CPX_SAN = CPX_SAN.rename(columns={'actual': 'actual_CPX_SAN', 'surpmean': 'surpmean_CPX_SAN', 'surpstdev': 'surpstdev_CPX_SAN', 'suescore': 'suescore_CPX_SAN'})

# ROE_SAN = ROE_SAN.rename(columns={'actual': 'actual_ROE_SAN', 'surpmean': 'surpmean_ROE_SAN', 'surpstdev': 'surpstdev_ROE_SAN', 'suescore': 'suescore_ROE_SAN'})

# CPS_SAN = CPS_SAN.rename(columns={'actual': 'actual_CPS_SAN', 'surpmean': 'surpmean_CPS_SAN', 'surpstdev': 'surpstdev_CPS_SAN', 'suescore': 'suescore_CPS_SAN'})

# NDT_SAN = NDT_SAN.rename(columns={'actual': 'actual_NDT_SAN', 'surpmean': 'surpmean_NDT_SAN', 'surpstdev': 'surpstdev_NDT_SAN', 'suescore': 'suescore_NDT_SAN'})

# ROA_SAN = ROA_SAN.rename(columns={'actual': 'actual_ROA_SAN', 'surpmean': 'surpmean_ROA_SAN', 'surpstdev': 'surpstdev_ROA_SAN', 'suescore': 'suescore_ROA_SAN'})

# ENT_SAN = ENT_SAN.rename(columns={'actual': 'actual_ENT_SAN', 'surpmean': 'surpmean_ENT_SAN', 'surpstdev': 'surpstdev_ENT_SAN', 'suescore': 'suescore_ENT_SAN'})

# OPR_SAN = OPR_SAN.rename(columns={'actual': 'actual_OPR_SAN', 'surpmean': 'surpmean_OPR_SAN', 'surpstdev': 'surpstdev_OPR_SAN', 'suescore': 'suescore_OPR_SAN'})

# EBS_SAN = EBS_SAN.rename(columns={'actual': 'actual_EBS_SAN', 'surpmean': 'surpmean_EBS_SAN', 'surpstdev': 'surpstdev_EBS_SAN', 'suescore': 'suescore_EBS_SAN'})

# CSH_SAN = CSH_SAN.rename(columns={'actual': 'actual_CSH_SAN', 'surpmean': 'surpmean_CSH_SAN', 'surpstdev': 'surpstdev_CSH_SAN', 'suescore': 'suescore_CSH_SAN'})

# FFO_SAN = FFO_SAN.rename(columns={'actual': 'actual_FFO_SAN', 'surpmean': 'surpmean_FFO_SAN', 'surpstdev': 'surpstdev_FFO_SAN', 'suescore': 'suescore_FFO_SAN'})

# SAL_LTG = SAL_LTG.rename(columns={'actual': 'actual_SAL_LTG', 'surpmean': 'surpmean_SAL_LTG', 'surpstdev': 'surpstdev_SAL_LTG', 'suescore': 'suescore_SAL_LTG'})

# NET_LTG = NET_LTG.rename(columns={'actual': 'actual_NET_LTG', 'surpmean': 'surpmean_NET_LTG', 'surpstdev': 'surpstdev_NET_LTG', 'suescore': 'suescore_NET_LTG'})

# EPS_LTG = EPS_LTG.rename(columns={'actual': 'actual_EPS_LTG', 'surpmean': 'surpmean_EPS_LTG', 'surpstdev': 'surpstdev_EPS_LTG', 'suescore': 'suescore_EPS_LTG'})

# PRE_LTG = PRE_LTG.rename(columns={'actual': 'actual_PRE_LTG', 'surpmean': 'surpmean_PRE_LTG', 'surpstdev': 'surpstdev_PRE_LTG', 'suescore': 'suescore_PRE_LTG'})

# EBI_LTG = EBI_LTG.rename(columns={'actual': 'actual_EBI_LTG', 'surpmean': 'surpmean_EBI_LTG', 'surpstdev': 'surpstdev_EBI_LTG', 'suescore': 'suescore_EBI_LTG'})

# GPS_LTG = GPS_LTG.rename(columns={'actual': 'actual_GPS_LTG', 'surpmean': 'surpmean_GPS_LTG', 'surpstdev': 'surpstdev_GPS_LTG', 'suescore': 'suescore_GPS_LTG'})

# EBT_LTG = EBT_LTG.rename(columns={'actual': 'actual_EBT_LTG', 'surpmean': 'surpmean_EBT_LTG', 'surpstdev': 'surpstdev_EBT_LTG', 'suescore': 'suescore_EBT_LTG'})

# DPS_LTG = DPS_LTG.rename(columns={'actual': 'actual_DPS_LTG', 'surpmean': 'surpmean_DPS_LTG', 'surpstdev': 'surpstdev_DPS_LTG', 'suescore': 'suescore_DPS_LTG'})

# GRM_LTG = GRM_LTG.rename(columns={'actual': 'actual_GRM_LTG', 'surpmean': 'surpmean_GRM_LTG', 'surpstdev': 'surpstdev_GRM_LTG', 'suescore': 'suescore_GRM_LTG'})

# NAV_LTG = NAV_LTG.rename(columns={'actual': 'actual_NAV_LTG', 'surpmean': 'surpmean_NAV_LTG', 'surpstdev': 'surpstdev_NAV_LTG', 'suescore': 'suescore_NAV_LTG'})

# BPS_LTG = BPS_LTG.rename(columns={'actual': 'actual_BPS_LTG', 'surpmean': 'surpmean_BPS_LTG', 'surpstdev': 'surpstdev_BPS_LTG', 'suescore': 'suescore_BPS_LTG'})

# CPX_LTG = CPX_LTG.rename(columns={'actual': 'actual_CPX_LTG', 'surpmean': 'surpmean_CPX_LTG', 'surpstdev': 'surpstdev_CPX_LTG', 'suescore': 'suescore_CPX_LTG'})

# ROE_LTG = ROE_LTG.rename(columns={'actual': 'actual_ROE_LTG', 'surpmean': 'surpmean_ROE_LTG', 'surpstdev': 'surpstdev_ROE_LTG', 'suescore': 'suescore_ROE_LTG'})

# CPS_LTG = CPS_LTG.rename(columns={'actual': 'actual_CPS_LTG', 'surpmean': 'surpmean_CPS_LTG', 'surpstdev': 'surpstdev_CPS_LTG', 'suescore': 'suescore_CPS_LTG'})

# NDT_LTG = NDT_LTG.rename(columns={'actual': 'actual_NDT_LTG', 'surpmean': 'surpmean_NDT_LTG', 'surpstdev': 'surpstdev_NDT_LTG', 'suescore': 'suescore_NDT_LTG'})

# ROA_LTG = ROA_LTG.rename(columns={'actual': 'actual_ROA_LTG', 'surpmean': 'surpmean_ROA_LTG', 'surpstdev': 'surpstdev_ROA_LTG', 'suescore': 'suescore_ROA_LTG'})

# ENT_LTG = ENT_LTG.rename(columns={'actual': 'actual_ENT_LTG', 'surpmean': 'surpmean_ENT_LTG', 'surpstdev': 'surpstdev_ENT_LTG', 'suescore': 'suescore_ENT_LTG'})

# OPR_LTG = OPR_LTG.rename(columns={'actual': 'actual_OPR_LTG', 'surpmean': 'surpmean_OPR_LTG', 'surpstdev': 'surpstdev_OPR_LTG', 'suescore': 'suescore_OPR_LTG'})

# EBS_LTG = EBS_LTG.rename(columns={'actual': 'actual_EBS_LTG', 'surpmean': 'surpmean_EBS_LTG', 'surpstdev': 'surpstdev_EBS_LTG', 'suescore': 'suescore_EBS_LTG'})

# CSH_LTG = CSH_LTG.rename(columns={'actual': 'actual_CSH_LTG', 'surpmean': 'surpmean_CSH_LTG', 'surpstdev': 'surpstdev_CSH_LTG', 'suescore': 'suescore_CSH_LTG'})

# FFO_LTG = FFO_LTG.rename(columns={'actual': 'actual_FFO_LTG', 'surpmean': 'surpmean_FFO_LTG', 'surpstdev': 'surpstdev_FFO_LTG', 'suescore': 'suescore_FFO_LTG'})

In [81]:
# # Add features to main dataframe
# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(NET_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(EPS_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(PRE_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(EBI_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(GPS_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(EBT_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(DPS_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(GRM_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(NAV_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(BPS_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(CPX_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(ROE_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(CPS_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(NDT_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(ROA_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(ENT_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(OPR_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(EBS_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(CSH_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

# df = df.merge(FFO_ANN, on='TIC-year-month', how='left', suffixes=('', '_y'))

In [82]:
# df.head(5)

In [83]:
# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_SAL_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_NET_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EPS_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_PRE_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EBI_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_GPS_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EBT_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_DPS_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_GRM_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_NAV_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_BPS_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_CPX_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_ROE_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_CPS_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_NDT_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_ROA_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_ENT_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_OPR_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EBS_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_CSH_QRT'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_FFO_QRT'))

In [84]:
# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_SAL_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_NET_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EPS_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_PRE_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EBI_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_GPS_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EBT_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_DPS_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_GRM_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_NAV_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_BPS_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_CPX_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_ROE_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_CPS_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_NDT_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_ROA_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_ENT_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_OPR_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EBS_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_CSH_SAN'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_FFO_SAN'))

In [85]:
# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_SAL_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_NET_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EPS_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_PRE_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EBI_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_GPS_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EBT_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_DPS_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_GRM_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_NAV_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_BPS_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_CPX_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_ROE_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_CPS_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_NDT_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_ROA_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_ENT_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_OPR_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_EBS_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_CSH_LTG'))

# df = df.merge(SAL_ANN, on='TIC-year-month', how='left', suffixes=('', '_FFO_LTG'))

In [86]:
# # Overview of merged dataset
# print("Number of columns:", len(df.columns))
# print("Number of rows:", len(df.index))
# df.head(5)